## Objetivo


+ Este notebook tem como objetivo realizar uma Análise Exploratória dos Dados (EAD) de bases do Ifood. 
+ O objetivo é responder:
    + `O que fizeram os clientes darem Churn?`
    + `Qual a importância dos eventos (push, compra, acesso, entre outros) ao longo da vida do cliente?`

+ As bases são:
    + `ORDERS - Informações sobre os pedidos realizados.`
    + `MARKETING PUSH FULL - Notificações PUSH ao longo de 6 meses (Junho-Dezembro/2019).`
    + `CUSTOMER SEGMENTATION - Segmentação do cliente.`
    + `ORDERS WITH COST REVENUE - Informações sobre o pedido relacionado, onde verifica-se se o mesmo gerou custo ou receita.`
    + `SESSION VISITS - Comportamento de uso do app.`

    
Criado por Jaime Mishima e Ariel Vicente </br>

## Imports

In [3]:
from pyspark.sql.functions import udf, count, when, isnull, col, mean, sum, max, min, stddev, count, trim, lower, split, explode
from pyspark.sql.functions import *
from pyspark.mllib.stat import Statistics

# tratamento de datas
from pyspark.sql.functions import datediff, to_date, to_timestamp, from_utc_timestamp, round, dayofweek, month

# para o groupby e lag column
import pyspark.sql.functions as f
from pyspark.sql.window import Window
from pyspark.sql import SQLContext
from pyspark.sql.functions import lit

# para a remoção de missing:
from functools import reduce

# para ajuste de type de arrays
from pyspark.sql.types import ArrayType, StringType

# para correlacao
import matplotlib.pyplot as plt
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation

## Help Functions

In [5]:
from pyspark.sql.functions import count, when, isnull, col
def contar_missing(df):
  """Realiza a contagem da quantidade de missing que existe dentro de um dataframe.
  Args:
    df - Dataframe Spark
  Returns:
    Data Frame spark com apenas 1 linha com a contagem de missing para cada variável.
  """
  aux = []
  for c in df.columns:
    aux.append(count(when(isnull(c), c)).alias(c))
  return df.select(aux)

def percent_missing(df):
  total_linhas = df.count()
  df = contar_missing(df)
  colunas = df.columns
  total_missing = list(df.first().asDict().values())
  valores = zip(colunas, total_missing)
  
  df_aux = spark.createDataFrame(valores, ['variaveis', 'total_missing'])
  df_aux = df_aux.withColumn('perc_missing', col('total_missing') *100/total_linhas)
  return df_aux

In [6]:
def percentByCol(df, group_column):
  """Retorna o groupby de uma coluna `col` de um dataframe `df`
  Args:
    df - Dataframe Spark
    group_column - Nome da coluna do dataframe df
  Returns:
    Data Frame spark com o groupby da coluna `col` e uma coluna com o percentual
  """
  return df.groupby(group_column)\
           .count()\
           .withColumnRenamed('count', 'cnt_per_group')\
           .withColumn('percent', f.col('cnt_per_group')*100/f.sum('cnt_per_group').over(Window.partitionBy()))\
           .orderBy('percent', ascending=False)

In [7]:
# Disclaimer: baseado em https://stackoverflow.com/questions/46944493/removing-duplicate-columns-after-a-df-join-in-spark
def join_removing_repeated(df1, df2, cond, how='left'):
    """Retorna o dataframe resultado do join de `df1` e `df2`
    Args:
      df1 - dataframe 1
      df2 - dataframe 2
      cond - chaves para realizar o join
      how - tipo de join (default left)
    Returns:
      Data Frame resultado do join removendo as colunas repetidas
    """
    df = df1.join(df2, cond, how=how)
    repeated_columns = [c for c in df1.columns if c in df2.columns]
    for col in repeated_columns:
        df = df.drop(df2[col])
    return df

In [8]:
def limpeza(x):
  """Retorna a string x após eliminação de caracteres indesejados
    Args:
      x - string
    Returns:
      String tratada
    """
  return x.replace('"', '').replace('\\', '').replace('[', '').replace(']', '')

udf_limpeza = udf(limpeza, StringType()) # create an udf based on limpeza function

In [9]:
from pyspark.sql.functions import udf
push_range = udf(lambda pushes: '1- < 20' if pushes < 20 else 
                                 '2- 20-60' if (pushes >= 20 and pushes < 60) else
                                 '3- 60-100' if (pushes >= 60 and pushes < 100) else
                                 '4- 100-140' if (pushes >= 100 and pushes < 140) else
                                 '5- 140-180' if (pushes >= 140 and pushes < 180) else
                                 '6- 180-220' if (pushes >= 180 and pushes < 220) else
                                 '7- 220-260' if (pushes >= 220 and pushes < 260) else
                                 '8- 260-300' if (pushes >= 260 and pushes < 300) else
                                 '9- 300+'  if (pushes >= 300) else '')

In [10]:
from pyspark.sql.functions import udf
order_range = udf(lambda orders: '1- < 5' if orders < 5 else 
                                 '2- 5-10' if (orders >= 5 and orders < 10) else
                                 '3- 0-15' if (orders >= 10 and orders < 15) else
                                 '4- 15-20' if (orders >= 15 and orders < 20) else
                                 '5- 20-25' if (orders >= 20 and orders < 25) else
                                 '6- 25-30' if (orders >= 25 and orders < 30) else
                                 '7- 30-35' if (orders >= 30 and orders < 35) else
                                 '8- 35-40' if (orders >= 35 and orders < 40) else
                                 '9- 40+'  if (orders >= 40) else '')

In [11]:
import seaborn as sns
def plot_corr_matrix(correlations,attr,fig_no, figsize=[15,10]):
  """Retorna o heatmap de uma lista de listas com as correlacoes de variaveis
  Args:
    correlations - lista de lista com as correlacoes
    attr - lista com os nomes das variaveis
    fig_no - If not provided, a new figure will be created, and the figure number will be incremented (para o plt.figure)
    figsize 0- tamanho do heatmap
  Returns:
    Heatmap com a matriz de correlacao
    """
  fig=plt.figure(fig_no, figsize=figsize)
  ax=fig.add_subplot(111)
  ax.set_title("Correlacao Variaveis")
  ax = sns.heatmap(correlations, cmap="YlGnBu")
  indice = list(range(1, len(attr)+1))
  indice = [str(s) + ' - ' for s in indice]
  res = [i + j for i, j in zip(indice, attr)] 
  #ax.set_xticks(range(len(filter_colunas_order)))
  ax.set_yticklabels(res)
  plt.yticks(rotation=0) 
  plt.show()

## Leitura das Bases

In [13]:
root_dir = '/dbfs/FileStore/ifood'
dbutils.fs.ls(f'{root_dir}')
df_customer_segmentation = spark.read.parquet(f'{root_dir}/customer_segmentation')
df_orders = spark.read.parquet(f'{root_dir}/orders')
df_orders_with_cost_revenue = spark.read.parquet(f'{root_dir}/orders_with_cost_revenue')
df_sessions_visits = spark.read.parquet(f'{root_dir}/sessions_visits')
df_marketing_push_full = spark.read.parquet(f'{root_dir}/marketing_push_full')

print('Customer segmentation:     ', df_customer_segmentation.count(), '   linhas e ', len(df_customer_segmentation.columns), ' colunas')
print('Orders:                    ', df_orders.count(), '   linhas e ', len(df_orders.columns), ' colunas')
print('Orders with cost revenue:  ', df_orders_with_cost_revenue.count(), '   linhas e ', len(df_orders_with_cost_revenue.columns), ' colunas')
print('Visits:                    ', df_sessions_visits.count(), '   linhas e ', len(df_sessions_visits.columns), ' colunas')
print('Pushes:                    ', df_marketing_push_full.count(), ' linhas e ', len(df_marketing_push_full.columns), ' colunas')

Customer segmentation: 210364 linhas e 50 colunas
Orders: 492138 linhas e 43 colunas
Orders with cost revenue: 492138 linhas e 8 colunas
Visits: 463620 linhas e 21 colunas
Pushes: 28426642 linhas e 21 colunas

## Análise Exploratória das Bases (EAD)

### 1. Pushes

#### Leitura e caching

In [17]:
display(df_marketing_push_full)

event_channel event_name brand sample_type user_id external_user_id event_time_utc3 platform campaign_id campaign_name message_variation_channel canvas_name canvas_step_id canvas_is_first_step canvas_first_step_name canvas_step_name canvas_real_step_name canvas_step_index canvas_tags send_id event_date push received iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-08-29T18:31:10.000Z android 23e2e9bf-61ae-48aa-8e24-85d8f2348b21 2019-08-29 / ANDROID / 20190829MIDIAKITKAS android_push null null null null null null null null null 2019-08-29T00:00:00.000Z push send iFood Brasil sample 5ac3121c8e5b4b5696ac49dc 290070089ba4bc832a39ffdb7f3bc7e70cb4e7746bc51163946e0045d548277e 2019-11-13T12:38:00.000Z ios null null null null null 0.0 null null null null null null 2019-11-13T00:00:00.000Z push send iFood Brasil sample 5ac2c99c059e9ee7e5eed43b 0753a6e30f7b58265e00becd06423d17181aa22d43f51ec34ebe9a2af0be3ab3 2019-10-10T11:31:02.000Z ios c3858a3b-1eea-4ab8-99ca-5b0166a9fb14 2019-10-10 / IOS / Almoço / Cidades DFN Geral ios_push null null 0.0 null null null null null null 2019-10-10T00:00:00.000Z push received iFood Brasil sample 5ac36acd409f7734a97df5b9 8468bb60ea7888a33a3506e4f3d2b541afca6651bde242ed49a75da8cce67a68 2019-10-27T21:05:31.000Z android e5b7abaf-eafa-4a2e-bde5-62965fefa0f5 2019-10-27 / ANDROID / Ativos / Ceia - KA / CUPOM android_push null null null null null null null null null 2019-10-28T00:00:00.000Z push send iFood Brasil sample 5ac3654ad75e5a3c29fb256f 6cbda064947aec380ac7c459de0902fc0182b23dcbaa59ee7317705927f52eee 2019-10-28T11:30:49.000Z android 2398c143-4f12-4541-afd9-06bb94cb7b8a 2019-10-28 / ANDROID / Ativos / Almoço - Light / CUPOM android_push null null 0.0 null null null null null null 2019-10-28T00:00:00.000Z push send iFood Brasil sample 5ac311e58e5b4b411df4c647 28b2fe193b22c7a4026afb94d4bd3104a296606b51ea107da1ad4a22611d2f2b 2019-10-25T12:12:49.000Z android null null null null null 0.0 null null null null null null 2019-10-25T00:00:00.000Z push received iFood Brasil sample 5ac35d290b97ee7b6f067992 54fcbbfab48d41e79c96471d17a570f1fb2d65d1bcc1c81a8547fc1a953edb4e 2019-10-15T18:12:44.000Z android fe0beda0-401f-4783-9ac3-45faa723a4bc 2019-10-15 / ANDROID / Ativos / Jantar / CUPOM android_push null null null null null null null null null 2019-10-15T00:00:00.000Z push send iFood Brasil sample 5b3b5459614b1ee0f8772035 bf3eea65d3cc69a040517cfbc9783ab5015500fb61afb015143aaf128fa78611 2019-07-15T18:27:53.000Z ios 110ab169-e1af-47c1-860f-7beea100459e 2019-07-15 / iOS / Ativos / Jantar / CUPOM / R$8 ios_push null null 0.0 null null null null null null 2019-07-15T00:00:00.000Z push received iFood Brasil sample 5c8ea2111668ab61c397680c 39ed72e5d00f25f46eefd5c566ef8ca352864a6f990800ad0dce219a1a150588 2019-08-18T18:19:45.000Z ios 310dfc26-55e7-41b7-9b26-d492122bffa6 2019-08-18 / iOS / Ativos / Jantar / CUPOM ios_push null null null null null null null null null 2019-08-18T00:00:00.000Z push send iFood Brasil sample 5af112133d477eece72791e2 71f0d523744e4211a3810b2d8530d68b0f75ede4e629b29a667055ab955573e0 2019-06-06T18:04:12.000Z android a38ea1b2-5073-4fb9-a895-35734b4e8f92 2019-06-06 / ANDROID / 20190606RECRAG android_push null null 0.0 null null null null null null 2019-06-06T00:00:00.000Z push received iFood Brasil sample 5ac368a9495e759a5f5e6670 7b0a3ea834e6dbd8352fe6950ead14e8f63579522279a616648da0daeb01bf87 2019-06-06T11:43:13.000Z ios 0d12cf49-f9da-4716-a819-ec0aba5f43e8 2019-06-06 / IOS / Almoço - Entrega Grátis / CUPOM ios_push null null null null null null null null null 2019-06-06T00:00:00.000Z push received iFood Brasil sample 5be8cf4086d18a401d3e9c8b c8b3a0ac1bb36ab6462f73b7c7bf04da40c61b95be074ee9388b8f5788008f65 2019-11-03T18:18:22.000Z ios 78ffbfd9-a333-4d24-a99a-0fc74ac991ef 2019-11-03 / iOS / Ativos / Jantar / CUPOM ios_push null null null null null null null null null 2019-11-03T00:00:00.000Z push send iFood Brasil sample 5ac37c03355f65ec1d8a5

In [18]:
# Adicionar no cache (100% em memoria)
df_marketing_push_full.cache()

Out[6]: DataFrame[event_channel: string, event_name: string, brand: string, sample_type: string, user_id: string, external_user_id: string, event_time_utc3: string, platform: string, campaign_id: string, campaign_name: string, message_variation_channel: string, canvas_name: string, canvas_step_id: string, canvas_is_first_step: double, canvas_first_step_name: string, canvas_step_name: string, canvas_real_step_name: string, canvas_step_index: double, canvas_tags: string, send_id: double, event_date: string]

In [19]:
df_marketing_push_full.dtypes

Out[8]: [('event_channel', 'string'),
 ('event_name', 'string'),
 ('brand', 'string'),
 ('sample_type', 'string'),
 ('user_id', 'string'),
 ('external_user_id', 'string'),
 ('event_time_utc3', 'string'),
 ('platform', 'string'),
 ('campaign_id', 'string'),
 ('campaign_name', 'string'),
 ('message_variation_channel', 'string'),
 ('canvas_name', 'string'),
 ('canvas_step_id', 'string'),
 ('canvas_is_first_step', 'double'),
 ('canvas_first_step_name', 'string'),
 ('canvas_step_name', 'string'),
 ('canvas_real_step_name', 'string'),
 ('canvas_step_index', 'double'),
 ('canvas_tags', 'string'),
 ('send_id', 'double'),
 ('event_date', 'string')]

#### Tratamento de Missings

In [21]:
colunas_pushes_missing = percent_missing(df_marketing_push_full).orderBy('perc_missing', ascending=False)
display(colunas_pushes_missing)

variaveis total_missing perc_missing send_id 28426642 100.0 canvas_tags 28405316 99.92497882796005 canvas_first_step_name 28405316 99.92497882796005 canvas_step_name 27543807 96.89433947210507 canvas_real_step_name 27543807 96.89433947210507 canvas_step_index 27543807 96.89433947210507 canvas_step_id 27543369 96.89279866401385 canvas_name 27542381 96.88932305124186 canvas_is_first_step 13672374 48.097042204281465 message_variation_channel 6042795 21.25750554708502 campaign_name 4638287 16.31668981513891 campaign_id 4638285 16.316682779485525 platform 157142 0.5527983220810956 brand 0 0.0 sample_type 0 0.0 event_date 0 0.0 user_id 0 0.0 event_channel 0 0.0 event_time_utc3 0 0.0 external_user_id 0 0.0 event_name 0 0.0

Removendo colunas com missing share acima de 22%

In [23]:
# Selecionar linhas de um dataframe > 22%
# Pega as linhas da coluna variaveis filtradas pelo threshold acima e converte para uma lista
# Remove colunas do dataframe passando essa lista

thresholdMissingPushes = 22
df_columns_to_drop = colunas_pushes_missing.filter(colunas_pushes_missing['perc_missing'] > thresholdMissingPushes).select('variaveis')
list_columns_to_drop = list([row[0] for row in df_columns_to_drop.collect()])
df_mpf = df_marketing_push_full.drop(*list_columns_to_drop)
display(df_mpf)

event_channel event_name brand sample_type user_id external_user_id event_time_utc3 platform campaign_id campaign_name message_variation_channel event_date push received iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-08-29T18:31:10.000Z android 23e2e9bf-61ae-48aa-8e24-85d8f2348b21 2019-08-29 / ANDROID / 20190829MIDIAKITKAS android_push 2019-08-29T00:00:00.000Z push send iFood Brasil sample 5ac3121c8e5b4b5696ac49dc 290070089ba4bc832a39ffdb7f3bc7e70cb4e7746bc51163946e0045d548277e 2019-11-13T12:38:00.000Z ios null null null 2019-11-13T00:00:00.000Z push send iFood Brasil sample 5ac2c99c059e9ee7e5eed43b 0753a6e30f7b58265e00becd06423d17181aa22d43f51ec34ebe9a2af0be3ab3 2019-10-10T11:31:02.000Z ios c3858a3b-1eea-4ab8-99ca-5b0166a9fb14 2019-10-10 / IOS / Almoço / Cidades DFN Geral ios_push 2019-10-10T00:00:00.000Z push received iFood Brasil sample 5ac36acd409f7734a97df5b9 8468bb60ea7888a33a3506e4f3d2b541afca6651bde242ed49a75da8cce67a68 2019-10-27T21:05:31.000Z android e5b7abaf-eafa-4a2e-bde5-62965fefa0f5 2019-10-27 / ANDROID / Ativos / Ceia - KA / CUPOM android_push 2019-10-28T00:00:00.000Z push send iFood Brasil sample 5ac3654ad75e5a3c29fb256f 6cbda064947aec380ac7c459de0902fc0182b23dcbaa59ee7317705927f52eee 2019-10-28T11:30:49.000Z android 2398c143-4f12-4541-afd9-06bb94cb7b8a 2019-10-28 / ANDROID / Ativos / Almoço - Light / CUPOM android_push 2019-10-28T00:00:00.000Z push send iFood Brasil sample 5ac311e58e5b4b411df4c647 28b2fe193b22c7a4026afb94d4bd3104a296606b51ea107da1ad4a22611d2f2b 2019-10-25T12:12:49.000Z android null null null 2019-10-25T00:00:00.000Z push received iFood Brasil sample 5ac35d290b97ee7b6f067992 54fcbbfab48d41e79c96471d17a570f1fb2d65d1bcc1c81a8547fc1a953edb4e 2019-10-15T18:12:44.000Z android fe0beda0-401f-4783-9ac3-45faa723a4bc 2019-10-15 / ANDROID / Ativos / Jantar / CUPOM android_push 2019-10-15T00:00:00.000Z push send iFood Brasil sample 5b3b5459614b1ee0f8772035 bf3eea65d3cc69a040517cfbc9783ab5015500fb61afb015143aaf128fa78611 2019-07-15T18:27:53.000Z ios 110ab169-e1af-47c1-860f-7beea100459e 2019-07-15 / iOS / Ativos / Jantar / CUPOM / R$8 ios_push 2019-07-15T00:00:00.000Z push received iFood Brasil sample 5c8ea2111668ab61c397680c 39ed72e5d00f25f46eefd5c566ef8ca352864a6f990800ad0dce219a1a150588 2019-08-18T18:19:45.000Z ios 310dfc26-55e7-41b7-9b26-d492122bffa6 2019-08-18 / iOS / Ativos / Jantar / CUPOM ios_push 2019-08-18T00:00:00.000Z push send iFood Brasil sample 5af112133d477eece72791e2 71f0d523744e4211a3810b2d8530d68b0f75ede4e629b29a667055ab955573e0 2019-06-06T18:04:12.000Z android a38ea1b2-5073-4fb9-a895-35734b4e8f92 2019-06-06 / ANDROID / 20190606RECRAG android_push 2019-06-06T00:00:00.000Z push received iFood Brasil sample 5ac368a9495e759a5f5e6670 7b0a3ea834e6dbd8352fe6950ead14e8f63579522279a616648da0daeb01bf87 2019-06-06T11:43:13.000Z ios 0d12cf49-f9da-4716-a819-ec0aba5f43e8 2019-06-06 / IOS / Almoço - Entrega Grátis / CUPOM ios_push 2019-06-06T00:00:00.000Z push received iFood Brasil sample 5be8cf4086d18a401d3e9c8b c8b3a0ac1bb36ab6462f73b7c7bf04da40c61b95be074ee9388b8f5788008f65 2019-11-03T18:18:22.000Z ios 78ffbfd9-a333-4d24-a99a-0fc74ac991ef 2019-11-03 / iOS / Ativos / Jantar / CUPOM ios_push 2019-11-03T00:00:00.000Z push send iFood Brasil sample 5ac37c03355f65ec1d8a5a2d c70467fbd28e9d0f600884f7286ee486762ff9d09403eea0db6efe3f4efaa30d 2019-09-11T16:01:35.000Z android 8c7e01e3-83de-48bf-a971-9b748bf34384 2019-09-11 / ANDROID / RECKAOAKBERRY android_push 2019-09-11T00:00:00.000Z push send iFood Brasil sample 5b453c1583292056a77b1e1a 410a8273d97b2e5350b5ea9f4d58ec47a2af5cb06d6ecff19251904a23c006ab 2019-08-07T11:18:40.000Z ios 494bb80c-597f-450c-8918-7d408e730c37 2019-08-07 / iOS / Ativos / Almoço / CUPOM ios_push 2019-08-07T00:00:00.000Z push send iFood Brasil sample 5bcb9e8e3a261160aea8f267 624788cb92ca1af84964b759ca3e3a8a886f4fa9c861f559a9706d59b0a5f580 2019-11-08T15:41:53.000Z android d170c128-e873-434f-a2b2-add2a57756e9 2019-11-08 / AN

Ao remover algumas colunas, ficam linhas duplicadas. Optamos por remover linhas repetidas. Assim temos **20.87M de registros**.

In [25]:
df_mpf = df_mpf.dropDuplicates()
print(df_mpf.count())

20875331

Inputa unknown para colunas categóricas com missing abaixo do threshold (22%). E a média para colunas numéricas (nao se aplica nessa base)

In [27]:
# Para as colunas que nao remover, separar em categoricas e numericas
df_columns_missing = colunas_pushes_missing.filter(
                                                   (colunas_pushes_missing['perc_missing'] <= thresholdMissingPushes) &
                                                   (colunas_pushes_missing['perc_missing'] > 0)
                                                  ).select('variaveis')
list_df_columns_missing = list([row[0] for row in df_columns_missing.collect()])

filter_colunas_numericas = [x[0] for x in df_mpf[list_df_columns_missing].dtypes if x[1] in ('double', 'int', 'long')]
filter_colunas_categoricas = [x[0] for x in df_mpf[list_df_columns_missing].dtypes if x[1] not in ('double', 'int', 'long')]

# Inputar unknown para colunas categoricas
for coluna in filter_colunas_categoricas:
  df_mpf = df_mpf.fillna('unknown', subset=[coluna])

# Inputar media para colunas numericas
for coluna in filter_colunas_numericas:
  media = df_mpf.agg(mean(coluna)).collect()[0][0]
  df_mpf = df_mpf.fillna(media, subset=[coluna])

In [28]:
display(df_mpf)

event_channel event_name brand sample_type user_id external_user_id event_time_utc3 platform campaign_id campaign_name message_variation_channel event_date push send iFood Brasil sample 5ace75b521ee9f180b96da24 a7a46fa1dfabc8fd9c027a51aba18c9332d07652541b7438ce6e6ce642a8d52e 2019-10-02T18:19:25.000Z android cdbb7816-880d-4406-9381-efc610863be2 2019-10-02 / ANDROID / Ativos / Jantar / CUPOM android_push 2019-10-02T00:00:00.000Z push received iFood Brasil sample 5ac311afbf062b4020f7ec08 2873048204304c8485e4fa6191a8e1b43f7b28abca24f8d823842b201a79b93e 2019-10-27T22:14:39.000Z ios unknown unknown unknown 2019-10-28T00:00:00.000Z push received iFood Brasil sample 5c0db994820f229401fa42e5 241e219b53e9cdfe733c654de5c496091713f0fee51b75ff43e103a66c15a05c 2019-11-27T11:29:26.000Z android e3474335-2525-4977-917f-66cee3a2577c 2019-11-27 / ANDROID / Ativos / Almoço - Light / CUPOM android_push 2019-11-27T00:00:00.000Z push send iFood Brasil sample 5c107c378caa6b789e5c38b7 432f7c45ede3ffe2f2c949089757eaaeb718c236aac7cec56803cd8cfd7a2234 2019-06-08T19:49:02.000Z android bd3daf82-e117-40d1-9d5c-7656f1362b06 2019-06-08 / ANDROID / 20190608RECACAOPONTUALKA android_push 2019-06-08T00:00:00.000Z push send iFood Brasil sample 5ac3120e832920cddd4eaf58 28f8af69956d26080ce13750e08a481a5379cb431517588cf77458f966219b7c 2019-06-11T11:53:35.000Z android unknown unknown unknown 2019-06-11T00:00:00.000Z push send iFood Brasil sample 5b4534172d15ef563929d170 6bc6e8a3cc7a785eb2397d928d2b937e57577aa4b99ec8e579be933a05324707 2019-11-01T10:15:13.000Z android unknown unknown unknown 2019-11-01T00:00:00.000Z push received iFood Brasil sample 5ac36f3c6ee329d3b8c09401 980a7fb7dfd8f5a9b67ae624c31cd53ec849c22587294e9157e6e73b1b7f17db 2019-10-04T11:19:44.000Z ios a9942a70-ed0b-4a8c-ac8b-1fe77cdc53ef 2019-10-04 / iOS / Ativos / Almoço - Light / CUPOM ios_push 2019-10-04T00:00:00.000Z push received iFood Brasil sample 5cdd81c0cb756f6e6039acdd a5a7937ffa49421f5c31069576c2576fce5e9459fa58fa74447db494dc0ffa75 2019-10-10T13:30:53.000Z android unknown unknown unknown 2019-10-10T00:00:00.000Z push received iFood Brasil sample 5ac364f65ca872eae7a61ada 6b4241b4a0f280284c25eaa2116f823e8bd524453c4eae369d3e047ac5af231e 2019-08-28T11:24:23.000Z ios 06eb0625-bf5c-404e-9d0a-8ed869295262 2019-08-28 / iOS / Ativos / Almoço / CUPOM unknown 2019-08-28T00:00:00.000Z push send iFood Brasil sample 5ac363668e504d030bb8da33 64b6c18a195a6305aac0274603498f113531bb740091fb9fddaa3d5eac6284c4 2019-06-19T20:24:54.000Z android unknown unknown unknown 2019-06-19T00:00:00.000Z push send iFood Brasil sample 5bffd598d8e702e88ab94487 09d7db86386e4f06c993cd2a9c8f92a8156579520cf5ffafcdfcf4a86a92432c 2019-10-23T20:05:00.000Z android unknown unknown unknown 2019-10-23T00:00:00.000Z push send iFood Brasil sample 5ac2cb0a495e7503fd623f08 0c0de7d005bb25d210eebd5c5a114cdc73760768bf88a7579861724151d830eb 2019-06-11T18:49:31.000Z ios c7100ad6-7f78-4dd1-bceb-9ec57996f7ea 2019-06-11 / iOS / Ativos 12 - Recuperação / Jantar / CUPOM ios_push 2019-06-11T00:00:00.000Z push received iFood Brasil sample 5ac37c410e560db820df209a c82f09b24e2b599d5323bc98bd0e79b9e6d76ece0bd93d91d87a994c4e5fc6a9 2019-10-09T18:24:09.000Z ios 2c5dea16-3193-4fe5-bd11-0c0d61b55b91 2019-10-09 / iOS / Ativos / Jantar / CUPOM ios_push 2019-10-09T00:00:00.000Z push send iFood Brasil sample 5ac38b3f4d6e4540e1b367d9 fd9d011ddf48d92d99bf1304274323fc2e84fd1dc835180523d21fa38fe69078 2019-06-16T18:42:09.000Z ios bab37793-8c80-42e1-ae1a-23883a67a596 2019-06-16 / iOS / Ativos / Jantar / CUPOM ios_push 2019-06-16T00:00:00.000Z push send iFood Brasil sample 5cfbd0694e08436bc6bc85de 16fa37186d9b3224c02b453158ef8ffb43d26d1e70b86d4e8c4cedc7a9d1ca5b 2019-07-01T19:04:00.000Z ios f8806b74-fd0d-4590-8a27-3e39f32c87cb 2019-07-01 / iOS / Ativos / Jantar / CUPOM ios_push 2019-07-01T00:00:00.000Z push send iFood Brasil sample 5be2414bb7ad7d4cf3579e23 50bfe866497289821130af3a899ee66e3232085ae33b920f8717535b53ed03f4 2019-06-04T18:58:11.000Z android 2b3d3893-3da3-49d8-b8d0

#### Tratamento de Datas

In [30]:
from pyspark.sql.functions import col
from pyspark.sql.functions import datediff, to_date, to_timestamp, from_utc_timestamp, round, dayofweek, month

# importante: transformar primeiro para timestamp, depois para date!!!
df_mpf = df_mpf.withColumn('event_time_utc3', from_utc_timestamp('event_time_utc3', 'UTC'))\
               .withColumn('event_date', from_utc_timestamp('event_date', 'UTC'))\
               .withColumn('event_date', to_date('event_date', 'YYYY-MM-DD'))\
               .withColumn('event_month', month('event_date'))\
               .withColumn('event_dayofweek', dayofweek('event_date'))
display(df_mpf)

event_channel event_name brand sample_type user_id external_user_id event_time_utc3 platform campaign_id campaign_name message_variation_channel event_date event_month event_dayofweek push send iFood Brasil sample 5ace75b521ee9f180b96da24 a7a46fa1dfabc8fd9c027a51aba18c9332d07652541b7438ce6e6ce642a8d52e 2019-10-02T18:19:25.000+0000 android cdbb7816-880d-4406-9381-efc610863be2 2019-10-02 / ANDROID / Ativos / Jantar / CUPOM android_push 2019-10-02 10 4 push received iFood Brasil sample 5ac311afbf062b4020f7ec08 2873048204304c8485e4fa6191a8e1b43f7b28abca24f8d823842b201a79b93e 2019-10-27T22:14:39.000+0000 ios unknown unknown unknown 2019-10-28 10 2 push received iFood Brasil sample 5ac3715ce41e7ec8dde33d2c a181461278b074497cf5d77e52df00a08c4d9b49e1df06e39f1dedc57adc8ef8 2019-07-11T09:05:57.000+0000 ios 26e91b0c-82eb-44f5-bf71-b26433d72f06 2019-07-11 / IOS / QuintaLoop ios_push 2019-07-11 7 5 push send iFood Brasil sample 5ac377a2c9f0895b04a64d57 b2d08ff98a22fe924d36ada7e978fee273e47b7aebf73be7239e451e3b5c3899 2019-10-21T11:22:17.000+0000 android 5af14d08-14de-4d95-94b9-679c8d6ab928 2019-10-21 / ANDROID / Ativos / Almoço / CUPOM android_push 2019-10-21 10 2 push send iFood Brasil sample 5ac3811471666591e0c8194e de39115680e14a3a3911662d39eacfec58baf5d951b824cd0215253fc2fbf3d2 2019-07-23T16:06:18.000+0000 android 5aa11544-ea25-4994-a8ef-0372145b7185 2019-07-23 / ANDROID / To Go android_push 2019-07-23 7 3 push received iFood Brasil sample 5ac32e060dd604a8b6234369 4920aea87c9e21be10de324bed9859c1e2239e06baa991a32917bd3875e561b5 2019-10-23T11:35:31.000+0000 android 80e60538-075a-454a-91dc-154c126a58ee 2019-10-23 / ANDROID / Ativos / Almoço / CUPOM android_push 2019-10-23 10 4 push send iFood Brasil sample 5b8b53d454a5ee2b3f0a8c97 c59ab1024f99eec1c84e0584153d70bfd4dc16125bcc093e938238168c300870 2019-08-24T14:50:13.000+0000 android unknown unknown unknown 2019-08-24 8 7 push send iFood Brasil sample 5b26fba83f5ceac7b64e8726 f7261bddc98a298dc833a428befecc6adf6d97b8f7c3755236152e88bfefda69 2019-11-17T11:42:24.000+0000 android d4a9ef4f-fa17-43e0-884c-986a208e1ef6 2019-11-17 / ANDROID / Ativos / Almoço - Light / CUPOM android_push 2019-11-17 11 1 push received iFood Brasil sample 5b5270f2376c97e2f20f0e55 36a6962fb680aa7109f7468a3894b754d887a59a1187cc5ab6860efe73290fa4 2019-07-30T18:21:32.000+0000 ios f94965dc-d829-4e73-88f2-e2a6ecac2585 2019-07-30 / iOS / Ativos / Jantar / CUPOM unknown 2019-07-30 7 3 push send iFood Brasil sample 5c0bc1bb2760acf76c3df3d3 e0aff996db63f9fcf152311ec931abec2736c42a5dbc5e7137686d79845d2258 2019-09-30T15:57:31.000+0000 ios unknown unknown unknown 2019-09-30 9 2 push received iFood Brasil sample 5ac364dbb56f2c8f38a3c9ed 6acd718bac2a0322df36c049bccbb457f54bcae5dcbe14b427fc478d07495117 2019-06-16T18:14:31.000+0000 ios bab37793-8c80-42e1-ae1a-23883a67a596 2019-06-16 / iOS / Ativos / Jantar / CUPOM ios_push 2019-06-16 6 1 push received iFood Brasil sample 5cbb40f727c7ae21421432b5 21d242eeb9d0b76aed7568e836e822aeda24f6ff95a3f1e2a9f54ee4eb98bb2b 2019-08-25T11:47:20.000+0000 ios 3661dfb2-3770-490b-b240-ebe3d9f111ce 2019-08-25 / iOS / Ativos / Almoço - Light / CUPOM ios_push 2019-08-25 8 1 push received iFood Brasil sample 5ce8918e64e87d7dd318f656 028acbc90ef27a5e837ac2418eb9699debd649564c340ec5fea6a6012bb87324 2019-08-07T18:07:27.000+0000 android 89acf1d2-990e-4797-b65a-e5d61d34f561 2019-08-07 / ANDROID / Ativos / Jantar / CUPOM android_push 2019-08-07 8 4 push received iFood Brasil sample 5b95a7211caa7fff8c2759dd 69c84971da2571ca9f4cc5f824d4a94a954224b0d2636f6b60e392c0e1a675b8 2019-10-18T15:12:57.000+0000 ios 745c36c4-ecb0-4bd5-b2d1-398dc2256089 2019-10-18 / iOS / Ativos / Lanche da Tarde / CUPOM ios_push 2019-10-18 10 6 push received iFood Brasil sample 5ac36e30447a5b84e08bc50a 93659a2c802808b700d6a77e2898241ebf334e5393cefcb4626daed5a84f6556 2019-10-31T20:42:02.000+0000 android 2b9ac2b5-feec-4ece-9df2-54d9b0d6c4d3 2019-10-31 / ANDROID / Jantar / Loop (Agendamento Awareness) android_push 2019-10-31 10 5 push send iFood Br

In [31]:
df_mpf_checkpoint = df_mpf # checkpoint para nao ter que rodar as celulas anteriores
df_mpf.cache()

Out[80]: DataFrame[event_channel: string, event_name: string, brand: string, sample_type: string, user_id: string, external_user_id: string, event_time_utc3: timestamp, platform: string, campaign_id: string, campaign_name: string, message_variation_channel: string, event_date: date, event_month: int, event_dayofweek: int]

In [32]:
df_mpf.dtypes

Out[81]: [('event_channel', 'string'),
 ('event_name', 'string'),
 ('brand', 'string'),
 ('sample_type', 'string'),
 ('user_id', 'string'),
 ('external_user_id', 'string'),
 ('event_time_utc3', 'timestamp'),
 ('platform', 'string'),
 ('campaign_id', 'string'),
 ('campaign_name', 'string'),
 ('message_variation_channel', 'string'),
 ('event_date', 'date'),
 ('event_month', 'int'),
 ('event_dayofweek', 'int')]

#### Análise Variáveis Qualitativas

In [34]:
variaveis_categoricas = [x[0] for x in df_mpf.dtypes if x[1] not in ('double', 'int', 'long')]
variaveis_categoricas

Out[82]: ['event_channel',
 'event_name',
 'brand',
 'sample_type',
 'user_id',
 'external_user_id',
 'event_time_utc3',
 'platform',
 'campaign_id',
 'campaign_name',
 'message_variation_channel',
 'event_date']

##### Canais

Somente temos um canal nessa base: pushes. Portanto essa variável pode ser removida no modelo

In [37]:
# Distribuicao por canais
display(df_mpf.groupby('event_channel').count())

event_channel count push 20875331

##### Brand

Somente temos uma marca nessa base: iFood Brasil. Portanto essa variável pode ser removida no modelo.

In [40]:
display(df_mpf.groupby('brand').count())

brand count iFood Brasil 20875331

##### Message Variation Channel

Talvez usar essa variável como proxy para quando a plataforma não é identificada.

In [43]:
display(df_mpf.groupby('platform','message_variation_channel').count())

platform message_variation_channel count android android_push 10154789 unknown ios_push 47077 unknown unknown 46104 unknown android_push 63956 ios ios_push 6332398 android unknown 2539141 ios unknown 1691866

##### Tipos de Eventos

+10.3M de pushes foram enviados. Destes 98.3% foram recebidos. Apenas 3.16% foram clicados e bounce da base foi de 4.4%.

In [46]:
# Tipos de eventos
import pyspark.sql.functions as f
from pyspark.sql.window import Window
from pyspark.sql import SQLContext

my_window = Window.partitionBy().orderBy(col('percent').desc())
aux = percentByCol(df_mpf, 'event_name')

df = aux.withColumn('prev_value', f.lag(aux.cnt_per_group).over(my_window))\
        .withColumn("Funnel", (f.col("cnt_per_group") * 100 / f.col("prev_value")))
display(df)

event_name cnt_per_group percent prev_value Funnel send 10355984 49.608717581532 null null received 10182446 48.77741100248902 10355984 98.3242731931606 click 322629 1.5455036377626779 10182446 3.1684823076891346 bounce 14272 0.06836777821630709 322629 4.423656893831614

##### Platforma

60.8% dos pushes foram para Android, 38.4% para ios. Unknowns representaram apenas 0.75%

In [49]:
display(percentByCol(df_mpf, 'platform'))

platform cnt_per_group percent android 12693930 60.80828131539567 ios 8024264 38.43897852446028 unknown 157137 0.7527401601440475

##### Sample Type

Aparentemente 0.75% dos pushes representam um universal control group

In [52]:
display(percentByCol(df_mpf, 'sample_type'))

sample_type cnt_per_group percent sample 20718194 99.24725983985596 control 157137 0.7527401601440475

#### Análise Variáveis Quantitativas

##### Event Month

Agosto foi o mês com menor volume de pushes recebidos (11.1% da base) e dezembro foi o mês com maior volume (17.5% da base)

In [56]:
display(percentByCol(df_mpf.filter(df_mpf['event_name'] == 'received'), 'event_month').orderBy('event_month'))

event_month cnt_per_group percent 6 1271095 12.483199027031423 7 1741702 17.10494708245936 8 1128464 11.082445219940277 9 1185351 11.641122378650474 10 1612874 15.839750095409295 11 1459939 14.337802527997694 12 1783021 17.510733668511474

##### Day of Week

Finais de semana tem menor volume de pushes (talvez a demanda é maior e não precisa de muitos incentivos). Quintas tiveram o maior volume de envios (16.4% da base)

In [59]:
display(percentByCol(df_mpf.filter(df_mpf['event_name'] == 'received'), 'event_dayofweek').orderBy('event_dayofweek'))

event_dayofweek cnt_per_group percent 1 1313607 12.90070185493741 2 1538769 15.111978006070448 3 1534154 15.066654907867914 4 1479915 14.53398328849473 5 1676006 16.459758293832348 6 1411231 13.859449880706462 7 1228764 12.067473768090693

##### User-id

In [61]:
# Histograma de frequencia de pushes recebidos por usuário
df_mpf_sample = df_mpf.sample(withReplacement=False, fraction=1.0, seed=42)
aux = df_mpf_sample\
            .filter(df_mpf_sample['event_name'] == 'received')\
            .groupby('user_id')\
            .count()\
            .withColumnRenamed('count', 'lifecycle_pushes')\
            .groupby('lifecycle_pushes')\
            .count()\
            .withColumnRenamed('count', 'count_users')\
            .withColumn('percent', f.col('count_users')*100/f.sum('count_users').over(Window.partitionBy()))\
            .orderBy('lifecycle_pushes', ascending=False)

In [62]:
display(aux)

lifecycle_pushes count_users percent 476 1 0.0035767937620716788 374 1 0.0035767937620716788 348 1 0.0035767937620716788 346 1 0.0035767937620716788 332 1 0.0035767937620716788 330 2 0.0071535875241433575 328 1 0.0035767937620716788 324 1 0.0035767937620716788 322 1 0.0035767937620716788 318 2 0.0071535875241433575 315 1 0.0035767937620716788 310 1 0.0035767937620716788 304 1 0.0035767937620716788 302 2 0.0071535875241433575 297 2 0.0071535875241433575 295 1 0.0035767937620716788 293 1 0.0035767937620716788 291 1 0.0035767937620716788 285 2 0.0071535875241433575 281 1 0.0035767937620716788 278 1 0.0035767937620716788 277 1 0.0035767937620716788 276 1 0.0035767937620716788 272 1 0.0035767937620716788 271 4 0.014307175048286715 270 1 0.0035767937620716788 269 2 0.0071535875241433575 268 2 0.0071535875241433575 266 2 0.0071535875241433575 265 1 0.0035767937620716788 264 1 0.0035767937620716788 263 1 0.0035767937620716788 261 1 0.0035767937620716788 259 1 0.0035767937620716788 258 2 0.0071535875241433575 257 1 0.0035767937620716788 255 1 0.0035767937620716788 254 1 0.0035767937620716788 253 1 0.0035767937620716788 252 2 0.0071535875241433575 250 5 0.017883968810358395 249 3 0.010730381286215037 248 1 0.0035767937620716788 247 1 0.0035767937620716788 246 2 0.0071535875241433575 244 1 0.0035767937620716788 243 1 0.0035767937620716788 242 2 0.0071535875241433575 241 4 0.014307175048286715 240 3 0.010730381286215037 239 2 0.0071535875241433575 238 4 0.014307175048286715 237 1 0.0035767937620716788 236 3 0.010730381286215037 235 5 0.017883968810358395 234 4 0.014307175048286715 233 5 0.017883968810358395 232 2 0.0071535875241433575 231 3 0.010730381286215037 230 3 0.010730381286215037 229 2 0.0071535875241433575 228 4 0.014307175048286715 227 3 0.010730381286215037 226 7 0.02503755633450175 225 3 0.010730381286215037 224 4 0.014307175048286715 223 3 0.010730381286215037 222 5 0.017883968810358395 221 6 0.021460762572430073 220 6 0.021460762572430073 219 7 0.02503755633450175 218 9 0.03219114385864511 217 2 0.0071535875241433575 216 5 0.017883968810358395 215 8 0.02861435009657343 214 5 0.017883968810358395 213 5 0.017883968810358395 212 7 0.02503755633450175 211 6 0.021460762572430073 210 7 0.02503755633450175 209 9 0.03219114385864511 208 5 0.017883968810358395 207 7 0.02503755633450175 206 12 0.04292152514486015 205 6 0.021460762572430073 204 6 0.021460762572430073 203 9 0.03219114385864511 202 3 0.010730381286215037 201 7 0.02503755633450175 200 11 0.03934473138278847 199 14 0.0500751126690035 198 10 0.03576793762071679 197 11 0.03934473138278847 196 8 0.02861435009657343 195 11 0.03934473138278847 194 6 0.021460762572430073 193 10 0.03576793762071679 192 16 0.05722870019314686 191 8 0.02861435009657343 190 13 0.046498318906931825 189 10 0.03576793762071679 188 12 0.04292152514486015 187 8 0.02861435009657343 186 18 0.06438228771729022 185 14 0.0500751126690035 184 5 0.017883968810358395 183 12 0.04292152514486015 182 22 0.07868946276557694 181 14 0.0500751126690035 180 10 0.03576793762071679 179 15 0.05365190643107518 178 13 0.046498318906931825 177 20 0.07153587524143358 176 23 0.08226625652764862 175 16 0.05722870019314686 174 13 0.046498318906931825 173 20 0.07153587524143358 172 19 0.0679590814793619 171 20 0.07153587524143358 170 24 0.0858430502897203 169 24 0.0858430502897203 168 21 0.07511266900350526 167 23 0.08226625652764862 166 21 0.07511266900350526 165 25 0.08941984405179197 164 23 0.08226625652764862 163 24 0.0858430502897203 162 25 0.08941984405179197 161 32 0.11445740038629372 160 32 0.11445740038629372 159 31 0.11088060662422204 158 29 0.10372701910007869 157 35 0.12518778167250877 156 32 0.11445740038629372 155 36 0.12876457543458045 154 30 0.10730381286215036 153 30 0.10730381286215036 152 37 0.13234136919665213 151 45 0.16095571929322555 150 48 0.1716861005794406 149 45 0.16095571929322555 148 45 0.16095571929322555 147 33 0.1180341941483654 146 50 0.17883968810358394 145 55 0.19672365691394234 144 47 0.16810930

##### User-id: Medidas de posição

A base de push envolve `28.5k usuarios únicos` que receberam pushes. Em média cada um recebeu 732 pushes no período (~4/dia).

In [65]:
df_mpf.select(f.countDistinct('user_id')).show()

+-----------------------+
count(DISTINCT user_id)|
+-----------------------+
 28508|
+-----------------------+

In [66]:
avg_pushes = df_mpf.groupBy('user_id')\
                           .count()\
                           .withColumnRenamed('count', 'number_pushes')\

chosen_column = 'number_pushes'
exprrs = [sum(chosen_column), max(chosen_column), min(chosen_column), stddev(chosen_column), mean(chosen_column)]
display(avg_pushes.agg(*exprrs))

sum(number_pushes) max(number_pushes) min(number_pushes) stddev_samp(number_pushes) avg(number_pushes) 20875331 4647 1 462.98739483835794 732.2622070997614

Um evento `received` vai ter um evento `send` corresponte? </br>
Sim, abaixo podemos ver que toda linha de um push com event_name `received` vai ter um correspondente `send`, caso ele tenha sido enviado com sucesso.

In [68]:
display(df_mpf.filter(df_mdf['user_id'] == '5ac365c96ee329b1951ac7e9'))

event_channel event_name brand sample_type user_id external_user_id event_time_utc3 platform campaign_id campaign_name message_variation_channel event_date event_month event_dayofweek push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-09-24T15:19:49.000+0000 android e06d2a9a-106a-4dac-af0b-3afb84ff8353 2019-09-24 / ANDROID / Ativos / Lanche da Tarde / CUPOM android_push 2019-09-24 9 3 push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-09-16T11:16:57.000+0000 android 80df02dc-6a78-4588-9a8d-0b42e65ae0bd 2019-09-16 / ANDROID / Ativos / Almoço / CUPOM android_push 2019-09-16 9 2 push received iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-10-30T18:43:26.000+0000 android 91bfd4e5-aa6b-45f8-b9ca-f4f2cf8598de 2019-10-30 / ANDROID / Ativos / Jantar - Light / CUPOM android_push 2019-10-30 10 4 push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-11-10T11:47:39.000+0000 android 8709b71b-8659-4560-9897-32f48cb1b194 2019-11-10 / ANDROID / Ativos / Almoço - Light / CUPOM android_push 2019-11-10 11 1 push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-12-23T15:21:25.000+0000 android ff031779-a252-4984-b371-3796ec79e36d 2019-12-23 / ANDROID / Ativos / Lanche da Tarde / CUPOM android_push 2019-12-23 12 2 push received iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-07-22T11:42:34.000+0000 android 230108da-6949-4a0c-acff-b2815ff11a25 2019-07-22 / ANDROID / Almoço / CRM_Restaurante_Expansao (TMA) unknown 2019-07-22 7 2 push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-10-23T11:25:08.000+0000 android 87d04b9f-11f3-4dc9-bebe-b5909f6240a2 2019-10-23 / ANDROID / Ativos / Almoço - Light / CUPOM android_push 2019-10-23 10 4 push send iFood Brasil control 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-09-01T18:01:31.000+0000 unknown 38d5426c-2152-40e0-b9c8-11bc2654faae 2019-09-01 / ANDROID / 20190901ACAOPONTUALKAS android_push 2019-09-01 9 1 push received iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-12-19T18:44:18.000+0000 android 60e95be9-7449-41fe-8b7e-5fca8f4f02b6 2019-12-19 / ANDROID / Ativos / Jantar / CUPOM android_push 2019-12-19 12 5 push received iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-11-07T11:33:00.000+0000 android 6d26e61c-1a33-4a7b-87bd-37506bce0446 2019-11-07 / ANDROID / Ativos / Almoço - Light / CUPOM android_push 2019-11-07 11 5 push received iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-11-16T17:42:16.000+0000 android 666406cb-b0da-4de1-b40f-9529c4588981 2019-11-16 / ANDROID / Jantar / To Go android_push 2019-11-16 11 7 push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-06-29T14:54:10.000+0000 android b7982238-d0a4-4c3f-8a03-128864171df2 2019-06-29 / ANDROID / Ativos / Almoço / CUPOM android_push 2019-06-29 6 7 push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-12-06T10:47:24.000+0000 android e2a186c9-e489-48e0-8adc-6a072076fc19 2019-12-06 / ANDROID / Ativos / Almoço - Light / CUPOM android_push 2019-12-06 12 6 push send iFood Brasil sample 5ac365c96ee329b1951ac7e9 6f040026ecb33d63875ca8340a55db433fe185d8e40a0111f7166063893944a8 2019-12-30T21:23:58.000+0000 android 0395bf17-4de3-441d-ab4d-41cfe81d1dae 2019-12-30 / ANDROID / 20191231_RECCU

In [69]:
from pyspark.sql.functions import udf
push_range = udf(lambda pushes: '1- < 20' if pushes < 20 else 
                                 '2- 20-60' if (pushes >= 20 and pushes < 60) else
                                 '3- 60-100' if (pushes >= 60 and pushes < 100) else
                                 '4- 100-140' if (pushes >= 100 and pushes < 140) else
                                 '5- 140-180' if (pushes >= 140 and pushes < 180) else
                                 '6- 180-220' if (pushes >= 180 and pushes < 220) else
                                 '7- 220-260' if (pushes >= 220 and pushes < 260) else
                                 '8- 260-300' if (pushes >= 260 and pushes < 300) else
                                 '9- 300+'  if (pushes >= 300) else '')

Share de clientes por bins de pushes recebidos durante os meses:

In [71]:
aux = df_mpf_sample.groupby('user_id', 'event_month')\
            .count()\
            .withColumnRenamed('count', 'monthly_pushes')

aux = aux.withColumn('push_range', push_range(aux.monthly_pushes))\
         .groupby('event_month', 'push_range')\
         .count()\
         .withColumnRenamed('count', 'qtde_clientes')\
         .orderBy('event_month', 'push_range')
display(aux)

event_month push_range qtde_clientes 6 1- < 20 3326 6 2- 20-60 4366 6 3- 60-100 5745 6 4- 100-140 9574 6 5- 140-180 3011 6 6- 180-220 888 6 7- 220-260 419 6 8- 260-300 154 6 9- 300+ 126 7 1- < 20 2505 7 2- 20-60 2287 7 3- 60-100 1882 7 4- 100-140 6489 7 5- 140-180 6942 7 6- 180-220 2966 7 7- 220-260 1499 7 8- 260-300 816 7 9- 300+ 760 8 1- < 20 4243 8 2- 20-60 4910 8 3- 60-100 4179 8 4- 100-140 5537 8 5- 140-180 2891 8 6- 180-220 1495 8 7- 220-260 686 8 8- 260-300 308 8 9- 300+ 251 9 1- < 20 2533 9 2- 20-60 5496 9 3- 60-100 4537 9 4- 100-140 5722 9 5- 140-180 3640 9 6- 180-220 1438 9 7- 220-260 561 9 8- 260-300 237 9 9- 300+ 253 10 1- < 20 2137 10 2- 20-60 4308 10 3- 60-100 2709 10 4- 100-140 3305 10 5- 140-180 4447 10 6- 180-220 3671 10 7- 220-260 1998 10 8- 260-300 817 10 9- 300+ 962 11 1- < 20 2327 11 2- 20-60 1867 11 3- 60-100 3752 11 4- 100-140 6580 11 5- 140-180 4928 11 6- 180-220 2688 11 7- 220-260 911 11 8- 260-300 387 11 9- 300+ 480 12 1- < 20 1421 12 2- 20-60 1826 12 3- 60-100 2107 12 4- 100-140 4595 12 5- 140-180 5206 12 6- 180-220 4803 12 7- 220-260 2487 12 8- 260-300 809 12 9- 300+ 733

A maior média mensal de pushes foi em dezembro com 152 pushes/cliente, a menor foi em agosto com 94 pushes/cliente. Para o modelo, podemos colocar uma variável que indica a média de pushes o cliente recebeu no mês.

In [73]:
monthly_mean = df_mpf_sample.groupby('user_id', 'event_month')\
                            .count()\
                            .withColumnRenamed('count', 'monthly_pushes')\
                            .groupby('event_month')\
                            .mean()\
                            .orderBy('event_month', asc=True)
display(monthly_mean)

event_month avg(event_month) avg(monthly_pushes) 6 6.0 94.93944003766887 7 7.0 137.31427369387288 8 8.0 94.00453061224489 9 9.0 99.45214399803416 10 10.0 135.06339820973966 11 11.0 124.97182274247491 12 12.0 152.32563471880601

### 2. Customer Segmentation

#### Tratamento de Duplicidades

In [77]:
df_customer_segmentation = df_customer_segmentation.distinct()
# Após a remoção de duplicados, as dimensões do dataframe passam a ser:
print('Customer segmentation:     ', df_customer_segmentation.count(), '   linhas e ', len(df_customer_segmentation.columns), ' colunas')

Customer segmentation: 210316 linhas e 50 colunas

#### Tratamento de Missing

In [79]:
perc_miss = percent_missing(df_customer_segmentation) # Calcula o percentual de missings para todas as colunas
col_drop = perc_miss.filter((perc_miss['perc_missing'] <= 0.1) & (perc_miss['perc_missing'] > 0)).select('variaveis').rdd.flatMap(lambda x: x).collect() # Seleciona colunas com menos de 0.1% de missings
col_drop.append('customer_id') # Acrescenta a coluna de customer_id na lista de colunas com missing
aux1 = df_customer_segmentation.select(col_drop) # Criar datafram auxiliar apenas com as colunas em col_drop
# Cria lista com o customer_id de quem tem algum dado nulo para alguma das colunas em col_drop:
c_id_drop = aux1.where(reduce(lambda x, y: x | y, (f.col(x).isNull() for x in aux1.columns))).select('customer_id').distinct().rdd.flatMap(lambda x: x).collect() 
# Exclui de df_customer_segmentation todos os registros de quem teve informação nula identificada: (Decisão tomada por conta da base ser histórica e o impacto em número absoluto de resgistros ser pequeno)
df_customer_segmentation = df_customer_segmentation.filter(~df_customer_segmentation.customer_id.isin(c_id_drop))

display(percent_missing(df_customer_segmentation).orderBy(desc('perc_missing')))
# A existência de missings é informação relevante para as colunas que permaneceram na lista.

variaveis total_missing perc_missing last_invalid_order_date 117137 55.91158164044601 preferred_shift_bucket_description 54968 26.23720788147243 days_to_reorder_at_concluded 18857 9.00078280128303 days_to_reorder_at_datasource 17879 8.53396593859783 merchant_variety_bucket 0 0.0 merchant_offer 0 0.0 merchant_offer_bucket 0 0.0 merchant_offer_bucket_description 0 0.0 top_dish_bucket 0 0.0 top_dish_bucket_description 0 0.0 preferred_dishes 0 0.0 preferred_dishes_code 0 0.0 qtt_valid_orders 0 0.0 qtt_invalid_orders 0 0.0 last_valid_order_date 0 0.0 top_centroid_id 0 0.0 marlin_tag 0 0.0 recency_months 0 0.0 customer_id 0 0.0 segmentation_month 0 0.0 ifood_status_last_month 0 0.0 ifood_status 0 0.0 orders_last_91d 0 0.0 qtt_orders_last_year 0 0.0 buyer_last_91d 0 0.0 top_city 0 0.0 top_district 0 0.0 customer_lifetime_months 0 0.0 first_order_date 0 0.0 last_order_date 0 0.0 rfv_score 0 0.0 recency_days 0 0.0 recency_days_bucket_description 0 0.0 recency_days_bucket 0 0.0 maturity_orders_bucket_description 0 0.0 benefits_sensitivity_bucket 0 0.0 benefits_sensitivity 0 0.0 preferred_shift_bucket 0 0.0 merchant_variety 0 0.0 freq_last_91d 0 0.0 freq_last_91d_bucket 0 0.0 freq_last_91d_bucket_description 0 0.0 avg_aov_last_91d 0 0.0 maturity_orders 0 0.0 maturity_orders_bucket 0 0.0 last_nps 0 0.0 registration_date 0 0.0 customer_lifetime_days 0 0.0 top_3_merchants_code 0 0.0 was_mub_last_month 0 0.0

#### Tratamento de Arrays

In [81]:
#Ajuste coluna preferred_dishes (tipo array):
df_customer_segmentation = df_customer_segmentation.withColumn('aux_1', udf_limpeza(col('preferred_dishes')))
df_customer_segmentation = df_customer_segmentation.withColumn('preferred_dishes_ar', split(col('aux_1'), ',').cast(ArrayType(StringType())))
#Ajuste coluna top_3_merchants_code (tipo array):
df_customer_segmentation = df_customer_segmentation.withColumn('aux_2', udf_limpeza(col('top_3_merchants_code')))
df_customer_segmentation = df_customer_segmentation.withColumn('top_3_merchants_code_ar', split(col('aux_2'), ',').cast(ArrayType(StringType())))

list_columns_to_drop = ['aux_1','aux_2']
df_customer_segmentation = df_customer_segmentation.drop(*list_columns_to_drop) # Exclusão de colunas auxiliares

df_customer_segmentation.columns

Out[12]: ['customer_id',
 'segmentation_month',
 'ifood_status_last_month',
 'ifood_status',
 'orders_last_91d',
 'qtt_orders_last_year',
 'qtt_valid_orders',
 'last_valid_order_date',
 'qtt_invalid_orders',
 'last_invalid_order_date',
 'marlin_tag',
 'recency_months',
 'last_nps',
 'registration_date',
 'customer_lifetime_days',
 'customer_lifetime_months',
 'top_3_merchants_code',
 'was_mub_last_month',
 'buyer_last_91d',
 'top_city',
 'top_district',
 'top_centroid_id',
 'first_order_date',
 'last_order_date',
 'days_to_reorder_at_datasource',
 'days_to_reorder_at_concluded',
 'rfv_score',
 'recency_days',
 'recency_days_bucket',
 'recency_days_bucket_description',
 'freq_last_91d',
 'freq_last_91d_bucket',
 'freq_last_91d_bucket_description',
 'avg_aov_last_91d',
 'maturity_orders',
 'maturity_orders_bucket',
 'maturity_orders_bucket_description',
 'benefits_sensitivity',
 'benefits_sensitivity_bucket',
 'preferred_shift_bucket',
 'preferred_shift_bucket_description',
 'merchant_variety',
 'merchant_variety_bucket',
 'merchant_offer',
 'merchant_offer_bucket',
 'merchant_offer_bucket_description',
 'top_dish_bucket',
 'top_dish_bucket_description',
 'preferred_dishes',
 'preferred_dishes_code',
 'preferred_dishes_ar',
 'top_3_merchants_code_ar']

#### Tratamento de Datas

In [83]:
df_customer_segmentation = df_customer_segmentation.withColumn('registration_date', from_utc_timestamp('registration_date', 'UTC'))\
                                                   .withColumn('registration_date', to_date('registration_date', 'YYYY-MM-DD'))\
                                                   .withColumn('last_valid_order_date', from_utc_timestamp('last_valid_order_date', 'UTC'))\
                                                   .withColumn('last_valid_order_date', to_date('last_valid_order_date', 'YYYY-MM-DD'))\
                                                   .withColumn('last_invalid_order_date', from_utc_timestamp('last_invalid_order_date', 'UTC'))\
                                                   .withColumn('last_invalid_order_date', to_date('last_invalid_order_date', 'YYYY-MM-DD'))\
                                                   .withColumn('first_order_date', from_utc_timestamp('first_order_date', 'UTC'))\
                                                   .withColumn('first_order_date', to_date('first_order_date', 'YYYY-MM-DD'))\
                                                   .withColumn('last_order_date', from_utc_timestamp('last_order_date', 'UTC'))\
                                                   .withColumn('last_order_date', to_date('last_order_date', 'YYYY-MM-DD'))\
                                                   .withColumn('segmentation_month', from_utc_timestamp('segmentation_month', 'UTC'))\
                                                   .withColumn('segmentation_month', to_date('segmentation_month', 'YYYY-MM-DD'))\
                                                   .withColumn('registration_month', month('registration_date'))\
                                                   .withColumn('registration_dayofweek', dayofweek('registration_date'))\
                                                   .withColumn('first_order_month', month('first_order_date'))\
                                                   .withColumn('first_order_dayofweek', dayofweek('first_order_date'))\
                                                   .withColumn('segmentation_month_month', month('segmentation_month'))\
                                                   .withColumn('segmentation_month_dayofweek', dayofweek('segmentation_month'))\
                                                   .withColumn('last_order_month', month('last_order_date'))\
                                                   .withColumn('last_order_dayofweek', dayofweek('last_order_date'))

#### Análise Variáveis Qualitativas

Describe das variáveis numéricas que auxiliaram a explicar as variáveis Qualitativas

In [86]:
var_num_cust_seg = [x[0] for x in df_customer_segmentation.dtypes if x[1] in ('double', 'int', 'long')]
display(df_customer_segmentation.describe(var_num_cust_seg))

summary orders_last_91d recency_months days_to_reorder_at_datasource days_to_reorder_at_concluded rfv_score recency_days recency_days_bucket freq_last_91d freq_last_91d_bucket avg_aov_last_91d maturity_orders maturity_orders_bucket benefits_sensitivity merchant_variety merchant_offer registration_month registration_dayofweek first_order_month first_order_dayofweek segmentation_month_month segmentation_month_dayofweek last_order_month last_order_dayofweek count 209504 209504 191625 190647 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 209504 mean 8.547378570337559 1.2802836620343765 34.40750885997784 35.56226937255755 2.7033708186955856 39.26262028409959 2.736907171223461 3.042965814495186 2.54704922101726 55.06199437719568 38.838552008553535 3.6059072857797463 0.6554377943448566 0.7475997084287131 1357.3949566595388 6.266863639835039 4.128723079272949 6.121019169085077 4.155787001680159 9.00339372995265 3.567550022911257 8.076919772414847 4.185309111043226 stddev 9.977829133633788 1.6360901047516403 74.83428254547731 75.88633798354759 0.6586515408969449 50.03528473568874 1.4838300778174163 3.2914642907782548 1.1215154732515034 22.986055395669755 62.337680435058985 1.1924221024110617 0.3351547210458754 0.24536067478995288 1338.513079953022 3.4003146241778524 2.2201720121999484 3.2071897317007814 2.226641198413645 1.998587334034061 2.257105194537576 2.0410546903375395 2.17692227337059 min 1.0 0.0 0.0 0.0 1.0 0.0 1.0 0.33 1.0 13.07 1.0 1.0 0.0 0.011494252873563218 1.0 1 1 1 1 6 1 1 1 max 213.0 40.03225806 2612.0 2612.0 5.0 1217.0 5.0 92.5 5.0 1428.0 1297.0 5.0 1.0 1.0 7031.0 12 7 12 7 12 7 12 7

Variáveis Qualitativas

In [88]:
var_cat_cust_seg = [x[0] for x in df_customer_segmentation.dtypes if x[1] not in ('double', 'int', 'long')]
var_cat_cust_seg

Out[15]: ['customer_id',
 'segmentation_month',
 'ifood_status_last_month',
 'ifood_status',
 'qtt_orders_last_year',
 'qtt_valid_orders',
 'last_valid_order_date',
 'qtt_invalid_orders',
 'last_invalid_order_date',
 'marlin_tag',
 'last_nps',
 'registration_date',
 'customer_lifetime_days',
 'customer_lifetime_months',
 'top_3_merchants_code',
 'was_mub_last_month',
 'buyer_last_91d',
 'top_city',
 'top_district',
 'top_centroid_id',
 'first_order_date',
 'last_order_date',
 'recency_days_bucket_description',
 'freq_last_91d_bucket_description',
 'maturity_orders_bucket_description',
 'benefits_sensitivity_bucket',
 'preferred_shift_bucket',
 'preferred_shift_bucket_description',
 'merchant_variety_bucket',
 'merchant_offer_bucket',
 'merchant_offer_bucket_description',
 'top_dish_bucket',
 'top_dish_bucket_description',
 'preferred_dishes',
 'preferred_dishes_code',
 'preferred_dishes_ar',
 'top_3_merchants_code_ar']

A chave da base é uma combinação entre customer_id e segmentation_month, isto é, a tabela é um recorte de uma base histórica de um grupo específico de clientes. Após a exclusão dos duplicados, tem-se aproximadamente 30k clientes e suas informações entre Junho e Dezembro.

In [90]:
customer_amount_seg_month = df_customer_segmentation.groupby('segmentation_month_month').count().orderBy('segmentation_month_month')
display(customer_amount_seg_month)

segmentation_month_month count 6 29726 7 29963 8 29963 9 29963 10 29963 11 29963 12 29963

#### Ifood Status

Esses clientes são classificados em 5 status em um determido mês. Outubro é o mês com a maior proporção de clientes Inativos. Em compensação, a proporção de Churn também se mostra como a menor desde Junho.

In [93]:
# O status desses clientes ao longo dos meses é:
df_ifood_status = df_customer_segmentation.groupby('ifood_status','segmentation_month_month').count().orderBy('segmentation_month_month','ifood_status')
display(df_ifood_status)

ifood_status segmentation_month_month count Active 6 17865 Churn 6 209 Inactive 6 235 New 6 5015 Resurrected 6 6402 Active 7 18253 Churn 7 11536 Inactive 7 174 Active 8 13825 Churn 8 4597 Inactive 8 8348 Resurrected 8 3193 Active 9 13429 Churn 9 3885 Inactive 9 9360 Resurrected 9 3289 Active 10 13298 Churn 10 154 Inactive 10 13203 Resurrected 10 3308 Active 11 13243 Churn 11 3363 Inactive 11 10076 Resurrected 11 3281 Active 12 13302 Churn 12 3459 Inactive 12 10319 Resurrected 12 2883

A tabela abaixo mostra a transição de ifood_status entre o mês anterior (eixo horizontal) e o mês atual (eixo vertical).

Highlights: A maioria dos inativos permanece inativo (33334). A maioria dos ativos, permanece ativo. Pessoas novas tem virado mais Churn do que Ativos (3713 contra 3113), mas a proporção é parecida. Maioria das pessoas que ressucitam se tornam ativas (12427). A maioria do Churn é de ativos (15802) e não de novos (3713).

Dúvidas: Pessoas que eram inativos virando Churn (346)? Pessoas que eram ativas virando Inativas direto (255)? Pessoas que eram novas virando Inativas direto (31)? Pessoas ressurretas virando Inativas direto (65)? Pessoas permanecendo como ressurretas (3308)?

In [95]:
df_status_trans = df_customer_segmentation.filter(df_customer_segmentation['ifood_status'] != 'New').groupby('ifood_status','ifood_status_last_month').count() # Df auxiliar com ifood_status e ifood_status_last_month
df_status_trans_pivot = df_status_trans.groupby('ifood_status').pivot('ifood_status_last_month').sum('count').orderBy('ifood_status') # Pivot do Df contruído no passo anterior colocando o ifood_status_last_month no eixo vertical
display(df_status_trans_pivot)

ifood_status Active Churn Inactive New Resurrected Churn 15802 null 346 3713 7342 Resurrected null 3117 15931 null 3308 Active 87675 null null 3113 12427 Inactive 255 18030 33334 31 65

In [96]:
df_ifood_status = df_customer_segmentation.select('customer_id','segmentation_month_month','ifood_status')
df_ifood_status_pivot = df_ifood_status.groupby('customer_id','ifood_status').pivot('segmentation_month_month').count().fillna(0)
df_ifood_status_pivot = df_ifood_status_pivot.withColumn('ifood_status_freq', df_ifood_status_pivot['6'] + df_ifood_status_pivot['7'] + df_ifood_status_pivot['8'] + df_ifood_status_pivot['9'] + df_ifood_status_pivot['10'] + df_ifood_status_pivot['11'] + df_ifood_status_pivot['12'])

Vê-se que, em média, as pessoas que tiveram status Ativo na base, o tiveram por 4 meses. Mais ainda, vê-se que, em média, quem deu Churn, o fez apenas uma vez no período.

In [98]:
display(df_ifood_status_pivot.groupby('ifood_status').agg(f.round(avg('ifood_status_freq'),0)).orderBy('ifood_status'))

ifood_status round(avg(ifood_status_freq), 0) Active 4.0 Churn 1.0 Inactive 3.0 New 1.0 Resurrected 1.0

Vê-se que, aproximadamente 30% (6680 clientes) das pessoas que tiveram status Ativo ao menos uma vez no período, na verdade, permanceram ativas durante os 7 meses que se tem de informação disponível. Entre os que em algum momento tiveram status Inativo, 30% (4751 clientes) foram inativos por 5 meses.

In [100]:
display(df_ifood_status_pivot.groupby('ifood_status','ifood_status_freq').count().orderBy('ifood_status','ifood_status_freq'))

ifood_status ifood_status_freq count Active 1 4227 Active 2 3241 Active 3 2766 Active 4 2728 Active 5 3086 Active 6 1851 Active 7 6680 Churn 1 15168 Churn 2 5196 Churn 3 537 Churn 4 8 Inactive 1 4451 Inactive 2 2423 Inactive 3 3299 Inactive 4 2130 Inactive 5 4751 Inactive 6 41 New 1 5015 Resurrected 1 10481 Resurrected 2 4561 Resurrected 3 891 Resurrected 4 20

#### Tipo de comida preferida

No período, Lanches aparece como sendo o tipo de prato preferido do clientes tendo sido classificado como uma preferência por cerca de X%. Pizza, Comida Brasileira e Comida Japonesa também se destacam como

In [103]:
df_preferred_dishes = df_customer_segmentation.select('customer_id','segmentation_month_month', explode(col('preferred_dishes_ar')).alias('pratos')) # Cria df auxiliar com pratos favoritos por mês
display(df_preferred_dishes.groupby('pratos').count()) # Ranking de pratos favoritos no período todo

pratos count Peixes 109 Cafeteria 471 Congelados Fit 3 Doces & Bolos 7061 Comida Chinesa 14856 Sopas & Caldos 78 Comida Brasileira 75081 Comida Árabe 9485 Açaí 16124 Comida Asiática 208 Panqueca 56 Comida Italiana 10580 Carnes 8632 Nordestina 35 Africana 26 Pastel 2920 Mercado 121 Baiana 16 Argentina 142 Bebidas 1685 Presentes 1 Comida Alemã 188 Xis 15 Vegana 124 Frutos do Mar 4354 Gaúcha 1 Congelados 298 Yakisoba 95 Hambúrguer 2222 Comida Francesa 499 Comida Variada 9746 Coreana 11 Comida Indiana 86 Comida Contemporânea 693 Pizza 93890 Comida Tailandesa 269 Padaria 1336 Lanches 131738 Espanhola 24 Cozinha Rápida 3617 Comida Japonesa 38099 Sorvetes 4343 Comida Saudável 14991 Colombiana 16 Tapioca 48 Comida Mediterrânea 177 Comida Mexicana 2300 Marmita 8614 Mineira 104 Conveniência 127 Salgados 7177 Vegetariana 633 Comida Peruana 101 Comida Portuguesa 120 Casa de Sucos 61 Crepe 54 Frangos 185

Vê-se que tipos de prato citados anteriormente permanecem entre os favoritos ao longo dos meses e que a partir de Agosto açaí ultrapassa comida chinesa como um dos 5 tipos de comidas favoritos entre os 30k clientes da base.

In [105]:
# Pratos favoritos mês a mês:

# Df auxiliar com preferência mensal:
df_preferred_dishes_aux = df_preferred_dishes.groupby('pratos','segmentation_month_month').count()
# Inclusão de coluna com ranking de prato preferido para cada mês:
df_preferred_dishes_ranked =  df_preferred_dishes_aux.withColumn(
  "rank", dense_rank().over(Window.partitionBy("segmentation_month_month").orderBy(desc("count"))))
# Inclusão de coluna que agrupa os pratos fora do TOP 5 de favoritos para cada mês:
df_preferred_dishes_ranked = df_preferred_dishes_ranked.withColumn(
  'pratos_group',f.when(df_preferred_dishes_ranked.rank > 5, 'other').otherwise(df_preferred_dishes_ranked.pratos))

display(df_preferred_dishes_ranked.groupby('segmentation_month_month','pratos_group').sum('count').orderBy("segmentation_month_month"))

segmentation_month_month pratos_group sum(count) 6 Comida Chinesa 2221 6 other 15656 6 Lanches 18248 6 Pizza 12909 6 Comida Brasileira 9970 6 Comida Japonesa 5274 7 Comida Japonesa 5367 7 Lanches 18938 7 Pizza 13621 7 Comida Brasileira 10593 7 Comida Chinesa 2206 7 other 16904 8 Comida Japonesa 5448 8 other 17329 8 Açaí 2224 8 Lanches 19102 8 Pizza 13847 8 Comida Brasileira 10867 9 Lanches 19018 9 Pizza 13715 9 Comida Brasileira 10907 9 Comida Japonesa 5511 9 Açaí 2319 9 other 17316 10 Lanches 18854 10 Pizza 13350 10 Comida Brasileira 10896 10 Comida Japonesa 5435 10 other 17152 10 Açaí 2411 11 Lanches 18788 11 Comida Japonesa 5545 11 Pizza 13180 11 Açaí 2459 11 other 17220 11 Comida Brasileira 10873 12 Lanches 18790 12 Pizza 13268 12 Comida Brasileira 10975 12 Comida Japonesa 5519 12 Açaí 2565 12 other 17256

##### Pedidos válidos

In [107]:
df_qtt_orders = df_customer_segmentation.select('customer_id','segmentation_month_month','ifood_status','orders_last_91d','qtt_orders_last_year','qtt_valid_orders').orderBy('customer_id','segmentation_month_month')
df_qtt_orders_lag = df_qtt_orders.withColumn('qtt_valid_orders_prev',
                                            f.lag(df_qtt_orders['qtt_valid_orders'])
                                             .over(Window.partitionBy("customer_id")
                                             .orderBy("segmentation_month_month")))

df_qtt_orders_final = df_qtt_orders_lag.withColumn('qtt_valid_orders_month', 
          (df_qtt_orders_lag['qtt_valid_orders'] - df_qtt_orders_lag['qtt_valid_orders_prev']) )

df_qtt_orders_result = df_qtt_orders_final.filter((df_qtt_orders_final['segmentation_month_month'] > 6) & (df_qtt_orders_final['qtt_valid_orders_month'] > 0)).groupby('segmentation_month_month').agg(sum('qtt_valid_orders_month'),count('customer_id'))

df_qtt_orders_result = df_qtt_orders_result.withColumn('qtt_valid_orders_avg',df_qtt_orders_result['sum(qtt_valid_orders_month)']/df_qtt_orders_result['count(customer_id)'])

Há um pico de mais de 70k pedidos no mês de Julho que não se repete até Dezembro. Outubro se destaca com o segundo maior número de pedidos no período, algo próximo de 68k. Os demais meses ficaram na casa dos 66k pedidos.

Obs.: Não existem informações consistentes para o mês de Junho.

In [109]:
display(df_qtt_orders_result.select('segmentation_month_month','sum(qtt_valid_orders_month)'))

segmentation_month_month sum(qtt_valid_orders_month) count(customer_id) qtt_valid_orders_avg 12 66563 16438 4.04933690229955 9 66603 17002 3.917362663216092 8 66547 17174 3.874868988005124 7 71008 18705 3.7962042234696605 10 68295 16710 4.087073608617594 11 66668 16527 4.0338839474798815

In [110]:
display(df_qtt_orders_result.agg(avg('sum(qtt_valid_orders_month)')))

avg(sum(qtt_valid_orders_month)) 67614.0

Enquanto o número absoluto tem seu pico em Julho, o número médio de pedidos tem uma curva crescente com seu pico em Outubro com algo próximo a 4.1 pedidos por cliente que efetuou ao menos um pedido.

In [112]:
display(df_qtt_orders_result.select('segmentation_month_month','qtt_valid_orders_avg'))

segmentation_month_month qtt_valid_orders_avg 12 4.04933690229955 9 3.917362663216092 8 3.874868988005124 7 3.7962042234696605 10 4.087073608617594 11 4.0338839474798815

São Paulo é a cidade com maior número de clientes, com quase o dobro do que o Rio de Janeiro, segunda colocada no ranking.

In [114]:
display(df_customer_segmentation.groupby(lower(col('top_city'))).count().orderBy(desc('count')))

lower(top_city) count sao paulo 32821 rio de janeiro 17071 belo horizonte 8161 brasilia 6773 fortaleza 6514 curitiba 6002 campinas 4587 recife 4151 porto alegre 3983 goiania 3268 salvador 3130 londrina 2791 ribeirao preto 2705 joao pessoa 2556 guarulhos 2428 niteroi 2345 florianopolis 2278 uberlandia 2224 manaus 2080 sao jose dos campos 2019 maceio 1977 santo andre 1917 maringa 1885 vitoria 1832 sao bernardo do campo 1829 belem 1818 campo grande 1752 osasco 1729 aracaju 1643 natal 1627 sorocaba 1538 santos 1530 vila velha 1501 juiz de fora 1491 contagem 1376 cuiaba 1111 jundiai 1098 uberaba 1084 mogi das cruzes 1066 sao goncalo 1056 sao jose do rio preto 1049 joinville 1035 teresina 1027 piracicaba 1007 bauru 981 sao carlos 936 blumenau 921 barueri 906 montes claros 873 caxias do sul 823 duque de caxias 810 campina grande 798 limeira 797 sao jose 797 sao luis 785 canoas 752 caruaru 736 sao caetano do sul 730 diadema 727 jaboatao dos guararapes 695 nova iguacu 667 carapicuiba 645 cascavel 642 franca 641 praia grande 638 americana 627 betim 627 maua 618 marilia 610 serra 600 taubate 597 campos dos goytacazes 567 volta redonda 559 indaiatuba 550 novo hamburgo 549 balneario camboriu 534 macae 532 parnamirim 528 olinda 507 anapolis 493 itajai 493 sumare 488 suzano 469 ponta grossa 464 jacarei 440 porto velho 428 aparecida de goiania 425 pres. prudente 412 sao jose dos pinhais 410 hortolandia 405 presidente prudente 405 palhoca 398 foz do iguacu 389 sao leopoldo 384 taboao da serra 383 rio claro 369 aracatuba 359 araraquara 358 ipatinga 353 pelotas 347 nilopolis 340 santa luzia 338 mossoro 337 itu 332 sao joao de meriti 330 governador valadares 325 divinopolis 319 passo fundo 314 braganca paulista 311 gravatai 309 feira de santana 307 petropolis 304 ananindeua 302 cabo frio 301 valinhos 299 cotia 298 paulista 298 santana de parnaiba 297 sete lagoas 286 botucatu 284 cariacica 279 dourados 275 paulinia 270 belford roxo 269 lauro de freitas 262 atibaia 249 sao vicente 246 mesquita 246 gov. valadares 246 juazeiro do norte 241 caucaia 241 vitoria da conquista 237 bento goncalves 236 pinhais 220 itaquaquecetuba 219 ouro preto 212 jandira 209 guaruja 206 colombo 197 cachoeirinha 188 ferraz de vasconcelos 188 varzea paulista 186 nova lima 185 araras 179 macapa 173 teresopolis 172 embu das artes 171 barra mansa 170 patos de minas 169 jau 162 sapucaia do sul 159 cambe 154 rio das ostras 150 catanduva 149 itapevi 148 aruja 144 araucaria 141 rio branco 141 rondonopolis 138 apucarana 135 assis 135 ribeirao das neves 130 pocos de caldas 129 arapiraca 128 chapeco 128 votorantim 127 criciuma 126 boa vista 124 nova friburgo 119 sao joao da boa vista 119 esteio 116 itapema 115 guarapari 114 camboriu 112 ribeirao pires 109 rio grande 106 poa 106 salto 106 vinhedo 104 sarandi 103 barretos 103 eusebio 103 santa barbara d'oeste 102 guarapuava 100 cachoeiro de itapemirim 100 santa barbara doeste 99 pouso alegre 99 varginha 99 ibirite 98 farroupilha 97 sao cristovao 93 campo limpo paulista 93 itabira 90 resende 90 lages 90 itaborai 89 camaragibe 88 caieiras 82 sapiranga 81 petrolina 80 tatui 77 campo largo 77 rio verde 76 ituiutaba 76 biguacu 76 itatiba 75 umuarama 74 sabara 74 campo bom 73 varzea grande 72 vicosa 72 sinop 71 imperatriz 70 fazenda rio grande 70 itapecerica da serra 69 arapongas 69 gramado 68 camacari 67 castanhal 66 itaperuna 62 araxa 61 porto seguro 61 linhares 60 cajamar 59 valparaiso de goias 59 mogi guacu 59 alvorada 59 maracanau 56 viamao 53 itaguai 53 tubarao 51 crateus 50 sertaozinho 50 marica 49 caraguatatuba 49 itapetininga 48 birigui 48 piraquara 47 palmas 46 guaratingueta 46 toledo 46 francisco morato 45 almirante tamandare 44 ubatuba 44 franco da rocha 44 sao pedro da aldeia 43 pirassununga 43 cabo de santo agostinho 42 araruama 41 sobral 41 peruibe 41 nossa sra. do socorro 40 canela 40 cabedelo 39 trindade 39 itanhaem 37 capao da canoa 36 ourinhos 35 alm. tamandare 35 juazeiro 35 araguari 35 brusque 33 avare 32 vitoria de sant

O cenário se mantém com São Paulo como destaque quando olha-se apenas para clientes ativos.

In [116]:
display(df_customer_segmentation.filter(df_customer_segmentation['ifood_status'] == 'Active').groupby(lower(col('top_city'))).count().orderBy(desc('count')))

lower(top_city) count sao paulo 17220 rio de janeiro 9395 belo horizonte 4082 brasilia 3667 fortaleza 3257 curitiba 3187 campinas 2536 recife 2154 porto alegre 2109 londrina 1661 goiania 1569 ribeirao preto 1473 niteroi 1315 salvador 1291 florianopolis 1249 guarulhos 1177 sao jose dos campos 1087 joao pessoa 1067 uberlandia 1062 maringa 1036 vitoria 1027 santo andre 1021 manaus 980 maceio 947 campo grande 905 belem 891 santos 879 sao bernardo do campo 875 osasco 797 natal 762 juiz de fora 743 aracaju 730 vila velha 715 sorocaba 712 contagem 654 jundiai 571 mogi das cruzes 552 piracicaba 537 sao jose do rio preto 530 sao carlos 522 barueri 506 sao goncalo 495 joinville 490 bauru 479 blumenau 475 cuiaba 465 uberaba 464 teresina 438 limeira 413 sao jose 393 caxias do sul 380 canoas 378 duque de caxias 367 sao caetano do sul 367 cascavel 341 sao luis 328 diadema 328 novo hamburgo 317 taubate 316 caruaru 316 jaboatao dos guararapes 313 americana 309 nova iguacu 300 carapicuiba 299 praia grande 298 campos dos goytacazes 295 montes claros 295 marilia 288 volta redonda 287 indaiatuba 282 macae 280 campina grande 270 franca 266 jacarei 264 serra 262 betim 261 itajai 252 balneario camboriu 246 maua 243 ponta grossa 235 porto velho 233 parnamirim 226 sumare 225 presidente prudente 215 suzano 210 hortolandia 204 araraquara 200 sao leopoldo 198 rio claro 194 olinda 193 aracatuba 187 sao jose dos pinhais 181 palhoca 177 itu 171 braganca paulista 165 valinhos 164 anapolis 160 aparecida de goiania 159 governador valadares 158 mossoro 157 nilopolis 155 taboao da serra 154 botucatu 154 foz do iguacu 152 gravatai 152 cotia 151 santana de parnaiba 150 passo fundo 145 petropolis 140 ipatinga 138 pelotas 137 paulinia 137 mesquita 133 dourados 129 belford roxo 129 pres. prudente 125 cariacica 120 atibaia 119 sao vicente 118 sao joao de meriti 116 cabo frio 115 paulista 113 cachoeirinha 113 jandira 104 bento goncalves 102 sete lagoas 99 divinopolis 94 pinhais 92 colombo 88 guaruja 88 araras 86 cambe 82 ouro preto 81 varzea paulista 80 caucaia 79 lauro de freitas 78 patos de minas 77 nova lima 76 ananindeua 76 feira de santana 75 gov. valadares 74 juazeiro do norte 72 teresopolis 72 sapucaia do sul 71 ferraz de vasconcelos 67 criciuma 64 macapa 64 catanduva 63 barra mansa 60 boa vista 60 votorantim 59 rio das ostras 59 embu das artes 57 santa luzia 56 poa 56 assis 55 itapevi 55 itapema 54 jau 53 vinhedo 51 arapiraca 49 aruja 49 varginha 48 nova friburgo 48 eusebio 48 sarandi 48 itaquaquecetuba 46 esteio 46 vitoria da conquista 45 araucaria 45 sao joao da boa vista 44 campo limpo paulista 44 biguacu 43 santa barbara doeste 42 sabara 42 pocos de caldas 41 rio branco 41 chapeco 41 farroupilha 41 itatiba 40 guarapuava 40 caieiras 40 guarapari 39 petrolina 39 salto 39 barretos 37 ribeirao das neves 35 cachoeiro de itapemirim 35 camboriu 35 mogi guacu 34 rio grande 34 ribeirao pires 34 campo bom 33 almirante tamandare 33 campo largo 32 apucarana 32 araxa 31 tatui 31 fazenda rio grande 31 arapongas 30 itapecerica da serra 30 sapiranga 29 itapetininga 27 resende 27 itabira 27 sinop 26 mogi mirim 25 ibirite 24 varzea grande 23 camaragibe 23 linhares 22 castanhal 22 viamao 22 pouso alegre 22 itaperuna 22 porto seguro 22 cabedelo 21 piraquara 21 valparaiso de goias 21 rondonopolis 21 pirassununga 21 francisco morato 21 santa barbara d'oeste 20 umuarama 20 araguari 20 itanhaem 19 rio verde 19 imperatriz 19 vicosa 19 cajamar 18 ituiutaba 18 sao cristovao 18 itaguai 18 angra dos reis 17 maraba 17 santarem 16 tubarao 16 crateus 15 toledo 15 lages 14 peruibe 14 nossa sra. do socorro 14 gramado 14 araruama 14 santo amaro da imperatriz 14 itumbiara 13 canela 13 itajuba 13 formosa 13 itaborai 13 alvorada 13 cabo de santo agostinho 12 batatais 12 marica 12 sao pedro da aldeia 12 vitoria de santo antao 11 tremembe 11 guaratingueta 11 navegantes 11 sertaozinho 10 itupeva 10 itabuna 10 alm. tamandare 10 ilheus 10 jaragua do sul 9 cianorte 9 cubatao 8 camacari 8 sao sebastia

Chegando ao nível dos bairros em São Paulo, Bela Vista, Vila Mariana e Pinheiros são os destaques.

In [118]:
display(df_customer_segmentation.filter((df_customer_segmentation['ifood_status'] == 'Active') & (df_customer_segmentation['top_city'] == 'SAO PAULO')).groupby(lower(col('top_district'))).count().orderBy(desc('count')))

lower(top_district) count bela vista 496 vila mariana 466 pinheiros 296 perdizes 281 jardim paulista 260 consolacao 237 itaim bibi 236 santana 224 indianopolis 224 vila olimpia 212 mooca 204 tatuape 194 vila clementino 178 santo amaro 174 barra funda 171 campo belo 160 liberdade 151 vila andrade 139 santa cecilia 127 aclimacao 123 ipiranga 122 cidade moncoes 119 brooklin paulista 119 saude 115 vila nova conceicao 113 vila leopoldina 113 vila prudente 112 vila buarque 112 paraiso 110 cerqueira cesar 110 jardim brasil (zona norte) 106 bras 106 agua branca 105 lauzane paulista 100 mirandopolis 99 cambuci 96 planalto paulista 93 vila gomes cardim 88 vila carrao 88 butanta 88 jaguare 88 moema 83 vila regente feijo 82 higienopolis 82 vila guarani(zona sul) 82 campos eliseos 78 vila carmosina 76 chacara santo antonio (zona sul) 75 vila madalena 75 vila formosa 70 sumarezinho 70 itaquera 69 vila suzana 68 parque da mooca 65 vila gustavo 64 alto de pinheiros 63 vila guilherme 60 jardim america 60 vila romana 59 vila dom pedro i 57 vila mascote 57 vila maria alta 56 vila da saude 55 jardim sao paulo(zona norte) 54 bom retiro 53 vila gumercindo 52 jardim paulistano 51 vila ipojuca 49 jardim leonor 48 vila monte alegre 48 alto da mooca 47 vila medeiros 47 pacaembu 46 vila uberabinha 45 parque boturussu 45 vila dom pedro ii 45 vila anglo brasileira 44 vila bertioga 43 lapa 43 vila mazzei 43 vila pompeia 42 agua fria 42 republica 42 cidade patriarca 41 centro 40 imirim 40 cidade lider 39 vila cordeiro 39 vila sofia 39 brooklin 39 vila aricanduva 38 cidade sao mateus 38 vila cruzeiro 38 belenzinho 38 penha de franca 37 tucuruvi 37 vila monumento 37 vila ema 36 sacoma 36 jardim da gloria 36 sumare 36 vila parque jabaquara 35 bosque da saude 35 santa teresinha 34 parque reboucas 34 alto da lapa 34 vila matilde 34 vila santa catarina 33 carandiru 33 jardim vila mariana 33 vila constanca 32 luz 32 vila isa 32 jardim vila formosa 32 parque edu chaves 31 jardim sao luis 31 vila nivi 30 parque continental 30 jardim europa 30 limoeiro 30 jardim iris 30 parada inglesa 30 americanopolis 30 vila siqueira (zona norte) 30 varzea da barra funda 28 vila re 28 vila nova mazzei 28 jardim consorcio 27 vila sao jose (ipiranga) 27 cidade mae do ceu 27 sitio do morro 27 parque grajau 27 cidade sao francisco 27 vila ester (zona norte) 27 jardim angela (zona leste) 26 jardim japao 26 socorro 26 vila congonhas 26 vila natal 26 vila alpina 26 jardim das acacias 26 jardim monte kemel 26 vila das belezas 26 vila invernada 25 se 25 jardim belem 25 vila firmiano pinto 24 parque munhoz 24 chacara santo antonio (zona leste) 24 pompeia 24 lajeado 24 cidade antonio estevao de carvalho 24 vila sabrina 24 jardim esmeralda 24 jardim umuarama 24 vila amelia 23 vila anastacio 23 parque santo antonio 23 parque sao domingos 23 vila bancaria munhoz 23 chacara california 23 jardim independencia 22 vila vermelha 22 vila guarani (z sul) 22 vila santa clara 22 parque sao lucas 22 vila isolina mazzei 22 jardim dom bosco 22 vila nova cachoeirinha 21 jardim londrina 21 chacara inglesa saude 21 jardim marajoara 21 chacara belenzinho 21 jabaquara 21 vila gomes 21 jardim brasil (zona sul) 21 jardim santa terezinha (zona leste) 21 cangaiba 21 vila do encontro 20 jardim pinheiros 20 cursino 20 caxingui 20 jardim analia franco 20 jardim franca 20 city america 20 paraisopolis 20 vila albertina 20 freguesia do o 19 parque america 19 jardim germania 19 jardim oriental 19 vila esperanca 19 parque casa de pedra 19 vila maria 19 conjunto residencial butanta 19 vila paiva 18 vila sao paulo 18 jardim silva teles 18 quarta parada 18 jardim caravelas 18 vila sonia 18 jardim taquaral 18 parque mandaqui 18 vila granada 18 jardim sao bernardo 18 vila california 18 bela alianca 18 jardim fonte do morumbi 18 quinta da paineira 18 jardim ester 17 jardim cotinha 17 jardim cidade pirituba 17 jardim jau (zona leste) 17 vila alexandria 17 parque independencia 17 chacara inglesa 17 vila lageado 17 vila gertrudes 17

Ser classificado como Marlin significa estar entre os melhores. Vê-se que a proporção de Marlins aumenta ao longo dos meses.

In [120]:
df_marlin_full = df_customer_segmentation.select('customer_id','marlin_tag','segmentation_month_month','ifood_status','ifood_status_last_month')

df_marlin_full_lag = df_marlin_full.withColumn('marlin_tag_prev',
                                            f.lag(df_marlin_full['marlin_tag'])
                                             .over(Window.partitionBy("customer_id")
                                             .orderBy("segmentation_month_month")))

df_marlin = df_marlin_full.groupby('marlin_tag','segmentation_month_month','ifood_status').count().orderBy('segmentation_month_month','marlin_tag')
display(df_marlin)

marlin_tag segmentation_month_month ifood_status count 1. Marlin 6 Inactive 11 1. Marlin 6 New 76 1. Marlin 6 Resurrected 62 1. Marlin 6 Active 5041 1. Marlin 6 Churn 3 2. Tilapia 6 Inactive 20 2. Tilapia 6 New 1401 2. Tilapia 6 Churn 59 2. Tilapia 6 Active 5609 2. Tilapia 6 Resurrected 780 3. Subsidy Carp 6 Inactive 27 3. Subsidy Carp 6 New 2110 3. Subsidy Carp 6 Resurrected 892 3. Subsidy Carp 6 Active 3255 3. Subsidy Carp 6 Churn 43 4. Retention Carp 6 Churn 104 4. Retention Carp 6 Active 3960 4. Retention Carp 6 Inactive 177 4. Retention Carp 6 New 1428 4. Retention Carp 6 Resurrected 4668 1. Marlin 7 Active 5997 1. Marlin 7 Inactive 11 1. Marlin 7 Churn 622 2. Tilapia 7 Inactive 57 2. Tilapia 7 Churn 2506 2. Tilapia 7 Active 6102 3. Subsidy Carp 7 Inactive 38 3. Subsidy Carp 7 Churn 3001 3. Subsidy Carp 7 Active 3149 4. Retention Carp 7 Inactive 68 4. Retention Carp 7 Active 3005 4. Retention Carp 7 Churn 5407 1. Marlin 8 Resurrected 237 1. Marlin 8 Churn 690 1. Marlin 8 Inactive 309 1. Marlin 8 Active 6880 2. Tilapia 8 Active 4418 2. Tilapia 8 Resurrected 1573 2. Tilapia 8 Churn 1768 2. Tilapia 8 Inactive 1647 3. Subsidy Carp 8 Active 1782 3. Subsidy Carp 8 Resurrected 333 3. Subsidy Carp 8 Inactive 2458 3. Subsidy Carp 8 Churn 904 4. Retention Carp 8 Active 745 4. Retention Carp 8 Inactive 3934 4. Retention Carp 8 Resurrected 1050 4. Retention Carp 8 Churn 1235 1. Marlin 9 Churn 838 1. Marlin 9 Inactive 590 1. Marlin 9 Active 7893 1. Marlin 9 Resurrected 253 2. Tilapia 9 Active 4255 2. Tilapia 9 Inactive 2274 2. Tilapia 9 Churn 1715 2. Tilapia 9 Resurrected 1887 3. Subsidy Carp 9 Inactive 2652 3. Subsidy Carp 9 Churn 523 3. Subsidy Carp 9 Resurrected 466 3. Subsidy Carp 9 Active 1081 4. Retention Carp 9 Active 200 4. Retention Carp 9 Churn 809 4. Retention Carp 9 Inactive 3844 4. Retention Carp 9 Resurrected 683 1. Marlin 10 Churn 29 1. Marlin 10 Active 8110 1. Marlin 10 Inactive 1429 1. Marlin 10 Resurrected 286 2. Tilapia 10 Active 4126 2. Tilapia 10 Inactive 3871 2. Tilapia 10 Churn 66 2. Tilapia 10 Resurrected 1830 3. Subsidy Carp 10 Inactive 3001 3. Subsidy Carp 10 Active 948 3. Subsidy Carp 10 Resurrected 414 3. Subsidy Carp 10 Churn 21 4. Retention Carp 10 Churn 38 4. Retention Carp 10 Active 114 4. Retention Carp 10 Inactive 4902 4. Retention Carp 10 Resurrected 778 1. Marlin 11 Resurrected 278 1. Marlin 11 Inactive 688 1. Marlin 11 Churn 685 1. Marlin 11 Active 7904 2. Tilapia 11 Churn 1596 2. Tilapia 11 Active 4040 2. Tilapia 11 Resurrected 1786 2. Tilapia 11 Inactive 2098 3. Subsidy Carp 11 Churn 353 3. Subsidy Carp 11 Inactive 2578 3. Subsidy Carp 11 Resurrected 253 3. Subsidy Carp 11 Active 1028 4. Retention Carp 11 Active 271 4. Retention Carp 11 Resurrected 964 4. Retention Carp 11 Inactive 4712 4. Retention Carp 11 Churn 729 1. Marlin 12 Inactive 686 1. Marlin 12 Resurrected 201 1. Marlin 12 Churn 678 1. Marlin 12 Active 7688 2. Tilapia 12 Inactive 1950 2. Tilapia 12 Churn 1474 2. Tilapia 12 Active 4119 2. Tilapia 12 Resurrected 1390 3. Subsidy Carp 12 Churn 318 3. Subsidy Carp 12 Active 1149 3. Subsidy Carp 12 Inactive 2529 3. Subsidy Carp 12 Resurrected 290 4. Retention Carp 12 Resurrected 1002 4. Retention Carp 12 Active 346 4. Retention Carp 12 Churn 989 4. Retention Carp 12 Inactive 5154

Assim como mais clientes passam a ser classificados como Marlin ao longo dos meses, os clientes classificados como Marlin mudam seu comportamento e alguns passam inclusive a ficar inativos. Em outubro 15% dos clientes classificados como Marlin estavam inativos.

In [122]:
display(df_marlin.filter(df_marlin['marlin_tag']=='1. Marlin').groupby('segmentation_month_month','ifood_status').sum('count').orderBy('segmentation_month_month',desc('ifood_status')))

segmentation_month_month ifood_status sum(count) 6 Resurrected 62 6 New 76 6 Inactive 11 6 Churn 3 6 Active 5041 7 Inactive 11 7 Churn 622 7 Active 5997 8 Resurrected 237 8 Inactive 309 8 Churn 690 8 Active 6880 9 Resurrected 253 9 Inactive 590 9 Churn 838 9 Active 7893 10 Resurrected 286 10 Inactive 1429 10 Churn 29 10 Active 8110 11 Resurrected 278 11 Inactive 688 11 Churn 685 11 Active 7904 12 Resurrected 201 12 Inactive 686 12 Churn 678 12 Active 7688

A tabela abaixo mostra a tag_marlin do próximo mês (eixo vertical) para quem era Marlin no mês anterior para cada um dos ifood_status (eixo horizontal).

Nota-se então que a grande maioria dos Inativos classificados como Marlin permanecem como Marlin no mês seguinte (2127). E o mesmo se aplica para quem deu Churn e era Marlin (2196).

In [124]:
df_marlin_lag = df_marlin_full_lag.filter(df_marlin_full_lag['marlin_tag_prev'] == '1. Marlin').groupby('marlin_tag','ifood_status_last_month').count()
df_marlin_full_lag_pivot = df_marlin_lag.groupby('marlin_tag').pivot('ifood_status_last_month').sum('count')
display(df_marlin_full_lag_pivot.orderBy('marlin_tag'))
# Uma vez Marlin, sempre Marlin? NÃO! O que precisa acontecer para alguém deixar de ser Marlin?

marlin_tag Active Churn Inactive New Resurrected 1. Marlin 38650 2196 2127 76 788 2. Tilapia 2621 689 921 null 606 3. Subsidy Carp 57 6 21 null 18 4. Retention Carp 7 1 103 null 35

##### NPS

A proporção de Promotores permanece maior que 75% em todos os meses, mas a proporção de Neutros e Detratores cresce ao longo do tempo.

In [127]:
df_nps_full = df_customer_segmentation.filter(df_customer_segmentation['last_nps'] != 'Sem Avaliacoes').select('customer_id','segmentation_month_month','last_nps')
df_nps = df_nps_full.groupby('segmentation_month_month','last_nps').count().orderBy('segmentation_month_month','last_nps')
display(df_nps)

segmentation_month_month last_nps count 6 Detractor 1025 6 Neutral 2004 6 Promoter 10527 7 Detractor 1048 7 Neutral 1991 7 Promoter 10557 8 Detractor 1015 8 Neutral 1920 8 Promoter 10174 9 Detractor 1037 9 Neutral 1927 9 Promoter 9541 10 Detractor 1053 10 Neutral 1884 10 Promoter 8820 11 Detractor 1101 11 Neutral 1939 11 Promoter 8775 12 Detractor 1138 12 Neutral 1983 12 Promoter 8608

Consequência do crescimento na proporção de Detratores e Neutros (e diminuição na proporção de Promotores), o NPS apresenta curva decrescente com considerável diminuição na inclinação a partir de Agosto.

In [129]:
df_nps_tot = df_nps_full.groupby('segmentation_month_month').count().withColumnRenamed('count','count_tot').withColumnRenamed('segmentation_month_month','segmentation_month_month_aux')
df_nps_join = df_nps.join(df_nps_tot, df_nps.segmentation_month_month == df_nps_tot.segmentation_month_month_aux, how='left')
df_nps_join = df_nps_join.withColumn('percent',col('count')/col('count_tot'))

df_nps_pivot_aux = df_nps_join.filter(df_nps_join['last_nps'] != 'Neutral').select('segmentation_month_month','last_nps','percent')
df_nps_pivot = df_nps_pivot_aux.groupby('segmentation_month_month').pivot('last_nps').sum('percent')
df_nps_pivot = df_nps_pivot.withColumn('nps',(col('Promoter') - col('Detractor')) * 100.0)

display(df_nps_pivot)

segmentation_month_month Detractor Promoter nps 12 0.0970244692642169 0.7339074089862734 63.68829397220564 6 0.07561227500737681 0.7765565063440543 70.09442313366775 9 0.08292682926829269 0.7629748100759696 68.0047980807677 8 0.07742772141276985 0.776108017392631 69.86802959798611 7 0.07708149455722271 0.7764783759929391 69.93968814357164 10 0.08956366420005103 0.7501913753508548 66.06277111508038 11 0.09318662716885315 0.7426999576809141 64.95133305120609

#### Sensibilidade a Benefícios

O índice médio de sensibilidade a benefícios tem curva crescente para todos os clientes da base.

In [132]:
display(df_customer_segmentation.groupby('segmentation_month_month').agg(avg('benefits_sensitivity')).orderBy('segmentation_month_month'))

segmentation_month_month avg(benefits_sensitivity) 6 0.6446650044406617 7 0.6470061006999089 8 0.6505910168027851 9 0.6572291486471352 10 0.6625707220513501 11 0.6630196065268191 12 0.662897751112593

O mesmo não se aplica para os clientes que são Churn, que tem comportamento bem mais instável.

In [134]:
display(df_customer_segmentation.filter(df_customer_segmentation['ifood_status'] == 'Churn').groupby('segmentation_month_month').agg(avg('benefits_sensitivity')).orderBy('segmentation_month_month'))

segmentation_month_month avg(benefits_sensitivity) 6 0.6527047685716415 7 0.6584145816031152 8 0.6579176234649798 9 0.6389272073584532 10 0.6733618834268185 11 0.6621119792442269 12 0.6675081493721615

#### Correlação de Variáveis

In [136]:
col_corr_graf =['orders_last_91d',
               'recency_months',
               #'days_to_reorder_at_datasource',
               #'days_to_reorder_at_concluded',
               'rfv_score',
               'recency_days',
               'recency_days_bucket',
               'freq_last_91d',
               'freq_last_91d_bucket',
               'avg_aov_last_91d',
               'maturity_orders',
               'maturity_orders_bucket',
               'benefits_sensitivity',
               'merchant_variety',
               'merchant_offer',
               'registration_month',
               #'registration_dayofweek',
               'first_order_month',
               #'first_order_dayofweek',
               'segmentation_month_month',
               #'segmentation_month_dayofweek',
               'last_order_month',
               #'last_order_dayofweek'
               ]

In [137]:
# Reference: https://stackoverflow.com/questions/55546467/how-to-plot-correlation-heatmap-when-using-pysparkdatabricks
vector_col = "corr_features"
assembler = VectorAssembler(inputCols=col_corr_graf,
                            outputCol=vector_col)
myGraph_vector = assembler.transform(df_customer_segmentation).select(vector_col)
matrix = Correlation.corr(myGraph_vector, vector_col)

# Gera uma lista de listas representando uma matriz de correlacao
matrix = Correlation.corr(myGraph_vector, vector_col).collect()[0][0]
corrmatrix_orders = matrix.toArray().tolist()
df_corr_orders = spark.createDataFrame(corrmatrix_orders,col_corr_graf)

In [138]:
corrmatrix_orders = matrix.toArray().tolist()
df_corr_orders = spark.createDataFrame(corrmatrix_orders,col_corr_graf)
plot_corr_matrix(corrmatrix_orders,col_corr_graf,fig_no=234, figsize=[15,10])

### 3 and 4. Orders and Orders with Cost/Revenue

#### Join bases de Pedidos e Pedidos com Custo/Receita

In [141]:
df_orders_total = join_removing_repeated(df_orders, df_orders_with_cost_revenue, df_orders.order_number == df_orders_with_cost_revenue.order_number, 'left')
df_orders_total.cache()

Out[11]: DataFrame[order_id: string, order_number: bigint, order_timestamp_local: string, order_shift: string, last_status_date_local: string, order_total: double, credit: double, paid_amount: double, delivery_type: string, scheduled: boolean, scheduled_creation_date_local: string, device_app_version: string, device_type: string, device_platform: string, payment_method: string, customer_state_label: string, customer_city: string, customer_district: string, customer_centroid_id: string, customer_has_plus: boolean, customer_seg_status_last_month: string, customer_seg_recency_bucket: double, customer_seg_frequency_bucket: double, customer_seg_merchant_offer_bucket: double, customer_seg_benefits_sensitivity_bucket: string, customer_seg_marlin_tag: string, customer_seg_gross_income_bucket: double, customer_seg_preferred_shift: string, frn_id: bigint, merchant_city: string, merchant_district: string, merchant_centroid_id: string, merchant_dish_type: string, distance_merchant_customer: double, promo_is_promotion: double, normal_items_quantity: double, promo_items_quantity: double, order_lag_at_login: double, order_lead_at_login: double, order_date_local: string, valid_order: bigint, session_id: string, customer_id: string, cohort_month: string, first_order_date: string, months_after_first_purchase: double, general_net_profit: double]

In [142]:
# Sanity check para verificar se o join está correto:
print(df_orders.count())
print(df_orders_with_cost_revenue.count())
print(df_orders_total.count())

492138
492138
492138

In [143]:
print('Orders with cost/revenue:     ', df_orders_total.count(), '   linhas e ', len(df_orders_total.columns), ' colunas')

Orders with cost/revenue: 492138 linhas e 47 colunas

#### Tratamento de Missings

Vemos que `customer_has_plus` tem muito missing, como esperado desde que esse é um teste. A abordagem usada vai ser definir `unknown` para as variáveis categóricas com missing. Para as numéricas, iremos adotar a média. Já para as númericas inteiras (ex: com buckets) vamos usar a média arredondada para o integer mais próximo.

In [146]:
colunas_orders_missing = percent_missing(df_orders_total).orderBy('perc_missing', ascending=False)
display(colunas_orders_missing)

variaveis total_missing perc_missing customer_has_plus 291126 59.15535886275801 customer_seg_preferred_shift 195687 39.7626275556856 customer_seg_marlin_tag 60587 12.310977815165664 order_lead_at_login 13431 2.729112565987589 customer_seg_frequency_bucket 8417 1.7102926414948652 customer_seg_recency_bucket 8417 1.7102926414948652 customer_seg_benefits_sensitivity_bucket 8417 1.7102926414948652 session_id 8346 1.69586579374078 customer_seg_gross_income_bucket 8301 1.686722016995233 customer_seg_status_last_month 8301 1.686722016995233 customer_seg_merchant_offer_bucket 8301 1.686722016995233 order_lag_at_login 5090 1.0342627474407584 device_app_version 2553 0.5187569340306987 promo_is_promotion 1 2.0319503878993292E-4 device_type 1 2.0319503878993292E-4 normal_items_quantity 1 2.0319503878993292E-4 promo_items_quantity 1 2.0319503878993292E-4 customer_state_label 0 0.0 customer_city 0 0.0 merchant_dish_type 0 0.0 customer_district 0 0.0 customer_centroid_id 0 0.0 merchant_centroid_id 0 0.0 distance_merchant_customer 0 0.0 order_total 0 0.0 paid_amount 0 0.0 scheduled 0 0.0 merchant_district 0 0.0 order_id 0 0.0 order_timestamp_local 0 0.0 last_status_date_local 0 0.0 device_platform 0 0.0 credit 0 0.0 order_date_local 0 0.0 delivery_type 0 0.0 valid_order 0 0.0 frn_id 0 0.0 merchant_city 0 0.0 months_after_first_purchase 0 0.0 order_number 0 0.0 order_shift 0 0.0 scheduled_creation_date_local 0 0.0 payment_method 0 0.0 cohort_month 0 0.0 customer_id 0 0.0 first_order_date 0 0.0 general_net_profit 0 0.0

In [147]:
# Para as colunas com missing, separar em categoricas e numericas
df_columns_orders_missing = colunas_orders_missing.filter(colunas_orders_missing['perc_missing'] > 0
                                                  ).select('variaveis')
list_df_columns_orders_missing = list([row[0] for row in df_columns_orders_missing.collect()])

filter_colunas_orders_numericas = [x[0] for x in df_orders_total[list_df_columns_orders_missing].dtypes if x[1] in ('double', 'long')]
filter_colunas_orders_numericas_int = [x[0] for x in df_orders_total[list_df_columns_orders_missing].dtypes if x[1] in ('int')]
filter_colunas_orders_categoricas = [x[0] for x in df_orders_total[list_df_columns_orders_missing].dtypes if x[1] not in ('double', 'int', 'long', 'boolean')]
filter_colunas_orders_booleanas = [x[0] for x in df_orders_total[list_df_columns_orders_missing].dtypes if x[1] in ('boolean')]

# Inputar unknown para colunas categoricas
for coluna in filter_colunas_orders_categoricas:
  df_orders_total = df_orders_total.fillna('unknown', subset=[coluna])

# Transformar colunas booleanas para string, depois inputar unknown
for coluna in filter_colunas_orders_booleanas:
  df_orders_total = df_orders_total.withColumn(coluna,col(coluna).cast('string'))
  df_orders_total = df_orders_total.fillna('unknown', subset=[coluna])

# Inputar media para colunas numericas
for coluna in filter_colunas_orders_numericas:
  media = df_orders_total.agg(mean(coluna)).collect()[0][0]
  df_orders_total = df_orders_total.fillna(media, subset=[coluna])
  
# Inputar media para colunas numericas inteiras arredondando para o integer mais perto
for coluna in filter_colunas_orders_numericas:
  media = df_orders_total.agg(mean(coluna)).collect()[0][0]
  df_orders_total = df_orders_total.fillna(media, subset=[coluna])
  df_orders_total = df_orders_total.withColumn(coluna, f.round(df_orders_total[coluna], 0))

In [148]:
len(list_df_columns_orders_missing)

Out[21]: 17

In [149]:
len(filter_colunas_orders_categoricas)

Out[17]: 7

In [150]:
len(filter_colunas_orders_numericas)

Out[19]: 9

In [151]:
len(filter_colunas_orders_booleanas)

Out[20]: 1

In [152]:
display(df_orders_total)

order_id order_number order_timestamp_local order_shift last_status_date_local order_total credit paid_amount delivery_type scheduled scheduled_creation_date_local device_app_version device_type device_platform payment_method customer_state_label customer_city customer_district customer_centroid_id customer_has_plus customer_seg_status_last_month customer_seg_recency_bucket customer_seg_frequency_bucket customer_seg_merchant_offer_bucket customer_seg_benefits_sensitivity_bucket customer_seg_marlin_tag customer_seg_gross_income_bucket customer_seg_preferred_shift frn_id merchant_city merchant_district merchant_centroid_id merchant_dish_type distance_merchant_customer promo_is_promotion normal_items_quantity promo_items_quantity order_lag_at_login order_lead_at_login order_date_local valid_order session_id customer_id cohort_month first_order_date months_after_first_purchase general_net_profit 56e7da7d-1019-4176-95c7-18677cf88138 667770135 2019-06-01T00:51:27.395Z weekend dawn 2019-06-01T06:33:20.137Z 29.0 4.0 25.0 DELIVERY false 2019-06-01T00:51:27.395Z Android_iFood_8.48.3 MOBILE ANDROID OTHERS_OFFLINE CE FORTALEZA Itaoca -3.77-38.55 unknown Active 2.0 4.0 5.0 Alta 3. Subsidy Carp 6.0 unknown 177457 FORTALEZA Democrito Rocha -3.76-38.57 Pizza 2265.780724667483 0.0 2.0 0.0 9.0 83.0 2019-06-01T00:00:00.000Z 1 abc8cd16-4b84-415c-8109-3a90ccf7ebcf abd722bdf397dbb6781354d0731b03bca2070ee4d60134feb0ff9ecae3617b4d 2019-01-01T00:00:00.000Z 2019-01-28T00:00:00.000Z 5.0 6.704 327a5c8f-9502-4671-9993-972accb291f0 667772160 2019-06-01T00:56:32.740Z weekend dawn 2019-06-01T06:41:05.017Z 34.9 4.0 30.9 DELIVERY false 2019-06-01T00:56:32.740Z iOS_iFood_9.2.0 MOBILE IOS CC_ONLINE MG BELO HORIZONTE Olaria (barreiro) -19.99-44.03 unknown Inactive 4.0 2.0 5.0 Media 4. Retention Carp 6.0 5. Jantar 260680 BELO HORIZONTE Flavio Marques Lisboa (barreiro) -19.99-44.0 Sorvetes 3071.509982380759 0.0 1.0 0.0 69.0 1.0 2019-06-01T00:00:00.000Z 1 d3abd2cc-93a2-44f5-a39d-1d684cac763e 83b3746d937cb40cd850794804284d8950845be290aedb0f3d3896e41df3f8d8 2018-06-01T00:00:00.000Z 2018-06-17T00:00:00.000Z 12.0 7.61841875 454fde87-b7e5-4c67-a5d2-356aeb339a44 669393616 2019-06-01T11:47:20.979Z weekend lunch 2019-06-01T12:18:53.882Z 55.9 4.0 51.9 DELIVERY false 2019-06-01T11:47:20.979Z iOS_iFood_9.2.0 MOBILE IOS CC_OFFLINE DF BRASILIA Asa Sul -15.81-47.91 unknown Active 3.0 5.0 5.0 Media 3. Subsidy Carp 6.0 unknown 211400 BRASILIA Setor De Habitacoes Individuais Sul -15.85-47.89 Marmita 4371.288354253842 1.0 0.0 2.0 18.0 2.0 2019-06-01T00:00:00.000Z 1 ac32568d-ebc6-4a6b-b801-87c50cb8da59 a63624c4d82738687bee190af3dd6e534007ee451ae681ee91c4984b4c95d905 2017-07-01T00:00:00.000Z 2017-07-18T00:00:00.000Z 23.0 1.565851111837798 5c007a8b-6b22-461f-9919-2b7754c4e72d 669406022 2019-06-01T11:59:24.212Z weekend lunch 2019-06-01T14:02:49.540Z 30.5 4.0 26.5 DELIVERY false 2019-06-01T11:59:24.212Z Android_iFood_9.3.1 MOBILE ANDROID OTHERS_OFFLINE SC SAO JOSE Rocado -27.59-48.62 unknown Active 1.0 3.0 5.0 Alta 2. Tilapia 6.0 unknown 184913 SAO JOSE Kobrasol -27.6-48.61 Comida Brasileira 903.747462995218 0.0 1.0 0.0 8.0 12.0 2019-06-01T00:00:00.000Z 1 9dbb825d-2a32-4d2d-9d67-b917253dd028 9bc258be21067f360696eb3aae36f1c6d902ad2f98c2e59ceeee11d5da830d17 2018-01-01T00:00:00.000Z 2018-01-12T00:00:00.000Z 17.0 6.86375 4b8c13a8-df68-40bb-a9a4-2ea60f7000b3 669484170 2019-06-01T13:00:25.188Z weekend lunch 2019-06-01T13:40:27.776Z 67.9 4.0 63.9 DELIVERY false 2019-06-01T13:00:25.188Z iOS_iFood_9.2.0 MOBILE IOS CC_ONLINE RJ RIO DE JANEIRO Copacabana -22.99-43.19 unknown Active 4.0 3.0 5.0 Alta 2. Tilapia 6.0 unknown 224519 RIO DE JANEIRO Leblon -22.98-43.22 Carnes 3316.477781154116 0.0 1.0 0.0 30.0 6.0 2019-06-01T00:00:00.000Z 1 606080a2-4523-4dbb-8066-a3db8f4dcf4f 6f5ae153404c42fbab723806b3f1a0bf80ba303ca62b72658b715c09406f94b4 2013-05-01T00:00:00.000Z 2013-05-14T00:00:00.000Z 73.0 7.0330499999999985 285b824a-c7ff-4bd0-8919-ccdd72f14e8d 669651996 2019-06-01T16:25:09.268Z weekend snack 2019-06-

#### Tratamento de Datas

In [154]:
# importante: transformar primeiro para timestamp, depois para date!!!
df_orders_total = df_orders_total.withColumn('order_timestamp_local', from_utc_timestamp('order_timestamp_local', 'UTC'))\
                                 .withColumn('last_status_date_local', from_utc_timestamp('last_status_date_local', 'UTC'))\
                                 .withColumn('scheduled_creation_date_local', from_utc_timestamp('scheduled_creation_date_local', 'UTC'))\
                                 .withColumn('order_date_local', from_utc_timestamp('order_date_local', 'UTC'))\
                                 .withColumn('cohort_month', from_utc_timestamp('cohort_month', 'UTC'))\
                                 .withColumn('first_order_date', from_utc_timestamp('first_order_date', 'UTC'))\
                                 .withColumn('order_date_local', to_date('order_date_local', 'YYYY-MM-DD'))\
                                 .withColumn('cohort_month', to_date('cohort_month', 'YYYY-MM-DD'))\
                                 .withColumn('first_order_date', to_date('first_order_date', 'YYYY-MM-DD'))\
                                 .withColumn('order_date_local_month', month('order_date_local'))\
                                 .withColumn('order_date_local_dayofweek', dayofweek('order_date_local'))
display(df_orders_total)

order_id order_number order_timestamp_local order_shift last_status_date_local order_total credit paid_amount delivery_type scheduled scheduled_creation_date_local device_app_version device_type device_platform payment_method customer_state_label customer_city customer_district customer_centroid_id customer_has_plus customer_seg_status_last_month customer_seg_recency_bucket customer_seg_frequency_bucket customer_seg_merchant_offer_bucket customer_seg_benefits_sensitivity_bucket customer_seg_marlin_tag customer_seg_gross_income_bucket customer_seg_preferred_shift frn_id merchant_city merchant_district merchant_centroid_id merchant_dish_type distance_merchant_customer promo_is_promotion normal_items_quantity promo_items_quantity order_lag_at_login order_lead_at_login order_date_local valid_order session_id customer_id cohort_month first_order_date months_after_first_purchase general_net_profit order_date_local_month order_date_local_dayofweek 56e7da7d-1019-4176-95c7-18677cf88138 667770135 2019-06-01T00:51:27.395+0000 weekend dawn 2019-06-01T06:33:20.137+0000 29.0 4.0 25.0 DELIVERY false 2019-06-01T00:51:27.395+0000 Android_iFood_8.48.3 MOBILE ANDROID OTHERS_OFFLINE CE FORTALEZA Itaoca -3.77-38.55 unknown Active 2.0 4.0 5.0 Alta 3. Subsidy Carp 6.0 unknown 177457 FORTALEZA Democrito Rocha -3.76-38.57 Pizza 2265.780724667483 0.0 2.0 0.0 9.0 83.0 2019-06-01 1 abc8cd16-4b84-415c-8109-3a90ccf7ebcf abd722bdf397dbb6781354d0731b03bca2070ee4d60134feb0ff9ecae3617b4d 2019-01-01 2019-01-28 5.0 6.704 6 7 327a5c8f-9502-4671-9993-972accb291f0 667772160 2019-06-01T00:56:32.740+0000 weekend dawn 2019-06-01T06:41:05.017+0000 34.9 4.0 30.9 DELIVERY false 2019-06-01T00:56:32.740+0000 iOS_iFood_9.2.0 MOBILE IOS CC_ONLINE MG BELO HORIZONTE Olaria (barreiro) -19.99-44.03 unknown Inactive 4.0 2.0 5.0 Media 4. Retention Carp 6.0 5. Jantar 260680 BELO HORIZONTE Flavio Marques Lisboa (barreiro) -19.99-44.0 Sorvetes 3071.509982380759 0.0 1.0 0.0 69.0 1.0 2019-06-01 1 d3abd2cc-93a2-44f5-a39d-1d684cac763e 83b3746d937cb40cd850794804284d8950845be290aedb0f3d3896e41df3f8d8 2018-06-01 2018-06-17 12.0 7.61841875 6 7 454fde87-b7e5-4c67-a5d2-356aeb339a44 669393616 2019-06-01T11:47:20.979+0000 weekend lunch 2019-06-01T12:18:53.882+0000 55.9 4.0 51.9 DELIVERY false 2019-06-01T11:47:20.979+0000 iOS_iFood_9.2.0 MOBILE IOS CC_OFFLINE DF BRASILIA Asa Sul -15.81-47.91 unknown Active 3.0 5.0 5.0 Media 3. Subsidy Carp 6.0 unknown 211400 BRASILIA Setor De Habitacoes Individuais Sul -15.85-47.89 Marmita 4371.288354253842 1.0 0.0 2.0 18.0 2.0 2019-06-01 1 ac32568d-ebc6-4a6b-b801-87c50cb8da59 a63624c4d82738687bee190af3dd6e534007ee451ae681ee91c4984b4c95d905 2017-07-01 2017-07-18 23.0 1.565851111837798 6 7 5c007a8b-6b22-461f-9919-2b7754c4e72d 669406022 2019-06-01T11:59:24.212+0000 weekend lunch 2019-06-01T14:02:49.540+0000 30.5 4.0 26.5 DELIVERY false 2019-06-01T11:59:24.212+0000 Android_iFood_9.3.1 MOBILE ANDROID OTHERS_OFFLINE SC SAO JOSE Rocado -27.59-48.62 unknown Active 1.0 3.0 5.0 Alta 2. Tilapia 6.0 unknown 184913 SAO JOSE Kobrasol -27.6-48.61 Comida Brasileira 903.747462995218 0.0 1.0 0.0 8.0 12.0 2019-06-01 1 9dbb825d-2a32-4d2d-9d67-b917253dd028 9bc258be21067f360696eb3aae36f1c6d902ad2f98c2e59ceeee11d5da830d17 2018-01-01 2018-01-12 17.0 6.86375 6 7 4b8c13a8-df68-40bb-a9a4-2ea60f7000b3 669484170 2019-06-01T13:00:25.188+0000 weekend lunch 2019-06-01T13:40:27.776+0000 67.9 4.0 63.9 DELIVERY false 2019-06-01T13:00:25.188+0000 iOS_iFood_9.2.0 MOBILE IOS CC_ONLINE RJ RIO DE JANEIRO Copacabana -22.99-43.19 unknown Active 4.0 3.0 5.0 Alta 2. Tilapia 6.0 unknown 224519 RIO DE JANEIRO Leblon -22.98-43.22 Carnes 3316.477781154116 0.0 1.0 0.0 30.0 6.0 2019-06-01 1 606080a2-4523-4dbb-8066-a3db8f4dcf4f 6f5ae153404c42fbab723806b3f1a0bf80ba303ca62b72658b715c09406f94b4 2013-05-01 2013-05-14 73.0 7.0330499999999985 6 7 285b824a-c7ff-4bd0-8919-ccdd72f14e8d 669651996 2019-06-01T16:25:09.268+0000 weekend snack 2019-06-01T18:25:26.004+0000 36.9 4.0 32.9 DELIVERY false 2019-06-01T16:25:09.268+00

#### Exploração Ordens

Temos +30k clientes que fizeram pedidos no periodo analisado.

In [157]:
df_orders_total.select(f.countDistinct('customer_id')).show()

+---------------------------+
count(DISTINCT customer_id)|
+---------------------------+
 30079|
+---------------------------+

`74%` dos clientes fizeram entre 0 e 10 pedidos. `91%` fizeram até 20 pedidos.

In [159]:
display(df_orders_total.groupBy('customer_id')\
                           .count()\
                           .withColumnRenamed('count', 'number_orders'))

customer_id number_orders 8e5f08475a5a81e15af97e2d9b2f49e0d795165f2d92dab2868c3b975ad075e8 32 e598f9ab70ce2aa561bf6f58adee027e17fe361722c3682caa2e15cac959f973 110 03f34adb449900100080d2defbf63b44e86e4632754e3d22720c99b95a318116 47 0087f7139bba1b717477767e6b0c4e08e0de5138c48a58bf34e3672fdb59c32a 18 a2332388f4a574f90b0bcf93cd4f37ec9902222217d02b7516f93e9b1ec2bab6 5 c093589580243a2b025f35cf3039a9952ea6be8ee2af4dc119d4f27da4578f08 14 e01a6c7a8339f7951bcf3d62dd5aaced75c48210489f15b6c32b6e8b52e40d49 68 f92562aaf4bfdfcd0576ea920d2d65a215dcabf4250739f26ffe8c32c3524f6b 8 39263b649334376ac6d6b9ec955a2f23e3f43f9986e5802a3da391469e49d739 26 8d2898750cf496417354a7da91095a7f1483da777e117df21d49e4d8fdf4f2f3 75 57e069c1e9360d9ecf7af4004bf21595f8ed759b4142131c48643b5a213e3b51 18 6d3eb0731581bb6eabd95867358a57e656cbf22559fe2176d10d4513ca2c3d72 27 0f595311e383989f9e0e90541024fdf0563f6943fd255e285e7a52dc172d89ce 27 e12a45aba2aef7a01cbc462fdf9c864789836b6921198f94fc7bb1d4470032ce 28 4a0bef219eefc8da3054af052c57a5aaac2694362e59d85012b880eadfc566db 14 dbcaf495091b2c361f2ced33a2427e8a4b70f7d7f02afc2b25fb244fcf5930ed 17 0642cb4d8e4b491f44a0ff6e8afdd16a7e59a6e41ecbbf41db494d161c19f406 38 b5b7f2da83dcf67c00a29c79a8b45d753363e860f01ca1f63c4bfe6df6e4377d 7 3b54fae8f774b3fc6dcc4eeb0b97ba9be650814d897467756a39b92c29c2535f 29 25d3df3245fb6d5a9f428a8c2553712c10019a541cd797b230caa5546d4e8f63 34 2bc718c6da40b1e390a32b2e69ece7ed24d151791dc50e2c466a2103cfcd6d07 22 187f7cee9769ab901ee84cc14d7fcbba2ab281c8484799349909ba4091438e4a 42 16fb7325b949f58d88c967eabaa2f18ea74168a4c09e29826ff30011c812540a 101 6f276bc04959b19bfef955e908d820822a8ad17f0c3ca516162541f2ca59e134 49 9ee700862563ee5cfc2662cfab328ebec0b0917faac0bbb429a6c06fde1da823 26 ab703fbf55ae2b19c0cc6db17f7a591ad226a9c4b93e991f6fa4944fddc585af 7 de39115680e14a3a3911662d39eacfec58baf5d951b824cd0215253fc2fbf3d2 39 28aeb0d9f56e8e983aede25ea8717cd71ca4babe4031b396f9dff13440467724 35 86d15d31542b6b43e167b610bc5ebcf2f4a3999e422288ada536c58f1463f2ed 45 61e692ed4286dac8e65ddce1b61ef4a35b22cd796fcaac27694946d237dab682 9 ddf2b319169c2e7a7cc805ce6c295c7d62f37bf4e57396d2ea09de32e320979b 32 dd827e7685ea63eacc57fa0cd7821fcdabb7cfbe26a17b6aeffd59cdaa5dd2cb 18 2f1804957f27bdfb3dcbd3223da966b4f54d9246299988c5c99eada48f0d8855 8 64ad85a2f0c182b18f429f5a0e08797dd9cb1d2583d15eb3e509c9c2426a128f 39 bfad3ea1d3db2f36789bb04dca6bea5ce5ab43f193b2cb30d726c0ff0beaf5f6 14 e20cd892fb81f9071051afc85e8afb8f5931e35e563bfc3bfa38dbee47f16184 48 8dc587dda3e986cd91bfeeff44564fa7564a5ecebc0dcab58b800c1d81ed5144 19 84eabd6cd44152a60b9349cc1d5e93114a1f0c08078e94c3163562261196184c 57 7d6d6eb828c10f08317adf58b6f3030d6a609d00d792f7ec02377dcc324138b1 31 cc8f67b32b0e47f4c87904cdb61b489be4f0eea0a23986089b86a51bc807d616 8 3ffc5923b75600d395f191f6b3b8585adf4d67799072d556f6a7457c46fbf12b 20 1459a58458a4600c57b05cd1aacccb99c27e7cf96b34bfa2901a65a7381242f2 25 06b21b70f58408d4c316e88fc04b94a4cb9c834579150147a463202f544c2326 35 e129b2e529657a4d2030e59c5de4e7e76e0726b207b64037adf3dab1b42ae6db 4 5fffda88aba97152dd88b31c2688d8aba7bb5d0dc96d3a6fcb6df910fb9a5067 6 24749a23fc629d03668a325d4feccaa398fc18ecdce3a8a3c5e36cf4b90a69f8 32 09db60ddf2e8fc87cc826859f4370b6f8269feb91f295558ae89830366e6d88c 28 230da947a6484c9880980102eda15178e021959c314710bc31f30c458424a896 14 c66c552f0543a4a78b20a68ff9a92eb2fb5ea0d0005987cc5c5e507a867034b9 18 ec94e574e0ba5972b23422ebcbf962da0866c367adf70ba6b9b7163870e604d3 8 94fdc745e30c2d4b09afb228045664ca891ff36f8a19002d5a18ad66a98246b6 10 39fc016fd5dd3c9a4ea215f5d4d0a97a90b41d2aa4a2d1e7c188a0f030c59348 13 418f49d29aa234c99fea35b44bc8f4691862d4fdea39052c14077b98d8f19de1 30 f029a2605ac6dfe994d4b67f22193e94ac2972262459e2ce5ae0acd08ff94613 5 67a40a4099418493a29e5c329c11f856ee8a385859d057496aa8b4022827acc4 15 96c12802fce9c6684136ac3acdb85775570ff8380b7717ddf8ff30cc474a0599 7 ca229968f6c20721d159e4eb9709d2ecb265f8e2124b4f09cdca55f3ec4eeef3 8 757f6049de99510962c122ec2b4577658a63e4f062290237607c762047b0fb6c 1 72bd61fbf0bba01355347e5085caf9304862fe8599

In [160]:
avg_order = df_orders_total.groupBy('customer_id')\
                           .count()\
                           .withColumnRenamed('count', 'number_orders')
avg_order = avg_order.withColumn('orders_range', order_range(avg_order.number_orders))\
                     .orderBy('orders_range', asc=True)

display(avg_order)

customer_id number_orders orders_range 1226f2861f1c3e97f12133da94fe3007c8654f2ecfd307d78ed539bb6a2fc129 2 1- < 5 cae6670d1e0b6d17366fbe8976045fffa8871558af1f0b525d9995ae8811b6c3 4 1- < 5 e27807191cabd1e818a151299aeb3353013956ae83887082551148ee6924f22c 1 1- < 5 5600ce927ea122946d8861a9397156d4a89fb2647d8bf82c2daec3238845ea4a 3 1- < 5 58fe654421ef13d2a1b9071f5f2b64fe90212e68441c62b1170de1bbe11e720c 1 1- < 5 e1af52e094fc45bcb0cbbb2a04a0a5bcd6244c39b85329bfe6b5d9d9ec56bc3c 1 1- < 5 3c8757f078ee76a46c0036ba1b7f3cb623120368033152253c49c0af9fad88ed 4 1- < 5 78e26a93b4badc9550d5a8d85a70e4d4b8b2105d491b54562146918cbf54b567 1 1- < 5 40fb865f9aea9dc52872c4fa68f24bd68786696540287b24c595de3f7347f37d 3 1- < 5 e702f47372b0db2abb5ddb06990d3d83e2fed434c08f69b745a5e4e1fdbc4755 3 1- < 5 421eb400acecd307b41c4820ed7ab6ba912f97bf1df09ad1b649bf9399632d3e 1 1- < 5 cd0c2109104f1187b39688ff1e319a5939eae3a74350369526b8cf29efc63a67 3 1- < 5 7811e4fdf9c4ff8edff11a9bf78852e49af1524949b154f5e42dfc50fd65e66e 1 1- < 5 07459e182a04c27a8975e9cb6c0b5f73c1087d854fa9bfab7d7977824f425335 3 1- < 5 0b43e37bfaa8ad1c1987375fb48b247b50ec5e4744abb47d7aa6b21769440802 1 1- < 5 bb8d58ed61a4efaab57310738d6046cb28677965f8bf93167174d4c046639b7e 1 1- < 5 13953cb1f0dcb3cf5d673cc93e728226c274fc39089cc9c3d6267ab978d4203b 1 1- < 5 f1ced9c036d4860bae034e58ff4a4e6638594e11958c92d145d7d94ea2261b5c 2 1- < 5 6c2c38966081f853107dccdc10498bbbcde61107645acd76a452fd978a0c49e6 3 1- < 5 d0441e0838d4309865b67c17fe9cfd773a11a40588da330f848dadc163a3094d 1 1- < 5 ed39188460eacafb82e57e5bf7ff0d4c93bd31a15abbb652b0588b2426234cc9 1 1- < 5 b55dd2ba7ce399b30fc8ed8862315a1d5e0b501e6619f9faeb69624e68fde505 4 1- < 5 40bf6ac65b6036b92337c1dd1e8a35b7f554d71e8c296b8d90597f72f96b3722 1 1- < 5 676cfc8d192390f745cf471bce13dae10d2570c6f4eba577d0bb550394c72ff0 2 1- < 5 cec20f1e869688afd6e4ce6ed26cff7affedc8c1135de736b8de2b4b684b78c5 3 1- < 5 b6c9cdddf14cf84d8b778aacc9476f74e34c71b75d1d3e23f12cd709fe05e4e2 1 1- < 5 4566e21103e43b17150182e78d794c8d505ae8766794c9de74ef57da582eaef4 2 1- < 5 98e529066727d670bb5231ab6051e046c0f3c61d52c5f194891e3cbb0e2e8f9d 1 1- < 5 3008730f564ffad967771c8bd29263daba99f7106254d883c133688c47dc57d0 4 1- < 5 67f771934bbf47c858863b9c8cf08391276afac5f2e5daabe7fe244b85ca32e8 1 1- < 5 72604d67b56949dedbcbb99343c639fa4f55ef3b0fd38da00e0f7b93eef16048 2 1- < 5 3d78cace40bfb677c72400c89cd35c41d978b469cfa8c98c4e9f5e647dc6336d 1 1- < 5 001ecec2f34e64c3a5ea847f416889c6414d2003d067797d543d49ab9a9a8c09 1 1- < 5 e73743f29f64d60dbdb5584a551543010f3bdb47c93a510d47226a4133324a35 1 1- < 5 e7588a8ea6c9fae17a686b4b500f90549ab4e2baeb48ce0bfa68759fc2f72fb7 1 1- < 5 8c9c9194598fbea397d8e7d9f7de5105c652d360554cfc610601180c576e9794 4 1- < 5 6e5d8c6db5d7df6ba4a917a1f0402a20f45644caf07e696290eb34cbe5e90848 1 1- < 5 9bdbe27830e3d0db0719fb8a23118c6b53b747c8473141a37c016417c9674260 1 1- < 5 3e2f1408fc9e4b00aa11b981a6a01212290efadca0d51017286faed035cad75d 4 1- < 5 1c61975b330cd7bce9b7569e32e2a437e213f1ee71fbf2c1283b29a0d1e50451 3 1- < 5 5b6126099289a487b83762a07316b58956aa2e50719d45c05c441e97a5956293 3 1- < 5 9a1adb88263980082a2a7fa01793a883de614f260f00f4eddd009ea3a5a4b506 3 1- < 5 ecfc45be4c8d06311ad2e58280379bbfe28a867d3dd843cddfb59cb6d0bace1e 4 1- < 5 b629e1e6dcc5fc1ad35b11930912d0e5d284319830d0d9585b16be0078cb7bd0 3 1- < 5 0eeba330cd098e485f1fa36cbed39d28790202b844ebcf4a8f5f6c94f09f7c53 3 1- < 5 f727d29b7fe69bd6b1735d6b6e48ad682f9705db2525b91a1baa1e4f68dfaddd 1 1- < 5 05c2ba1c1402a1be605e9ae900e4d7ab7841e00bfed1d21a703717d4d774cacb 2 1- < 5 92c4c11970c5b75913bcc90e6626019573f39a0b3c95850461c7e7ff216c2c78 1 1- < 5 e0d16f36712d344c153e2011552af75028493204fe127fed3b92204c03bbe56a 3 1- < 5 4067257831f7f29cd4d9e5c5bdcfbf958d15440cef130d47c673e36da19108bd 1 1- < 5 469db0a5d144a8a202aa43ae03b0e28b814df4e69b707c15c10f843ce10381e9 1 1- < 5 dcfcb11e9c8feb7e7d23d23eb96f3690a1a704aef43b5f234c6613a647034cab 3 1- < 5 a8dc42b63f8a1e94110b38857f0f729b7fa18f791cf79e6ed7cbc7b8213bebef 1 1- < 5 13e2237aca730128f393eafa984a2fcc3ab32c7

Os `+30k` clientes fizeram `+492k` pedidos. A média de pedidos por cliente foi de `16.4`.

In [162]:
chosen_column = 'number_orders'
exprrs = [sum(chosen_column), max(chosen_column), min(chosen_column), stddev(chosen_column), mean(chosen_column)]
display(avg_order.agg(*exprrs))

sum(number_orders) max(number_orders) min(number_orders) stddev_samp(number_orders) avg(number_orders) 492138 421 1 21.06712970559962 16.36151467801456

#### Variáveis Qualitativas

In [164]:
display(percentByCol(df_orders_total, 'device_app_version'))

device_app_version cnt_per_group percent 9.30.0 21766 4.42274321430168 Android_iFood_9.4.1 18141 3.686161198688173 9.27.0 15499 3.14931990620517 iOS_iFood_9.5.0 15345 3.1180278702315203 Android_iFood_9.8.0 12161 2.471054866724374 Android_iFood_9.20.0 12148 2.468413331220105 iOS_iFood_9.17.1 11089 2.253229785141566 9.28.1 10916 2.2180770434309074 iOS_iFood_9.18.0 10897 2.214216337693899 iOS_iFood_9.8.1 10574 2.1485843401647506 Android_iFood_9.3.1 10039 2.0398749944121364 Android_iFood_9.23.0 9958 2.023416196270152 Android_iFood_9.6.2 9736 1.9783068976587868 Android_iFood_9.12.0 9058 1.8405406613592123 Android_iFood_9.18.2 9030 1.8348512002730941 Android_iFood_9.24.2 8629 1.753369989718331 Android_iFood_9.13.0 8150 1.6560395661379532 9.28.0 8006 1.626779480552203 iOS_iFood_9.23.0 7719 1.5684625044194922 9.29.1 7472 1.5182733298383786 iOS_iFood_9.20.0 7424 1.5085199679764618 Android_iFood_9.14.1 7299 1.4831205881277203 Android_iFood_9.22.1 7294 1.4821046129337707 Android_iFood_9.7.1 7271 1.477431127041602 9.31.0 7052 1.432931413546607 iOS_iFood_9.16.1 6879 1.3977786718359484 iOS_iFood_9.24.1 6668 1.3549045186512727 Android_iFood_9.7.2 6410 1.30248019864347 Android_iFood_9.26.0 6213 1.262450776001853 iOS_iFood_9.11.0 6078 1.2350194457652122 iOS_iFood_9.14.0 5959 1.2108392361492102 Android_iFood_9.25.1 5799 1.178328029942821 iOS_iFood_9.6.1 5697 1.1576021359862478 iOS_iFood_9.25.0 5686 1.1553669905595585 Android_iFood_9.9.5 5640 1.1460200187752216 Android_iFood_9.21.1 5515 1.12062063892648 iOS_iFood_9.9.0 5490 1.1155407629567315 Android_iFood_9.16.1 5445 1.1063969862111847 iOS_iFood_9.2.1 5444 1.1061937911723947 iOS_iFood_9.13.0 5355 1.0881094327200906 iOS_iFood_9.12.0 5332 1.0834359468279222 iOS_iFood_9.2.0 5188 1.0541758612421719 9.26.0 4855 0.9865119133251242 Android_iFood_9.19.1 4613 0.9373387139379605 Android_iFood_9.17.1 4280 0.8696747660209129 iOS_iFood_9.15.0 4201 0.8536223579565081 Android_iFood_9.15.2 4160 0.8452913613661209 iOS_iFood_9.24.0 4128 0.8387891201248431 Android_iFood_9.11.0 4087 0.8304581235344558 Android_iFood_9.11.3 4055 0.823955882293178 iOS_iFood_9.26.0 3643 0.7402395263117256 Android_iFood_9.9.2 3634 0.7384107709626162 Android_iFood_9.17.2 3412 0.6933014723512511 iOS_iFood_9.10.0 3344 0.6794842097135356 Android_iFood_9.5.4 3291 0.6687148726576692 Android_iFood_9.15.1 3284 0.6672925073861397 iOS_iFood_9.4.0 2890 0.5872336621029061 unknown 2553 0.5187569340306987 iOS_iFood_9.21.1 2503 0.5085971820912021 Android_iFood_9.24.0 2495 0.5069716217808826 Android_iFood_9.2.3 2086 0.42386485091580006 Android_iFood_9.24.1 2043 0.4151274642478329 9.29.0 2039 0.4143146840926732 iOS_iFood_9.19.0 1680 0.3413676651670873 Android_iFood_9.16.0 1635 0.3322238884215403 Android_iFood_9.25.0 1447 0.2940232211290329 Android_iFood_9.17.0 1390 0.28244110391800675 Android_iFood_8.48.3 1202 0.24424043662549935 iOS_iFood_9.7.2 1151 0.23387748964721278 Android_iFood_9.1.1 1147 0.23306470949205305 iOS_iFood_8.54.1 1110 0.22554649305682553 iOS_iFood_9.6.0 1081 0.21965383693191748 Android_iFood_8.47.0 1043 0.21193242545790003 iOS_iFood_9.22.1 1033 0.2099004750700007 iOS_iFood_9.22.0 1008 0.20482059910025238 iOS_iFood_9.1.0 971 0.19730238266502484 Android_iFood_9.0.4 960 0.19506723723833558 iOS_iFood_9.7.0 874 0.17759246390240135 iOS_iFood_9.19.4 841 0.17088702762233357 Android_iFood_9.11.2 801 0.16275922607073626 webapp_5.0.1 748 0.15198988901486982 webapp_4.7.1 709 0.14406528250206244 9.23.0 709 0.14406528250206244 webapp_4.11.0 702 0.1426429172305329 iOS_iFood_9.0.0 643 0.13065440994192687 Android_iFood_9.5.2 622 0.12638731412733828 webapp_5.2.3 610 0.12394897366185907 webapp_5.4.1 602 0.12232341335153961 iOS_iFood_9.19.3 587 0.11927548776969062 webapp_4.9.0 556 0.1129764415672027 9.25.0 533 0.10830295567503424 iOS_iFood_8.51.0 526 0.10688059040350471 webapp_5.0.6 513 0.10423905489923559 iOS_iFood_8.54.0 503 0.10220710451133626 iOS_iFood_8.50.0 493 0.10017515412343692 9.25.1 466 0.09468888807610873 iOS_iFood_8.52.0 465 0.09448569303731

In [165]:
# 97% dos pedidos são realizados via celular.
display(percentByCol(df_orders_total, 'device_type'))

device_type cnt_per_group percent MOBILE 479398 97.41129520581626 SITE 12739 2.5885015991449554 unknown 1 2.0319503878993292E-4

In [166]:
# Share de pedidos retirados nos restaurantes ainda é bem baixo: 0.33%
display(percentByCol(df_orders_total, 'delivery_type'))

delivery_type cnt_per_group percent DELIVERY 490513 99.66980806196636 TAKEOUT 1625 0.330191938033641

In [167]:
# 98% dos pedidos não são agendados
display(percentByCol(df_orders_total, 'scheduled'))

scheduled cnt_per_group percent false 485424 98.6357485095644 true 6714 1.3642514904356096

In [168]:
# 55% dos pedidos foram feitos em celular android. 42% em IOS: A penetração de mercado em iphone é elevada.
display(percentByCol(df_orders_total, 'device_platform'))

device_platform cnt_per_group percent ANDROID 274822 55.842466950326944 IOS 207432 42.14915328627336 DESKTOP 9883 2.008176568360907 OTHER 1 2.0319503878993292E-4

#### Variáveis quantitativas: medidas de posição, dispersão

A média do valor dos pedidos foi de R$55.8, com um desconto médio de R$6.25/pedido. O lucro médio por pedido foi de R$7.39 (14.7% do valor pago [7.39/50.32])

32% dos pedidos foram feitos com promoção.

In [172]:
# Estatistica basica variaveis quantitativas
aux = []
for nome, tipo in df_orders_total.dtypes:
  if tipo in ('double', 'int'):
    aux.append(nome)
    
display(df_orders_total[aux].describe())

summary order_total credit paid_amount customer_seg_recency_bucket customer_seg_frequency_bucket customer_seg_merchant_offer_bucket customer_seg_gross_income_bucket distance_merchant_customer promo_is_promotion normal_items_quantity promo_items_quantity order_lag_at_login order_lead_at_login months_after_first_purchase general_net_profit order_date_local_month order_date_local_dayofweek count 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 mean 55.81699667572885 6.25805912162847 50.32678909167726 1.6588030186654963 3.440977937082688 4.730628400976962 5.96455872133426 2781.805529506255 0.3225416448232 1.5838321771535626 0.4712255505569576 10.915743145215366 9.73069748729015 24.335806216955408 7.395985463685502 8.851121027029004 4.093918778879095 stddev 31.489082445695136 4.44324696730593 32.239551902977276 1.0522834901845284 1.1481918207385826 0.6013609258606312 0.38165737591704463 50211.794754761584 0.4674494370275182 2.1554135665166045 1.3568022095589585 33.392796628430744 18.139347606284343 17.937811997715375 6.81242294289999 2.045058398783173 2.1072029289648144 min 13.0 4.0 9.0 1.0 1.0 1.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 -1994.034375 6 1 max 1641.0 84.0 1637.0 5.0 5.0 6.0 6.0 1.1974527883558273E7 1.0 233.0 105.0 2614.0 247.0 95.0 178.382 12 7

In [173]:
display(percentByCol(df_orders_total, 'promo_is_promotion'))

promo_is_promotion cnt_per_group percent 0.0 333403 67.74583551768 1.0 158735 32.25416448232

In [174]:
display(df_orders_total[aux].summary())

summary order_total credit paid_amount customer_seg_recency_bucket customer_seg_frequency_bucket customer_seg_merchant_offer_bucket customer_seg_gross_income_bucket distance_merchant_customer promo_is_promotion normal_items_quantity promo_items_quantity order_lag_at_login order_lead_at_login months_after_first_purchase general_net_profit order_date_local_month order_date_local_dayofweek count 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 492138 mean 55.81699667572885 6.25805912162847 50.32678909167726 1.6588030186654963 3.440977937082688 4.730628400976962 5.96455872133426 2781.805529506255 0.3225416448232 1.5838321771535626 0.4712255505569576 10.915743145215366 9.73069748729015 24.335806216955408 7.395985463685502 8.851121027029004 4.093918778879095 stddev 31.489082445695136 4.44324696730593 32.239551902977276 1.0522834901845284 1.1481918207385826 0.6013609258606312 0.38165737591704463 50211.794754761584 0.4674494370275182 2.1554135665166045 1.3568022095589585 33.392796628430744 18.139347606284343 17.937811997715375 6.81242294289999 2.045058398783173 2.1072029289648144 min 13.0 4.0 9.0 1.0 1.0 1.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 -1994.034375 6 1 25% 35.9 4.0 30.0 1.0 3.0 5.0 6.0 985.6013771070673 0.0 1.0 0.0 1.0 1.0 9.0 6.08315 7 2 50% 47.7 4.0 42.51 1.0 4.0 5.0 6.0 1893.466744055135 0.0 1.0 0.0 4.0 4.0 21.0 7.9758125 9 4 75% 66.0 4.0 61.6 2.0 4.0 5.0 6.0 3146.908372031764 1.0 2.0 1.0 10.0 10.0 36.0 10.16984375 11 6 max 1641.0 84.0 1637.0 5.0 5.0 6.0 6.0 1.1974527883558273E7 1.0 233.0 105.0 2614.0 247.0 95.0 178.382 12 7

#### Correlação Variáveis

In [176]:
# recupera colunas numericas
filter_colunas_order = [x[0] for x in df_orders_total.dtypes if x[1] in ('double', 'int', 'long')]
filter_colunas_order =['order_total',
                       'credit',
                       'paid_amount',
                       'distance_merchant_customer',
                       'promo_is_promotion',
                       'normal_items_quantity',
                       'promo_items_quantity',
                       'order_lag_at_login',
                       'order_lead_at_login',
                       'months_after_first_purchase',
                       'general_net_profit']

In [177]:
import matplotlib.pyplot as plt
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation

# Reference: https://stackoverflow.com/questions/55546467/how-to-plot-correlation-heatmap-when-using-pysparkdatabricks
vector_col = "corr_features"
assembler = VectorAssembler(inputCols=filter_colunas_order,
                            outputCol=vector_col)
myGraph_vector = assembler.transform(df_orders_total).select(vector_col)
matrix = Correlation.corr(myGraph_vector, vector_col)

# Gera uma lista de listas representando uma matriz de correlacao
matrix = Correlation.corr(myGraph_vector, vector_col).collect()[0][0]
corrmatrix_orders = matrix.toArray().tolist()
df_corr_orders = spark.createDataFrame(corrmatrix_orders,filter_colunas_order)

`order_total` é altamente correlacionada com o `paid_amount`, como esperado. Podemos ver também uma correlação negativa entre `general_net_profit` e `order_total`.

Interessante observar também a correlação entre `promo_is_promotion` com `normal_items_quantity`.

In [179]:
plot_corr_matrix(corrmatrix_orders,filter_colunas_order,fig_no=234, figsize=[15,10])

### 5. Visits

#### Tratamento de Missings

In [182]:
colunas_visits_missing = percent_missing(df_sessions_visits).orderBy('perc_missing', ascending=False)
display(colunas_visits_missing)

variaveis total_missing perc_missing media_network 453445 97.80531469738148 user_account_uuid 24917 5.374444588240369 user_identifier 24916 5.374228894353134 sum_view_restaurant_screen 15264 3.2923514947586385 sum_click_add_item 7069 1.5247400888658815 sum_view_dish_screen 5730 1.235925973857901 first_order_origin_feature 2214 0.477546266338812 session_ended_at_utc0 2077 0.44799620378758465 session_duration_seconds 2077 0.44799620378758465 session_ended_at_amsp 2077 0.44799620378758465 sum_view_checkout 1925 0.41521073292782884 order_session_quantity 1773 0.382425262068073 sum_callback_purchase 1352 0.29161813554203875 sum_event_open 128 0.027608817566110177 device_model 0 0.0 device_manufacturer 0 0.0 session_started_at_amsp 0 0.0 session_started_at_utc0 0 0.0 platform 0 0.0 dau 0 0.0 session_id 0 0.0

In [183]:
# Para as colunas com missing, separar em categoricas e numericas
df_columns_visits_missing = colunas_visits_missing.filter(colunas_visits_missing['perc_missing'] > 0
                                                  ).select('variaveis')
list_df_columns_visits_missing = list([row[0] for row in df_columns_visits_missing.collect()])

filter_colunas_visits_numericas = [x[0] for x in df_sessions_visits[list_df_columns_visits_missing].dtypes if x[1] in ('double', 'long')]
filter_colunas_visits_numericas_int = [x[0] for x in df_sessions_visits[list_df_columns_visits_missing].dtypes if x[1] in ('int')]
filter_colunas_visits_categoricas = [x[0] for x in df_sessions_visits[list_df_columns_visits_missing].dtypes if x[1] not in ('double', 'int', 'long', 'boolean')]
filter_colunas_visits_booleanas = [x[0] for x in df_sessions_visits[list_df_columns_visits_missing].dtypes if x[1] in ('boolean')]

# Inputar unknown para colunas categoricas
for coluna in filter_colunas_visits_categoricas:
  df_sessions_visits = df_sessions_visits.fillna('unknown', subset=[coluna])

# Transformar colunas booleanas para string, depois inputar unknown
for coluna in filter_colunas_visits_booleanas:
  df_sessions_visits = df_sessions_visits.withColumn(coluna,col(coluna).cast('string'))
  df_sessions_visits = df_sessions_visits.fillna('unknown', subset=[coluna])

# Inputar media para colunas numericas
for coluna in filter_colunas_visits_numericas:
  media = df_sessions_visits.agg(mean(coluna)).collect()[0][0]
  df_sessions_visits = df_sessions_visits.fillna(media, subset=[coluna])
  
# Inputar media para colunas numericas inteiras arredondando para o integer mais perto
for coluna in filter_colunas_visits_numericas:
  media = df_orders_total.agg(mean(coluna)).collect()[0][0]
  df_sessions_visits = df_sessions_visits.fillna(media, subset=[coluna])
  df_sessions_visits = df_sessions_visits.withColumn(coluna, f.round(df_sessions_visits[coluna], 0))

--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 62 try : 
 ---> 63 return f ( * a , ** kw ) 
 64 except py4j . protocol . Py4JJavaError as e : 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 --> 328 format(target_id, ".", name), value)
 329 else : 

 Py4JJavaError : An error occurred while calling o2266.agg.
: org.apache.spark.sql.AnalysisException: cannot resolve '`sum_view_restaurant_screen`' given input columns: [paid_amount, promo_is_promotion, customer_id, order_timestamp_local, customer_seg_gross_income_bucket, customer_seg_merchant_offer_bucket, scheduled_creation_date_local, cohort_month, customer_seg_benefits_sensitivity_bucket, merchant_city, frn_id, device_platform, session_id, promo_items_quantity, device_type, customer_has_plus, order_number, merchant_dish_type, general_net_profit, order_date_local, merchant_centroid_id, order_lag_at_login, customer_state_label, scheduled, months_after_first_purchase, distance_merchant_customer, normal_items_quantity, last_status_date_local, delivery_type, first_order_date, customer_district, customer_seg_recency_bucket, valid_order, customer_seg_status_last_month, payment_method, order_total, customer_centroid_id, order_lead_at_login, merchant_district, customer_seg_frequency_bucket, customer_seg_marlin_tag, order_shift, customer_seg_preferred_shift, customer_city, credit, order_id, device_app_version];;
'Aggregate [avg('sum_view_restaurant_screen) AS avg(sum_view_restaurant_screen)#22081]
+- Project [order_id#112, order_number#113L, order_timestamp_local#114, order_shift#115, last_status_date_local#116, order_total#117, credit#118, paid_amount#119, delivery_type#120, scheduled#121, scheduled_creation_date_local#122, device_app_version#8998, device_type#9093, device_platform#125, payment_method#126, customer_state_label#127, customer_city#128, customer_district#129, customer_centroid_id#130, customer_has_plus#9236, customer_seg_status_last_month#8903, customer_seg_recency_bucket#16207, customer_seg_frequency_bucket#16880, customer_seg_merchant_offer_bucket#17553, ... 23 more fields]
 +- Project [order_id#112, order_number#113L, order_timestamp_local#114, order_shift#115, last_status_date_local#116, order_total#117, credit#118, paid_amount#119, delivery_type#120, scheduled#121, scheduled_creation_date_local#122, device_app_version#8998, device_type#9093, device_platform#125, payment_method#126, customer_state_label#127, customer_city#128, customer_district#129, customer_centroid_id#130, customer_has_plus#9236, customer_seg_status_last_month#8903, customer_seg_recency_bucket#16207, customer_seg_frequency_bucket#16880, customer_seg_merchant_offer_bucket#17553, ... 23 more fields]
 +- Project [order_id#112, order_number#113L, order_timestamp_local#114, order_shift#115, last_status_date_local#116, order_total#117, credit#118, paid_amount#119, delivery_type#120, scheduled#121, scheduled_creation_date_local#122, device_app_version#8998, device_type#9093, device_platform#125, payment_method#126, customer_state_label#127, customer_city#128, customer_district#129, customer_centroid_id#130, customer_has_plus#9236, customer_seg_status_last_month#8903, customer_seg_recency_bucket#16207, customer_seg_frequency_bucket#16880, customer_seg_merchant_offer_bucket#17553, ... 23 more fields]
 +- Project [order_id#112, order_number#113L, order_timestamp_local#114, order_shift#115, last_status_date_local#116, order_total#117, credit#118, paid_amount#119, delivery_type#120, scheduled#121, scheduled_creation_date_local#122, device_app_version#8998, device_type#9093, device_platform#125, payment_method#126, customer_state_label#127, customer_city#128, customer_district#129, customer_centroid_id#130, customer_has_plus#9236, c

In [184]:
len(list_df_columns_visits_missing)

Out[27]: 14

In [185]:
len(filter_colunas_visits_categoricas)

Out[28]: 6

In [186]:
len(filter_colunas_visits_numericas)

Out[29]: 8

In [187]:
display(df_sessions_visits)

session_id dau platform user_identifier user_account_uuid session_started_at_amsp session_ended_at_amsp session_started_at_utc0 session_ended_at_utc0 session_duration_seconds device_model device_manufacturer sum_event_open sum_view_restaurant_screen sum_view_dish_screen sum_click_add_item sum_view_checkout sum_callback_purchase order_session_quantity first_order_origin_feature media_network 41162808-5335-4e4f-aa52-45754ec1d558 2019-11-04_661ead80-50a2-48b4-ae78-f872e2f08c11 IOS ffa840ebe8b397e995245525ec98f0b31a882c4d3e47dc0e91d3115cd20d6d80 ca438b60-3d04-44c0-9883-c4f01fc512ad 2019-11-04T09:14:47.566Z 2019-11-04T09:15:50.323Z 2019-11-04T11:14:47.566Z 2019-11-04T11:15:50.323Z 63.0 iPhone9,3 Apple 1.0 8.933784760324386 1.0 1.0 1.0 1.0 1.0 Loop unknown 52f0a543-fcc7-4ff0-bed1-41bec8a51374 2019-12-07_17ae6c54-37e1-42e3-b82b-e562aaeb7730 IOS a59ea42fbbaf0fa9a48b65f45842d9d061d23775ad2af61c28d1235b5510ae68 414f1e51-e872-42ca-ad5e-c30b085bd5e4 2019-12-07T13:28:37.764Z 2019-12-07T15:04:00.819Z 2019-12-07T15:28:37.764Z 2019-12-07T17:04:00.819Z 5723.0 iPhone9,3 Apple 17.0 12.0 3.0 1.0 2.0 1.0 1.0 Last Restaurants unknown f06f2a6d-14cc-44e3-8ec6-66191659430b 2019-12-29_d8a7f51d-4394-3c9a-ae62-8522f5885d3f ANDROID e7dcbc11f83b22ea57ec8b385b9fa38d48532b180e3d19cbde6d4766687a48b9 5c697207-d8a4-460e-b171-3e94e42be5ab 2019-12-29T19:58:38.297Z 2019-12-29T20:17:45.199Z 2019-12-29T22:58:38.297Z 2019-12-29T23:17:45.199Z 1147.0 Redmi Note 8 Xiaomi 2.0 4.0 7.0 7.0 5.0 1.0 1.0 Ranking unknown 716d0044-0d76-4199-86ca-62930a751d59 2019-12-03_9675dcd9-9dd5-3ec3-809e-9006b4fac160 ANDROID 2959b13e1caef84fa6cde74693ba2476f17eaa72b66dad051b74924762da14c7 615b2fb5-e76d-4fa7-b982-9564650c76c5 2019-12-03T14:54:14.621Z 2019-12-03T16:31:47.527Z 2019-12-03T16:54:14.621Z 2019-12-03T18:31:47.527Z 5853.0 SM-A520F samsung 11.0 1.0 1.0 1.0 3.0 1.0 1.0 Taxa na faixa unknown 96081494-8554-4c3f-92b6-94e2070d1660 2019-12-20_e953c804-ecd2-3f00-8465-0ba2d8ce5aa1 ANDROID 9c944018e8b8cd2ac2fec6edf1f46c3c452c4e70c46e39a89cc37430edf01ad7 ba8596c4-9fbf-4f67-9e2a-dbb65f4b7c40 2019-12-20T20:28:22.584Z 2019-12-20T20:54:25.376Z 2019-12-20T23:28:22.584Z 2019-12-20T23:54:25.376Z 1563.0 SM-J710MN samsung 4.0 4.0 9.0 2.0 2.0 1.0 1.0 CRM Restaurant unknown 85091579-c5e8-474c-9b77-7129564141d9 2019-08-09_37124edd-a771-41bc-95bd-e0d607863f6d ANDROID c447b075-5080-4ea9-99eb-1119973e9e08 c447b075-5080-4ea9-99eb-1119973e9e08 2019-08-09T20:25:25.025Z 2019-08-09T21:22:41.041Z 2019-08-09T23:25:25.025Z 2019-08-10T00:22:41.041Z 3436.0 Moto G Play motorola 5.0 2.0 24.0 4.0 5.0 1.0 1.0 Lanches unknown 2284b979-27c9-4ad2-8d12-557ad537200e 2019-12-14_aa7ca448-de7d-4f24-9003-030ad0142522 IOS 0b51610a7974ad8751637867fa168e3b112df6feda0e01ca493977128741eaea 76cb1602-6a45-431a-a2af-2a63bad6f038 2019-12-14T21:46:56.353Z 2019-12-14T21:54:19.136Z 2019-12-15T00:46:56.353Z 2019-12-15T00:54:19.136Z 443.0 iPhone7,2 Apple 2.0 5.0 2.0 1.0 1.0 1.0 1.0 Ranking unknown e969590a-382e-41fc-b7c5-9980984d40f4 2019-12-06_3e0c8796-3451-4f93-954a-7562098407ea IOS cc37994f00b79a48ae57678a6d192c454c74b52f6839e7e6bb693ab1e8b67a03 b00996d7-3fa3-4c21-aaaf-3a52cc231e37 2019-12-06T13:07:41.512Z 2019-12-06T13:11:25.127Z 2019-12-06T15:07:41.512Z 2019-12-06T15:11:25.127Z 224.0 iPhone10,6 Apple 3.0 4.0 2.0 1.0 1.0 1.0 1.0 Last Restaurants unknown 83a6e98e-ecbc-440e-81b2-b03ab719e190 2019-06-02_6de65a8d-eead-477f-9542-7de7d82a149b IOS 228ebd5d-1099-4c27-8304-382541861e81 228ebd5d-1099-4c27-8304-382541861e81 2019-06-02T22:48:40.566Z 2019-06-02T23:26:59.356Z 2019-06-03T01:48:40.566Z 2019-06-03T02:26:59.356Z 2299.0 iPhone11,8 Apple 9.0 9.0 4.0 4.0 3.0 1.0 1.0 Featured Restaurant unknown 0de892ef-e99e-406f-9959-8b12da2b3bbc 2019-10-01_11c0c641-8c7f-38ee-9c96-26499acdef34 ANDROID 2c64e0bbf845290318ac4816a9a4c547edb326a4e777e0c262d4c3c76c4d3d03 5bf6ae78-249e-4836-9727-3dba86dbc067 2019-10-01T23:19:27.027Z 2019-10-01T23:53:43.043Z 2019-10-02T02:19:27.027Z 2019-10-02T02:53:43.043Z 2056.0 Moto G (5S) motorola 9.0 13.0 20.0 6.0 12.0 1.0 1.0 La

#### Tratamento de Datas

In [189]:
# importante: transformar primeiro para timestamp, depois para date!!!
df_sessions_visits = df_sessions_visits.withColumn('session_started_at_amsp', from_utc_timestamp('session_started_at_amsp', 'UTC'))\
                                       .withColumn('session_ended_at_amsp', from_utc_timestamp('session_ended_at_amsp', 'UTC'))\
                                       .withColumn('session_started_at_utc0', from_utc_timestamp('session_started_at_utc0', 'UTC'))\
                                       .withColumn('session_ended_at_utc0', from_utc_timestamp('session_ended_at_utc0', 'UTC'))\
                                       .withColumn('session_started_at_utc0', from_utc_timestamp('session_started_at_utc0', 'UTC'))\
                                       .withColumn('session_started_date', to_date('session_started_at_amsp', 'YYYY-MM-DD'))\
                                       .withColumn('session_started_month', month('session_started_date'))\
                                       .withColumn('session_started_dayofweek', dayofweek('session_started_date'))
display(df_sessions_visits)

session_id dau platform user_identifier user_account_uuid session_started_at_amsp session_ended_at_amsp session_started_at_utc0 session_ended_at_utc0 session_duration_seconds device_model device_manufacturer sum_event_open sum_view_restaurant_screen sum_view_dish_screen sum_click_add_item sum_view_checkout sum_callback_purchase order_session_quantity first_order_origin_feature media_network session_started_date session_started_month session_started_dayofweek 41162808-5335-4e4f-aa52-45754ec1d558 2019-11-04_661ead80-50a2-48b4-ae78-f872e2f08c11 IOS ffa840ebe8b397e995245525ec98f0b31a882c4d3e47dc0e91d3115cd20d6d80 ca438b60-3d04-44c0-9883-c4f01fc512ad 2019-11-04T09:14:47.566+0000 2019-11-04T09:15:50.323+0000 2019-11-04T11:14:47.566+0000 2019-11-04T11:15:50.323+0000 63.0 iPhone9,3 Apple 1.0 8.933784760324386 1.0 1.0 1.0 1.0 1.0 Loop unknown 2019-11-04 11 2 52f0a543-fcc7-4ff0-bed1-41bec8a51374 2019-12-07_17ae6c54-37e1-42e3-b82b-e562aaeb7730 IOS a59ea42fbbaf0fa9a48b65f45842d9d061d23775ad2af61c28d1235b5510ae68 414f1e51-e872-42ca-ad5e-c30b085bd5e4 2019-12-07T13:28:37.764+0000 2019-12-07T15:04:00.819+0000 2019-12-07T15:28:37.764+0000 2019-12-07T17:04:00.819+0000 5723.0 iPhone9,3 Apple 17.0 12.0 3.0 1.0 2.0 1.0 1.0 Last Restaurants unknown 2019-12-07 12 7 f06f2a6d-14cc-44e3-8ec6-66191659430b 2019-12-29_d8a7f51d-4394-3c9a-ae62-8522f5885d3f ANDROID e7dcbc11f83b22ea57ec8b385b9fa38d48532b180e3d19cbde6d4766687a48b9 5c697207-d8a4-460e-b171-3e94e42be5ab 2019-12-29T19:58:38.297+0000 2019-12-29T20:17:45.199+0000 2019-12-29T22:58:38.297+0000 2019-12-29T23:17:45.199+0000 1147.0 Redmi Note 8 Xiaomi 2.0 4.0 7.0 7.0 5.0 1.0 1.0 Ranking unknown 2019-12-29 12 1 716d0044-0d76-4199-86ca-62930a751d59 2019-12-03_9675dcd9-9dd5-3ec3-809e-9006b4fac160 ANDROID 2959b13e1caef84fa6cde74693ba2476f17eaa72b66dad051b74924762da14c7 615b2fb5-e76d-4fa7-b982-9564650c76c5 2019-12-03T14:54:14.621+0000 2019-12-03T16:31:47.527+0000 2019-12-03T16:54:14.621+0000 2019-12-03T18:31:47.527+0000 5853.0 SM-A520F samsung 11.0 1.0 1.0 1.0 3.0 1.0 1.0 Taxa na faixa unknown 2019-12-03 12 3 96081494-8554-4c3f-92b6-94e2070d1660 2019-12-20_e953c804-ecd2-3f00-8465-0ba2d8ce5aa1 ANDROID 9c944018e8b8cd2ac2fec6edf1f46c3c452c4e70c46e39a89cc37430edf01ad7 ba8596c4-9fbf-4f67-9e2a-dbb65f4b7c40 2019-12-20T20:28:22.584+0000 2019-12-20T20:54:25.376+0000 2019-12-20T23:28:22.584+0000 2019-12-20T23:54:25.376+0000 1563.0 SM-J710MN samsung 4.0 4.0 9.0 2.0 2.0 1.0 1.0 CRM Restaurant unknown 2019-12-20 12 6 85091579-c5e8-474c-9b77-7129564141d9 2019-08-09_37124edd-a771-41bc-95bd-e0d607863f6d ANDROID c447b075-5080-4ea9-99eb-1119973e9e08 c447b075-5080-4ea9-99eb-1119973e9e08 2019-08-09T20:25:25.025+0000 2019-08-09T21:22:41.041+0000 2019-08-09T23:25:25.025+0000 2019-08-10T00:22:41.041+0000 3436.0 Moto G Play motorola 5.0 2.0 24.0 4.0 5.0 1.0 1.0 Lanches unknown 2019-08-09 8 6 2284b979-27c9-4ad2-8d12-557ad537200e 2019-12-14_aa7ca448-de7d-4f24-9003-030ad0142522 IOS 0b51610a7974ad8751637867fa168e3b112df6feda0e01ca493977128741eaea 76cb1602-6a45-431a-a2af-2a63bad6f038 2019-12-14T21:46:56.353+0000 2019-12-14T21:54:19.136+0000 2019-12-15T00:46:56.353+0000 2019-12-15T00:54:19.136+0000 443.0 iPhone7,2 Apple 2.0 5.0 2.0 1.0 1.0 1.0 1.0 Ranking unknown 2019-12-14 12 7 e969590a-382e-41fc-b7c5-9980984d40f4 2019-12-06_3e0c8796-3451-4f93-954a-7562098407ea IOS cc37994f00b79a48ae57678a6d192c454c74b52f6839e7e6bb693ab1e8b67a03 b00996d7-3fa3-4c21-aaaf-3a52cc231e37 2019-12-06T13:07:41.512+0000 2019-12-06T13:11:25.127+0000 2019-12-06T15:07:41.512+0000 2019-12-06T15:11:25.127+0000 224.0 iPhone10,6 Apple 3.0 4.0 2.0 1.0 1.0 1.0 1.0 Last Restaurants unknown 2019-12-06 12 6 83a6e98e-ecbc-440e-81b2-b03ab719e190 2019-06-02_6de65a8d-eead-477f-9542-7de7d82a149b IOS 228ebd5d-1099-4c27-8304-382541861e81 228ebd5d-1099-4c27-8304-382541861e81 2019-06-02T22:48:40.566+0000 2019-06-02T23:26:59.356+0000 2019-06-03T01:48:40.566+0000 2019-06-03T02:26:59.356+0000 2299.0 iPhone11,8 Apple 9.0 9.0 4.0 4.0 3.0 1.0 1.0 Featured Restaurant unknown 2019-06-02 6 1 0

In [190]:
df_sessions_visits.dtypes

Out[150]: [('session_id', 'string'),
 ('dau', 'string'),
 ('platform', 'string'),
 ('user_identifier', 'string'),
 ('user_account_uuid', 'string'),
 ('session_started_at_amsp', 'timestamp'),
 ('session_ended_at_amsp', 'timestamp'),
 ('session_started_at_utc0', 'timestamp'),
 ('session_ended_at_utc0', 'timestamp'),
 ('session_duration_seconds', 'double'),
 ('device_model', 'string'),
 ('device_manufacturer', 'string'),
 ('sum_event_open', 'double'),
 ('sum_view_restaurant_screen', 'double'),
 ('sum_view_dish_screen', 'double'),
 ('sum_click_add_item', 'double'),
 ('sum_view_checkout', 'double'),
 ('sum_callback_purchase', 'double'),
 ('order_session_quantity', 'double'),
 ('first_order_origin_feature', 'string'),
 ('media_network', 'string'),
 ('session_started_date', 'date'),
 ('session_started_month', 'int'),
 ('session_started_dayofweek', 'int')]

#### Exploração Sessions

A base de eventos contém +463k sessões de +68k `user_identifiers`.

In [193]:
df_sessions_visits.select(f.countDistinct('session_id')).show()

+--------------------------+
count(DISTINCT session_id)|
+--------------------------+
 463620|
+--------------------------+

In [194]:
df_sessions_visits.select(f.countDistinct('user_identifier')).show()

+-------------------------------+
count(DISTINCT user_identifier)|
+-------------------------------+
 68157|
+-------------------------------+

In [195]:
df_sessions_visits.select(f.countDistinct('dau')).show()

+-------------------+
count(DISTINCT dau)|
+-------------------+
 435661|
+-------------------+

In [196]:
df_sessions_visits.select(f.countDistinct('device_model')).show()

+----------------------------+
count(DISTINCT device_model)|
+----------------------------+
 811|
+----------------------------+

In [197]:
display(percentByCol(df_sessions_visits, 'device_manufacturer'))

device_manufacturer cnt_per_group percent Apple 200977 43.349510374875976 samsung 135191 29.159872309218756 motorola 73582 15.871187610543117 Xiaomi 22817 4.921487425046374 asus 13361 2.881886027349985 LGE 8958 1.9321858418532418 LENOVO 2037 0.43936844829817523 Sony 1426 0.30757948319744616 OnePlus 1167 0.25171476640352014 HUAWEI 949 0.20469349898623873 TCL 582 0.1255338423709072 Quantum 357 0.07700271774297916 LG Electronics 319 0.06880635002804021 Google 256 0.055217635132220354 BLU 236 0.05090375738751564 Multilaser 154 0.033216858634226305 Meizu 123 0.026530348129933996 LeMobile 86 0.018549674302230274 HMD Global 79 0.017039817091583625 BullittGroupLimited 77 0.016608429317113153 nubia 75 0.01617704154264268 blackshark 70 0.015098572106466503 LeEco 54 0.01164746991070273 Blackview 53 0.011431776023467495 Positivo 43 0.009274837151115137 ulefone 42 0.009059143263879901 Ulefone 38 0.008196367714938958 positivo 36 0.007764979940468487 ZTE 36 0.007764979940468487 lenovo 32 0.006902204391527544 HTC 31 0.006686510504292308 Razer 30 0.006470816617057073 ZUK 30 0.006470816617057073 A-gold 27 0.005823734955351365 CUBOT 23 0.004960959406410423 alps 19 0.004098183857469479 DOOGEE 19 0.004098183857469479 UMIDIGI 17 0.003666796082999008 vernee 15 0.0032354083085285364 Mirage 15 0.0032354083085285364 Lenovo 15 0.0032354083085285364 Motorola 15 0.0032354083085285364 Droi 14 0.0030197144212933008 BlackBerry 12 0.002588326646822829 TP-LINK 12 0.002588326646822829 PHONEMAX 12 0.002588326646822829 Huawei 12 0.002588326646822829 Fortune Ship 9 0.0019412449851171217 OUKITEL 9 0.0019412449851171217 OPPO 9 0.0019412449851171217 HOW 8 0.001725551097881886 realme 8 0.001725551097881886 Coolpad 8 0.001725551097881886 ECS 5 0.0010784694361761788 DL 5 0.0010784694361761788 V6 5 0.0010784694361761788 SPRD 4 8.62775548940943E-4 X23 4 8.62775548940943E-4 wheatek 2 4.313877744704715E-4 iPhone 2 4.313877744704715E-4 xiaomi 2 4.313877744704715E-4 XGODY 1 2.1569388723523576E-4 P20 Pro 1 2.1569388723523576E-4 NUU 1 2.1569388723523576E-4 Philips 1 2.1569388723523576E-4 vivo 1 2.1569388723523576E-4 Amazon 1 2.1569388723523576E-4 GOME 1 2.1569388723523576E-4 Wingtech 1 2.1569388723523576E-4 google 1 2.1569388723523576E-4

Sextas e finais de semana são os dias com mais sessões geradas, 16% e 34% respectivamente.

In [199]:
display(percentByCol(df_sessions_visits, 'session_started_dayofweek').orderBy('session_started_dayofweek'))

session_started_dayofweek cnt_per_group percent 1 81116 17.496225356973383 2 53279 11.491954618006126 3 54848 11.830378327078211 4 59557 12.846080842068936 5 61956 13.363530477546266 6 74527 16.075018333980417 7 78337 16.896812044346664

In [200]:
df_sessions_month = df_sessions_visits.groupby('session_started_dayofweek','session_started_month')\
                                    .count()\
                                    .orderBy('session_started_month','session_started_dayofweek')
display(df_sessions_month)

session_started_dayofweek session_started_month count 4 5 1 6 5 9 1 6 16400 2 6 8575 3 6 8872 4 6 10604 5 6 10643 6 6 12233 7 6 15370 1 7 9527 2 7 8896 3 7 9766 4 7 10162 5 7 8331 6 7 9468 7 7 9359 1 8 9972 2 8 6190 3 8 6575 4 8 7192 5 8 9409 6 8 11603 7 8 12451 1 9 12882 2 9 7926 3 9 6747 4 9 7276 5 9 7770 6 9 9648 7 9 9966 1 10 10128 2 10 6423 3 10 8509 4 10 9113 5 10 9582 6 10 9754 7 10 9720 1 11 10252 2 11 6646 3 11 7222 4 11 7933 5 11 8333 6 11 12501 7 11 12385 1 12 11955 2 12 8623 3 12 7157 4 12 7276 5 12 7888 6 12 9311 7 12 9086

97.8% das sessões não são identificadas. Se forem visitas `orgânicas`, vale entender se é possível fazer uma atribuição do horário do disparo do evento de `push` (`event_time_utc3`) e uma janela de X minutos após em que a sessão é gerada.

In [202]:
display(percentByCol(df_sessions_visits, 'media_network'))

media_network cnt_per_group percent unknown 453445 97.80531469738148 googleadwords_int 4127 0.8901686726198179 Email Avaliacao 3111 0.6710236831888184 Facebook Ads 1075 0.23187092877787843 twitter 795 0.17147664035201243 MGM 473 0.10202320866226651 criteo_int 103 0.02221647038522928 jampp_int 103 0.02221647038522928 doubleclick_int 99 0.02135369483628834 SMS_Prospect 68 0.014667184331996031 muvmobile_int 57 0.012294551572408437 Stories 28 0.0060394288425866015 Email 25 0.005392347180880894 manage_int 20 0.004313877744704715 cuponeria 14 0.0030197144212933008 Twitter 10 0.0021569388723523576 rtbhouse_int 9 0.0019412449851171217 lemmonetmobile_int 7 0.0015098572106466504 WhatsApp 7 0.0015098572106466504 progmedia 6 0.0012941633234114145 Banner-Site 6 0.0012941633234114145 appia_int 5 0.0010784694361761788 Teste_Nova_Regra 4 8.62775548940943E-4 cocaeifood 4 8.62775548940943E-4 SMS 4 8.62775548940943E-4 lista_brasilia 2 4.313877744704715E-4 Mercado-Facebook 2 4.313877744704715E-4 Progmedia 1 2.1569388723523576E-4 infleux_int 1 2.1569388723523576E-4 Influencers-Julho 1 2.1569388723523576E-4 Loop-Whatsapp 1 2.1569388723523576E-4 startapp_int 1 2.1569388723523576E-4 Retirar-Facebook 1 2.1569388723523576E-4 Parceiros 1 2.1569388723523576E-4 crm_wpp 1 2.1569388723523576E-4 Google 1 2.1569388723523576E-4 Vic-CRM-2803 1 2.1569388723523576E-4 Push 1 2.1569388723523576E-4

In [203]:
df_sessions_visits.dtypes

Out[192]: [('session_id', 'string'),
 ('dau', 'string'),
 ('platform', 'string'),
 ('user_identifier', 'string'),
 ('user_account_uuid', 'string'),
 ('session_started_at_amsp', 'timestamp'),
 ('session_ended_at_amsp', 'timestamp'),
 ('session_started_at_utc0', 'timestamp'),
 ('session_ended_at_utc0', 'timestamp'),
 ('session_duration_seconds', 'double'),
 ('device_model', 'string'),
 ('device_manufacturer', 'string'),
 ('sum_event_open', 'double'),
 ('sum_view_restaurant_screen', 'double'),
 ('sum_view_dish_screen', 'double'),
 ('sum_click_add_item', 'double'),
 ('sum_view_checkout', 'double'),
 ('sum_callback_purchase', 'double'),
 ('order_session_quantity', 'double'),
 ('first_order_origin_feature', 'string'),
 ('media_network', 'string'),
 ('session_started_date', 'date'),
 ('session_started_month', 'int'),
 ('session_started_dayofweek', 'int')]

#### Tipos de visualizações por sessão

A quantidade de views das telas de restaurantes por sessões é maior para users com aparelho da `Apple`: Q1 é 5, Mediana em 8.9 e Q3 em 16.

In [206]:
display(df_sessions_visits.select('device_manufacturer','sum_view_restaurant_screen'))

device_manufacturer sum_view_restaurant_screen Apple 8.933784760324386 Apple 12.0 Xiaomi 4.0 samsung 1.0 samsung 4.0 motorola 2.0 Apple 5.0 Apple 4.0 Apple 9.0 motorola 13.0 samsung 5.0 Apple 18.0 asus 8.0 motorola 9.0 Sony 3.0 Apple 3.0 samsung 2.0 Apple 11.0 asus 1.0 Apple 3.0 samsung 1.0 samsung 5.0 Apple 16.0 Xiaomi 4.0 Apple 4.0 Apple 4.0 motorola 3.0 samsung 2.0 samsung 5.0 samsung 2.0 samsung 7.0 Apple 24.0 LGE 8.0 samsung 7.0 samsung 6.0 Apple 66.0 Apple 11.0 Apple 9.0 samsung 10.0 Apple 47.0 Apple 57.0 Apple 5.0 Apple 0.0 samsung 8.933784760324386 Apple 5.0 samsung 4.0 Apple 13.0 Apple 3.0 Apple 6.0 Apple 8.0 Apple 11.0 samsung 2.0 Apple 33.0 motorola 1.0 Apple 6.0 samsung 1.0 motorola 8.0 motorola 1.0 Xiaomi 3.0 Apple 13.0 Apple 26.0 Apple 19.0 Apple 5.0 Apple 3.0 motorola 35.0 samsung 9.0 motorola 1.0 Apple 5.0 samsung 6.0 LGE 2.0 samsung 5.0 motorola 4.0 Apple 44.0 motorola 8.933784760324386 motorola 3.0 Apple 6.0 motorola 11.0 Apple 4.0 Apple 8.0 Apple 5.0 motorola 18.0 motorola 1.0 Xiaomi 1.0 samsung 5.0 Apple 4.0 Apple 8.0 asus 3.0 samsung 2.0 motorola 6.0 motorola 1.0 Apple 9.0 Apple 4.0 samsung 1.0 Apple 36.0 Xiaomi 4.0 samsung 17.0 motorola 1.0 motorola 5.0 Apple 2.0 Apple 7.0 samsung 3.0 motorola 25.0 motorola 3.0 samsung 1.0 samsung 1.0 Apple 5.0 samsung 53.0 Apple 6.0 Apple 7.0 samsung 6.0 Apple 8.0 samsung 2.0 Apple 14.0 Apple 5.0 samsung 1.0 motorola 3.0 Apple 1.0 samsung 53.0 motorola 1.0 Apple 8.0 Apple 1.0 Apple 15.0 samsung 4.0 Apple 3.0 Apple 11.0 samsung 8.933784760324386 asus 1.0 motorola 1.0 samsung 4.0 Apple 16.0 samsung 6.0 samsung 13.0 samsung 2.0 Apple 9.0 motorola 12.0 Apple 7.0 samsung 7.0 Apple 20.0 samsung 91.0 LGE 1.0 Xiaomi 83.0 Apple 8.0 Apple 17.0 OnePlus 1.0 asus 27.0 Apple 6.0 Apple 8.0 samsung 1.0 Apple 2.0 Apple 3.0 motorola 19.0 samsung 2.0 Xiaomi 8.933784760324386 samsung 2.0 Apple 3.0 asus 1.0 Apple 32.0 samsung 19.0 samsung 1.0 samsung 1.0 Apple 16.0 Apple 7.0 samsung 2.0 Xiaomi 50.0 Apple 78.0 Apple 66.0 asus 21.0 motorola 1.0 samsung 1.0 Apple 4.0 samsung 1.0 motorola 4.0 LGE 4.0 Apple 139.0 Apple 23.0 samsung 2.0 Apple 5.0 motorola 3.0 Xiaomi 4.0 samsung 1.0 samsung 1.0 samsung 11.0 Apple 20.0 samsung 1.0 samsung 2.0 Apple 6.0 samsung 1.0 samsung 4.0 Apple 10.0 motorola 3.0 samsung 1.0 samsung 1.0 samsung 8.933784760324386 samsung 2.0 Apple 3.0 Apple 18.0 Apple 82.0 motorola 12.0 Apple 24.0 Apple 3.0 samsung 3.0 motorola 1.0 samsung 6.0 Apple 7.0 motorola 22.0 samsung 2.0 Apple 3.0 Apple 3.0 samsung 8.0 samsung 1.0 motorola 1.0 samsung 3.0 motorola 4.0 motorola 2.0 asus 1.0 Apple 3.0 motorola 9.0 samsung 2.0 Apple 10.0 motorola 1.0 Apple 11.0 Apple 7.0 motorola 4.0 Apple 6.0 Apple 3.0 Apple 13.0 Xiaomi 6.0 asus 4.0 motorola 2.0 samsung 3.0 Xiaomi 3.0 samsung 4.0 Apple 21.0 samsung 1.0 Apple 12.0 Apple 7.0 Apple 5.0 Apple 19.0 samsung 2.0 samsung 1.0 Apple 5.0 Apple 32.0 Apple 18.0 samsung 2.0 samsung 2.0 motorola 11.0 Apple 30.0 Meizu 3.0 Apple 16.0 samsung 1.0 motorola 15.0 Apple 27.0 motorola 5.0 Apple 3.0 Xiaomi 5.0 Apple 1.0 LGE 8.933784760324386 Apple 5.0 LGE 11.0 Xiaomi 11.0 Apple 1.0 samsung 5.0 Xiaomi 2.0 samsung 12.0 samsung 6.0 Xiaomi 22.0 Xiaomi 1.0 samsung 6.0 samsung 29.0 asus 1.0 Apple 14.0 Apple 29.0 samsung 6.0 Apple 6.0 samsung 5.0 samsung 4.0 Apple 4.0 Apple 14.0 motorola 1.0 samsung 1.0 LENOVO 4.0 samsung 1.0 samsung 3.0 motorola 1.0 motorola 8.0 Apple 5.0 Apple 8.933784760324386 samsung 11.0 Apple 5.0 asus 8.0 Apple 8.933784760324386 samsung 3.0 Apple 20.0 Apple 12.0 Apple 6.0 samsung 5.0 Apple 20.0 motorola 1.0 samsung 2.0 samsung 2.0 samsung 2.0 Xiaomi 1.0 samsung 9.0 samsung 1.0 samsung 1.0 Apple 5.0 Apple 4.0 asus 10.0 Apple 4.0 Apple 21.0 samsung 11.0 samsung 1.0 motorola 1.0 samsung 4.0 motorola 13.0 motorola 8.933784760324386 motorola 3.0 Apple 2.0 motorola 3.0 samsung 12.0 Apple 32.0 asus 1.0 samsung 1.0 motorola 14.0 Apple 1.0 Apple 12.0 Apple 3.0 asus 8.933784760324386 LGE 3.0 samsung 1.0 samsung 1.0 samsung 1.0 samsung 2.0 Apple 4.0 Apple 6.0 

In [207]:
display(df_sessions_visits.select('device_manufacturer','sum_view_dish_screen'))

device_manufacturer sum_view_dish_screen Apple 1.0 Apple 3.0 Xiaomi 7.0 samsung 1.0 samsung 9.0 motorola 24.0 Apple 2.0 Apple 2.0 Apple 4.0 motorola 20.0 samsung 1.0 Apple 4.0 asus 5.0 motorola 11.0 Sony 2.0 Apple 1.0 samsung 5.0 Apple 3.0 asus 3.0 Apple 1.0 samsung 1.0 samsung 9.0 Apple 11.0 Xiaomi 2.0 Apple 1.0 Apple 2.0 motorola 3.0 samsung 4.0 samsung 3.0 samsung 2.0 samsung 4.0 Apple 2.0 LGE 6.0 samsung 1.0 samsung 4.0 Apple 12.0 Apple 3.0 Apple 4.0 samsung 4.0 Apple 18.0 Apple 26.0 Apple 1.0 Apple 0.0 samsung 5.7181703029111794 Apple 2.0 samsung 3.0 Apple 4.0 Apple 5.0 Apple 4.0 Apple 4.0 Apple 4.0 samsung 4.0 Apple 13.0 motorola 5.0 Apple 1.0 samsung 3.0 motorola 10.0 motorola 1.0 Xiaomi 4.0 Apple 5.0 Apple 15.0 Apple 10.0 Apple 2.0 Apple 1.0 motorola 17.0 samsung 6.0 motorola 2.0 Apple 2.0 samsung 16.0 LGE 5.0 samsung 2.0 motorola 2.0 Apple 23.0 motorola 5.7181703029111794 motorola 1.0 Apple 3.0 motorola 14.0 Apple 3.0 Apple 6.0 Apple 3.0 motorola 11.0 motorola 2.0 Xiaomi 11.0 samsung 3.0 Apple 2.0 Apple 6.0 asus 8.0 samsung 8.0 motorola 10.0 motorola 4.0 Apple 3.0 Apple 2.0 samsung 1.0 Apple 16.0 Xiaomi 7.0 samsung 6.0 motorola 3.0 motorola 4.0 Apple 1.0 Apple 4.0 samsung 7.0 motorola 31.0 motorola 7.0 samsung 2.0 samsung 3.0 Apple 2.0 samsung 14.0 Apple 3.0 Apple 4.0 samsung 1.0 Apple 3.0 samsung 1.0 Apple 5.0 Apple 5.0 samsung 3.0 motorola 18.0 Apple 3.0 samsung 71.0 motorola 6.0 Apple 3.0 Apple 6.0 Apple 5.0 samsung 5.0 Apple 1.0 Apple 7.0 samsung 3.0 asus 4.0 motorola 4.0 samsung 15.0 Apple 5.0 samsung 13.0 samsung 7.0 samsung 7.0 Apple 2.0 motorola 4.0 Apple 3.0 samsung 35.0 Apple 3.0 samsung 22.0 LGE 2.0 Xiaomi 41.0 Apple 4.0 Apple 9.0 OnePlus 2.0 asus 6.0 Apple 1.0 Apple 2.0 samsung 1.0 Apple 4.0 Apple 1.0 motorola 6.0 samsung 6.0 Xiaomi 1.0 samsung 3.0 Apple 1.0 asus 1.0 Apple 8.0 samsung 12.0 samsung 3.0 samsung 1.0 Apple 4.0 Apple 3.0 samsung 1.0 Xiaomi 40.0 Apple 7.0 Apple 14.0 asus 8.0 motorola 2.0 samsung 5.0 Apple 2.0 samsung 4.0 motorola 1.0 LGE 6.0 Apple 64.0 Apple 11.0 samsung 1.0 Apple 1.0 motorola 5.0 Xiaomi 4.0 samsung 3.0 samsung 1.0 samsung 12.0 Apple 5.0 samsung 1.0 samsung 7.0 Apple 2.0 samsung 1.0 samsung 7.0 Apple 3.0 motorola 5.0 samsung 3.0 samsung 3.0 samsung 5.0 samsung 3.0 Apple 6.0 Apple 11.0 Apple 27.0 motorola 6.0 Apple 4.0 Apple 1.0 samsung 6.0 motorola 2.0 samsung 3.0 Apple 2.0 motorola 6.0 samsung 4.0 Apple 1.0 Apple 1.0 samsung 9.0 samsung 7.0 motorola 8.0 samsung 3.0 motorola 5.0 motorola 2.0 asus 2.0 Apple 1.0 motorola 39.0 samsung 2.0 Apple 5.0 motorola 2.0 Apple 5.0 Apple 11.0 motorola 10.0 Apple 2.0 Apple 3.0 Apple 4.0 Xiaomi 7.0 asus 8.0 motorola 1.0 samsung 6.0 Xiaomi 3.0 samsung 4.0 Apple 14.0 samsung 2.0 Apple 8.0 Apple 3.0 Apple 3.0 Apple 3.0 samsung 2.0 samsung 4.0 Apple 3.0 Apple 11.0 Apple 7.0 samsung 3.0 samsung 1.0 motorola 24.0 Apple 13.0 Meizu 7.0 Apple 6.0 samsung 3.0 motorola 2.0 Apple 10.0 motorola 4.0 Apple 1.0 Xiaomi 1.0 Apple 2.0 LGE 5.7181703029111794 Apple 2.0 LGE 21.0 Xiaomi 4.0 Apple 4.0 samsung 9.0 Xiaomi 3.0 samsung 20.0 samsung 7.0 Xiaomi 5.0 Xiaomi 3.0 samsung 9.0 samsung 4.0 asus 1.0 Apple 8.0 Apple 11.0 samsung 7.0 Apple 1.0 samsung 14.0 samsung 2.0 Apple 2.0 Apple 11.0 motorola 2.0 samsung 2.0 LENOVO 4.0 samsung 6.0 samsung 3.0 motorola 7.0 motorola 8.0 Apple 3.0 Apple 2.0 samsung 7.0 Apple 2.0 asus 3.0 Apple 4.0 samsung 4.0 Apple 2.0 Apple 4.0 Apple 1.0 samsung 3.0 Apple 4.0 motorola 2.0 samsung 2.0 samsung 2.0 samsung 6.0 Xiaomi 4.0 samsung 6.0 samsung 3.0 samsung 1.0 Apple 3.0 Apple 2.0 asus 5.7181703029111794 Apple 3.0 Apple 30.0 samsung 9.0 samsung 3.0 motorola 1.0 samsung 19.0 motorola 9.0 motorola 1.0 motorola 3.0 Apple 1.0 motorola 4.0 samsung 4.0 Apple 20.0 asus 2.0 samsung 1.0 motorola 14.0 Apple 5.7181703029111794 Apple 3.0 Apple 1.0 asus 2.0 LGE 12.0 samsung 3.0 samsung 3.0 samsung 3.0 samsung 5.0 Apple 6.0 Apple 1.0 samsung 2.0 Apple 1.0 Apple 9.0 samsung 1.0 motorola 5.0 Apple 2.0 Apple 5.0 Apple 6.0 motorola 3.0 samsung 10.0 Apple 2

In [208]:
display(df_sessions_visits.select('device_manufacturer','sum_click_add_item'))

device_manufacturer sum_click_add_item Apple 1.0 Apple 1.0 Xiaomi 7.0 samsung 1.0 samsung 2.0 motorola 4.0 Apple 1.0 Apple 1.0 Apple 4.0 motorola 6.0 samsung 1.0 Apple 2.0 asus 2.0 motorola 7.0 Sony 2.0 Apple 2.0 samsung 1.0 Apple 1.0 asus 2.0 Apple 1.0 samsung 1.0 samsung 2.0 Apple 4.0 Xiaomi 2.0 Apple 1.0 Apple 1.0 motorola 1.0 samsung 4.0 samsung 3.0 samsung 1.0 samsung 2.0 Apple 2.0 LGE 3.0 samsung 1.0 samsung 4.0 Apple 4.0 Apple 3.0 Apple 4.0 samsung 2.0 Apple 8.0 Apple 4.0 Apple 1.0 Apple 0.0 samsung 2.930546642105701 Apple 2.0 samsung 1.0 Apple 2.0 Apple 1.0 Apple 2.0 Apple 1.0 Apple 1.0 samsung 4.0 Apple 10.0 motorola 2.0 Apple 1.0 samsung 3.0 motorola 3.0 motorola 1.0 Xiaomi 3.0 Apple 5.0 Apple 8.0 Apple 8.0 Apple 3.0 Apple 1.0 motorola 11.0 samsung 2.0 motorola 2.0 Apple 2.0 samsung 7.0 LGE 4.0 samsung 1.0 motorola 1.0 Apple 9.0 motorola 2.0 motorola 1.0 Apple 1.0 motorola 6.0 Apple 3.0 Apple 6.0 Apple 1.0 motorola 4.0 motorola 1.0 Xiaomi 6.0 samsung 2.0 Apple 3.0 Apple 2.0 asus 2.0 samsung 6.0 motorola 5.0 motorola 2.0 Apple 2.0 Apple 2.0 samsung 1.0 Apple 10.0 Xiaomi 9.0 samsung 2.0 motorola 1.0 motorola 4.0 Apple 1.0 Apple 2.0 samsung 3.0 motorola 10.0 motorola 2.0 samsung 2.0 samsung 1.0 Apple 2.0 samsung 8.0 Apple 3.0 Apple 2.0 samsung 2.930546642105701 Apple 3.0 samsung 1.0 Apple 1.0 Apple 6.0 samsung 4.0 motorola 5.0 Apple 1.0 samsung 5.0 motorola 2.0 Apple 3.0 Apple 6.0 Apple 3.0 samsung 3.0 Apple 1.0 Apple 3.0 samsung 1.0 asus 2.0 motorola 2.0 samsung 10.0 Apple 2.0 samsung 2.0 samsung 1.0 samsung 2.0 Apple 2.0 motorola 7.0 Apple 1.0 samsung 2.0 Apple 3.0 samsung 15.0 LGE 1.0 Xiaomi 44.0 Apple 3.0 Apple 5.0 OnePlus 1.0 asus 7.0 Apple 1.0 Apple 2.0 samsung 1.0 Apple 3.0 Apple 1.0 motorola 4.0 samsung 3.0 Xiaomi 1.0 samsung 2.0 Apple 1.0 asus 1.0 Apple 5.0 samsung 3.0 samsung 2.0 samsung 1.0 Apple 2.0 Apple 2.0 samsung 1.0 Xiaomi 2.0 Apple 2.0 Apple 3.0 asus 2.0 motorola 1.0 samsung 1.0 Apple 3.0 samsung 5.0 motorola 1.0 LGE 2.0 Apple 31.0 Apple 6.0 samsung 1.0 Apple 2.0 motorola 3.0 Xiaomi 5.0 samsung 1.0 samsung 1.0 samsung 3.0 Apple 3.0 samsung 1.0 samsung 1.0 Apple 1.0 samsung 1.0 samsung 2.0 Apple 3.0 motorola 1.0 samsung 2.0 samsung 1.0 samsung 2.0 samsung 2.0 Apple 2.0 Apple 5.0 Apple 12.0 motorola 1.0 Apple 3.0 Apple 1.0 samsung 2.0 motorola 4.0 samsung 2.0 Apple 1.0 motorola 2.0 samsung 2.0 Apple 1.0 Apple 1.0 samsung 3.0 samsung 1.0 motorola 1.0 samsung 4.0 motorola 1.0 motorola 2.0 asus 2.0 Apple 1.0 motorola 8.0 samsung 2.0 Apple 1.0 motorola 1.0 Apple 2.0 Apple 2.0 motorola 7.0 Apple 2.0 Apple 1.0 Apple 2.0 Xiaomi 1.0 asus 5.0 motorola 1.0 samsung 3.0 Xiaomi 1.0 samsung 2.0 Apple 2.0 samsung 1.0 Apple 1.0 Apple 3.0 Apple 3.0 Apple 1.0 samsung 2.0 samsung 4.0 Apple 1.0 Apple 4.0 Apple 3.0 samsung 3.0 samsung 1.0 motorola 3.0 Apple 5.0 Meizu 3.0 Apple 3.0 samsung 3.0 motorola 1.0 Apple 7.0 motorola 4.0 Apple 1.0 Xiaomi 1.0 Apple 2.0 LGE 2.930546642105701 Apple 3.0 LGE 2.0 Xiaomi 3.0 Apple 2.0 samsung 4.0 Xiaomi 2.0 samsung 5.0 samsung 9.0 Xiaomi 2.0 Xiaomi 1.0 samsung 8.0 samsung 2.0 asus 1.0 Apple 7.0 Apple 6.0 samsung 2.0 Apple 1.0 samsung 4.0 samsung 1.0 Apple 2.0 Apple 9.0 motorola 1.0 samsung 1.0 LENOVO 1.0 samsung 4.0 samsung 1.0 motorola 2.0 motorola 5.0 Apple 1.0 Apple 1.0 samsung 2.0 Apple 2.0 asus 3.0 Apple 3.0 samsung 2.0 Apple 5.0 Apple 4.0 Apple 1.0 samsung 3.0 Apple 1.0 motorola 1.0 samsung 2.0 samsung 1.0 samsung 1.0 Xiaomi 6.0 samsung 3.0 samsung 2.0 samsung 2.0 Apple 3.0 Apple 1.0 asus 2.930546642105701 Apple 4.0 Apple 4.0 samsung 4.0 samsung 3.0 motorola 1.0 samsung 2.0 motorola 4.0 motorola 1.0 motorola 2.0 Apple 1.0 motorola 3.0 samsung 1.0 Apple 6.0 asus 2.0 samsung 1.0 motorola 9.0 Apple 2.930546642105701 Apple 2.0 Apple 1.0 asus 1.0 LGE 1.0 samsung 2.0 samsung 2.0 samsung 1.0 samsung 1.0 Apple 3.0 Apple 2.0 samsung 1.0 Apple 1.0 Apple 4.0 samsung 1.0 motorola 2.0 Apple 2.0 Apple 2.0 Apple 1.0 motorola 2.0 samsung 1.0 Apple 2.0 motorola 2.0 Apple 5.0 samsung 1.0 Apple 5.0 Apple

In [209]:
display(df_sessions_visits.select('device_manufacturer','sum_event_open'))

device_manufacturer sum_event_open Apple 1.0 Apple 17.0 Xiaomi 2.0 samsung 11.0 samsung 4.0 motorola 5.0 Apple 2.0 Apple 3.0 Apple 9.0 motorola 9.0 samsung 4.0 Apple 3.0 asus 4.0 motorola 9.0 Sony 10.0 Apple 1.0 samsung 19.0 Apple 2.0 asus 1.0 Apple 2.0 samsung 1.0 samsung 2.0 Apple 10.0 Xiaomi 2.0 Apple 5.0 Apple 4.0 motorola 7.0 samsung 5.0 samsung 4.0 samsung 10.0 samsung 1.0 Apple 8.0 LGE 13.0 samsung 9.0 samsung 4.0 Apple 1.0 Apple 5.0 Apple 3.0 samsung 10.0 Apple 4.0 Apple 20.0 Apple 5.0 Apple 1.0 samsung 1.0 Apple 3.0 samsung 2.0 Apple 9.0 Apple 3.0 Apple 2.0 Apple 23.0 Apple 3.0 samsung 8.0 Apple 19.0 motorola 5.0 Apple 2.0 samsung 4.0 motorola 2.0 motorola 3.0 Xiaomi 4.0 Apple 7.0 Apple 7.0 Apple 7.0 Apple 7.0 Apple 3.0 motorola 10.0 samsung 4.0 motorola 3.0 Apple 1.0 samsung 7.0 LGE 3.0 samsung 1.0 motorola 8.0 Apple 5.0 motorola 3.0 motorola 8.0 Apple 12.0 motorola 7.0 Apple 1.0 Apple 4.0 Apple 4.0 motorola 7.0 motorola 8.0 Xiaomi 9.0 samsung 4.0 Apple 2.0 Apple 13.0 asus 2.0 samsung 10.0 motorola 10.0 motorola 2.0 Apple 3.0 Apple 2.0 samsung 1.0 Apple 21.0 Xiaomi 7.0 samsung 3.0 motorola 5.0 motorola 8.0 Apple 3.0 Apple 6.0 samsung 7.0 motorola 2.0 motorola 3.0 samsung 2.0 samsung 9.0 Apple 2.0 samsung 6.0 Apple 2.0 Apple 6.0 samsung 6.0 Apple 3.0 samsung 2.0 Apple 4.0 Apple 9.0 samsung 3.0 motorola 16.0 Apple 4.0 samsung 16.0 motorola 3.0 Apple 2.0 Apple 5.0 Apple 10.0 samsung 7.0 Apple 2.0 Apple 8.0 samsung 1.0 asus 5.0 motorola 5.0 samsung 10.0 Apple 7.0 samsung 3.0 samsung 1.0 samsung 2.0 Apple 3.0 motorola 20.0 Apple 2.0 samsung 5.0 Apple 2.0 samsung 17.0 LGE 6.0 Xiaomi 10.0 Apple 6.0 Apple 11.0 OnePlus 4.0 asus 7.0 Apple 8.0 Apple 2.0 samsung 1.0 Apple 2.0 Apple 5.0 motorola 8.0 samsung 6.0 Xiaomi 4.0 samsung 6.0 Apple 2.0 asus 8.0 Apple 4.0 samsung 4.0 samsung 1.0 samsung 1.0 Apple 6.0 Apple 4.0 samsung 6.0 Xiaomi 7.0 Apple 10.0 Apple 2.0 asus 4.0 motorola 4.0 samsung 8.0 Apple 2.0 samsung 3.0 motorola 7.0 LGE 5.0 Apple 13.0 Apple 2.0 samsung 5.0 Apple 5.0 motorola 6.0 Xiaomi 3.0 samsung 1.0 samsung 1.0 samsung 8.0 Apple 1.0 samsung 2.0 samsung 8.0 Apple 2.0 samsung 6.0 samsung 9.0 Apple 2.0 motorola 3.0 samsung 11.0 samsung 9.0 samsung 7.0 samsung 10.0 Apple 4.0 Apple 9.0 Apple 10.0 motorola 10.0 Apple 6.0 Apple 1.0 samsung 4.0 motorola 8.0 samsung 3.0 Apple 5.0 motorola 5.0 samsung 1.0 Apple 4.0 Apple 3.0 samsung 2.0 samsung 12.0 motorola 5.0 samsung 3.0 motorola 5.0 motorola 9.0 asus 3.0 Apple 3.0 motorola 5.0 samsung 4.0 Apple 8.0 motorola 3.0 Apple 1.0 Apple 3.0 motorola 3.0 Apple 4.0 Apple 1.0 Apple 18.0 Xiaomi 5.0 asus 15.0 motorola 8.0 samsung 17.0 Xiaomi 7.0 samsung 4.0 Apple 8.0 samsung 3.0 Apple 1.0 Apple 4.0 Apple 2.0 Apple 5.0 samsung 24.0 samsung 13.0 Apple 2.0 Apple 10.0 Apple 4.0 samsung 19.0 samsung 1.0 motorola 4.0 Apple 5.0 Meizu 3.0 Apple 2.0 samsung 1.0 motorola 12.0 Apple 14.0 motorola 3.0 Apple 2.0 Xiaomi 1.0 Apple 6.0 LGE 2.0 Apple 4.0 LGE 8.0 Xiaomi 5.0 Apple 2.0 samsung 9.0 Xiaomi 13.0 samsung 17.0 samsung 9.0 Xiaomi 8.0 Xiaomi 6.0 samsung 19.0 samsung 14.0 asus 15.0 Apple 4.0 Apple 4.0 samsung 20.0 Apple 5.0 samsung 17.0 samsung 2.0 Apple 2.0 Apple 1.0 motorola 10.0 samsung 9.0 LENOVO 8.0 samsung 3.0 samsung 2.0 motorola 7.0 motorola 2.0 Apple 1.0 Apple 1.0 samsung 2.0 Apple 5.0 asus 13.0 Apple 3.0 samsung 2.0 Apple 2.0 Apple 3.0 Apple 4.0 samsung 3.0 Apple 4.0 motorola 1.0 samsung 4.0 samsung 3.0 samsung 10.0 Xiaomi 3.0 samsung 6.0 samsung 4.0 samsung 2.0 Apple 2.0 Apple 1.0 asus 7.0 Apple 7.0 Apple 18.0 samsung 14.0 samsung 15.0 motorola 2.0 samsung 8.0 motorola 6.0 motorola 16.0 motorola 10.0 Apple 2.0 motorola 2.0 samsung 2.0 Apple 1.0 asus 4.0 samsung 1.0 motorola 6.0 Apple 1.0 Apple 2.0 Apple 4.0 asus 6.0 LGE 5.0 samsung 1.0 samsung 4.0 samsung 3.0 samsung 2.0 Apple 2.0 Apple 4.0 samsung 5.0 Apple 10.0 Apple 12.0 samsung 1.0 motorola 4.0 Apple 4.0 Apple 4.0 Apple 11.0 motorola 1.0 samsung 6.0 Apple 4.0 motorola 1.0 Apple 12.0 samsung 6.0 Apple 3.0 Apple 7.0 Apple 4.0 samsung 

#### Estatísticas básicas

In [211]:
# Estatistica basica variaveis quantitativas
aux = []
for nome, tipo in df_sessions_visits.dtypes:
  if tipo in ('double', 'int'):
    aux.append(nome)
    
display(df_sessions_visits[aux].describe())

summary session_duration_seconds sum_event_open sum_view_restaurant_screen sum_view_dish_screen sum_click_add_item sum_view_checkout sum_callback_purchase order_session_quantity session_started_month session_started_dayofweek count 463620 463620 463620 463620 463620 463620 463620 463620 463620 463620 mean 2658.8750712286133 6.091563608433379 8.933784760327478 5.7181703029112825 2.9305466421051785 4.208141738593542 1.248587399517117 1.153414442445203 8.860057805961778 4.089010396445365 stddev 20539.091757625276 6.247750152218677 13.354595274020154 6.768130251305075 3.909645017613745 6.531655744351323 2.24089780822729 2.0707662087639336 2.043890271557854 2.1076238048712965 min -93.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 5 1 max 2575751.0 631.0 1086.0 409.0 708.0 800.0 359.0 311.0 12 7

In [212]:
display(df_sessions_visits[aux].summary())

summary session_duration_seconds sum_event_open sum_view_restaurant_screen sum_view_dish_screen sum_click_add_item sum_view_checkout sum_callback_purchase order_session_quantity session_started_month session_started_dayofweek count 463620 463620 463620 463620 463620 463620 463620 463620 463620 463620 mean 2658.8750712286133 6.091563608433379 8.933784760327478 5.7181703029112825 2.9305466421051785 4.208141738593542 1.248587399517117 1.153414442445203 8.860057805961778 4.089010396445365 stddev 20539.091757625276 6.247750152218677 13.354595274020154 6.768130251305075 3.909645017613745 6.531655744351323 2.24089780822729 2.0707662087639336 2.043890271557854 2.1076238048712965 min -93.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 5 1 25% 672.0 2.0 2.0 2.0 1.0 1.0 1.0 1.0 7 2 50% 1800.0 4.0 5.0 4.0 2.0 3.0 1.0 1.0 9 4 75% 3144.0 8.0 10.0 7.0 3.0 5.0 1.0 1.0 11 6 max 2575751.0 631.0 1086.0 409.0 708.0 800.0 359.0 311.0 12 7